Point72 MI Data - Analytics Case Study:
<br>
*	You are given two types of data: 311 Service requests, and weather. The 311 Service requests dataset contains all the 311 calls from 2016 to 2018 with many different features including timestamps, location, service request descriptions, etc.
*   Please describe the steps you take to ingest and process the data, what are the challenges and how you overcome them.
*	Aggregate the 311 records in ways that best describes the characteristics of the inbound call patterns. Explain and visualize your findings. What are the implications you can infer from the patterns?
*	The weather data contains the weather information from the weather stations in NYC from 2010 to 2018 in daily intervals. Describe and visualize your findings. (Please note this is NOT weather forecast)
*	The final goal of this project is to predict the daily 311 inbound calls for the next 7 days 
    *	Use your insights from previous sections to build a predictive model of your choice – explain the assumptions of your model and why you picked it.
    *	What features are you using in your model and, how does your data exploration process help you decide which features you are incorporating in your model?
    *	Evaluate the impact of weather on the call volume, find patterns and define causal impact if there’s any. 
    *	Build a reasonable model framework, explain your model results, and justify the relationships identified in the model. Not necessary to dig into complex models.


In [ ]:
%matplotlib inline

In [ ]:
import pandas as pd
import polars as pl
import numpy as np
import seaborn as sns
from matplotlib import pyplot as plt
from collections import defaultdict
import sklearn
import gradio as gr
import gc
from IPython.display import display, HTML
import plotly.figure_factory as ff
import plotly.express as px
import plotly
import json
import folium
import xgboost as xgb
from xgboost import plot_importance
from scipy.stats import entropy
from sklearn.impute import SimpleImputer
from bertopic import BERTopic
import json
pl.Config.set_tbl_width_chars(200)
pl.Config.set_fmt_str_lengths(100)
pl.Config.set_tbl_rows(10)

# Custom Functions
from utils import map_vals, agg_and_merge_historical
from utils import create_datetime, build_temporal_features
from utils import MyNaiveImputer, get_feature_importance

# seaborn Color Palette
color_pal = sns.color_palette("tab10")

# 1. Data Preprocessing

In [ ]:
# Load Weather Data in pandas
# No need for polars because data is sufficiently small
weather_data = pd.read_csv("data/weather_NY_2010_2018Nov.csv")

# Load Service data in polars for speed optimization
# Loading directly with polars leads to errors
# Load in pandas then convert to polars
service_data_pd = pd.read_csv("data/311-2016-2018.csv")
assert service_data_pd["Unique Key"].nunique() == len(service_data_pd)
# This casting is done just because of some errors when loading pl from pandas
service_data_pd["Incident Zip"] = service_data_pd["Incident Zip"].astype("string")
service_data_pd["BBL"] = service_data_pd["BBL"].astype("string")
service_data = pl.DataFrame(service_data_pd)

# Clear some ram
del service_data_pd
gc.collect()

## Initial Data Discovery

Before performing a more in depth EDA, I look at the high level features of each dataset.<br><br>
**Key takeaways:**
* mismatch in Location: Weather data covers the whole state of NY, 311 calls focus only on Manhatten
* mismatch in Dates: Weather data cuts off in November and 311 call data needs to be aggregated

### Service Data

#### NAN values

In [ ]:
service_data.null_count().transpose(include_header=True)

#### Date

In [ ]:
# This function builds the temporal features
# CAN UNCOMMENT

# from utils import build_temporal_features
# service_data = create_datetime(service_data, "Created Date")
# service_data = build_temporal_features(service_data, "Created Date")

#### Location by Year

In [ ]:
# # VIEW MAP ON GRADIO APPLICATION OR UNCOMMENT

# fig = folium.Figure(height=500, width=750)
# map_nyc = folium.Map(location=[40.7128, -74.0060], zoom_start=10, tiles='cartodbpositron',)
# year_cm = {2016: "red", 2017: "blue", 2018: "green"}
# for row in service_data[:, ["Latitude", "Longitude", "Year"]].drop_nulls().sample(10000).rows():
#     lat, long, year = row[0], row[1], row[2]
#     folium.CircleMarker(location=[lat, long], radius=1, weight=3, color=year_cm[int(year)]).add_to(map_nyc)

# fig.add_child(map_nyc)
# fig

### Weather Data

#### NAN values

In [ ]:
weather_data.isna().sum()

#### Date

In [ ]:
# Quickly aggregate Year, Month, Day into a datetime object
# This is because the 311 data uses datetime
weather_data["Datetime"] = weather_data["Year"].astype("str") + "-" + weather_data["Month"].astype("str") + "-" + weather_data["Day"].astype("str")
weather_data["Datetime"] = pd.to_datetime(weather_data["Datetime"], format="%Y-%m-%d")
# weather_data = build_temporal_features(weather_data, "Datetime")

The important takeaway here is to notice that we have 29 days missing from the original data for 2018

In [ ]:
days_missing = (pd.to_datetime(service_data["Created Date"].max()) - weather_data["Datetime"].max()).days
print(f"Total Days Missing: {days_missing} days")

#### Location

The weather data covers a wider area than the service data.

In [ ]:
# VIEW MAP ON GRADIO APPLICATION OR UNCOMMENT

# fig, weather_map = map_vals(weather_data.loc[weather_data["Year"] >= 2016], cols=["Latitude", "Longitude"], label_cols=["StationName"], color='red', radius=3, weight=4)
# fig, combined_map = map_vals(service_data, cols=["Latitude", "Longitude"], color="blue", submap=weather_map, weight=2, radius=1)
# fig

In [ ]:
# VIEW MAP ON GRADIO APPLICATION OR UNCOMMENT

# fig, service_map = map_vals(service_data, cols=["Latitude", "Longitude"], color="blue", weight=2, radius=1, start_loc=[40.7128, -74.0060], zoom_start=10)
# fig, weather_map = map_vals(weather_data.loc[weather_data["Year"] >= 2016], cols=["Latitude", "Longitude"], submap=service_map, label_cols=["StationName"], color='red', radius=5, weight=2)
# fig

Location plays a factor into how we aggregate the data. Additionally, we dont have as granular weather data as we do service data

1. First We need to aggregate the weather features by Time and Location.
2. We choose which variables to combine with the 311 Data

To aggregate by location we can essentially create a bounding box of points, only choosing the ones that fall within our box.

In [ ]:
# VIEW MAP ON GRADIO APPLICATION OR UNCOMMENT

# lat_min = service_data["Latitude"].min()
# lat_max = service_data["Latitude"].max()
# long_min = service_data["Longitude"].min()
# long_max = service_data["Longitude"].max()

# fig = folium.Figure(height=500, width=750)
# service_bounds_map = folium.Map(location=[40.7128, -74.0060], zoom_start=10, tiles='cartodbpositron',)

# kw = {
#     "color": "#F1807E",
#     "line_cap": "round",
#     "fill": True,
#     "fill_color": "blue",
#     "weight": 3,
#     "popup": "Service Data Coverage Zone",
# }

# folium.Rectangle(
#     bounds=[[lat_min, long_min], [lat_max, long_max]],
#     line_join="round",
#     dash_array="5 5",
#     **kw,
# ).add_to(service_bounds_map)

# fig.add_child(service_bounds_map)
# fig

In [ ]:
# VIEW MAP ON GRADIO APPLICATION OR UNCOMMENT

# mincon_lat = weather_data["Latitude"] >= lat_min
# maxcon_lat = weather_data["Latitude"] <= lat_max
# mincon_long = weather_data["Longitude"] >= long_min
# maxcon_long = weather_data["Longitude"] <= long_max

# wd_localized = weather_data.loc[mincon_lat & maxcon_lat & mincon_long & maxcon_long]
# fig, wd_local_map = map_vals(wd_localized, submap=service_bounds_map, label_cols=["StationName"], color='red', radius=5, weight=2)
# fig

## Weather Data


### Filter & Aggregate

Two Steps:
1. Filter the Weather data to only cover the same area as the 311 service data
2. Aggregate across each day

<br>**Filter by Location:**<br>
* It is possible to further aggregate by location based on the 311 call source. (i.e. finding data based on datapoints with minimal distance)
    * This may be added in future revisions but for now, I will assume weather in this general area will be relatively similar
    * To aggregate across areas, I am going to simply find the mean for each timestep following the assumption above
    * There are also only at most 5 datapoints per timestamp, so mean should be the least lossy operation to use.

Some of these columns we can drop arbitrarily as they are not aggregatable and most likely not useful.<br>
Most of the categorical columns are either redundant (like State) or just not useful. USAF and WBAN seem to be IDs for specific departments, most likely linked to StationName.<br>

In [ ]:
# Quickly aggregate Year, Month, Day into a datetime object
# This is because the 311 data uses datetime
weather_data["Datetime"] = weather_data["Year"].astype("str") + "-" + weather_data["Month"].astype("str") + "-" + weather_data["Day"].astype("str")
weather_data = create_datetime(weather_data, "Datetime", format="%Y-%m-%d")

lat_min = service_data["Latitude"].min()
lat_max = service_data["Latitude"].max()
long_min = service_data["Longitude"].min()
long_max = service_data["Longitude"].max()

mincon_lat = weather_data["Latitude"] >= lat_min
maxcon_lat = weather_data["Latitude"] <= lat_max
mincon_long = weather_data["Longitude"] >= long_min
maxcon_long = weather_data["Longitude"] <= long_max

wd_localized = weather_data.loc[mincon_lat & maxcon_lat & mincon_long & maxcon_long]

drop_cols = [
    "USAF",
    "WBAN",
    "StationName",
    "State",
    "Latitude",
    "Longitude"
]
wd_localized = wd_localized.drop(columns=drop_cols)
# wd_localized.to_csv("data/weather_2016_2018_localized.csv")

**Aggregation:**
* We've removed all locational data, now we need to group by the date
* To be a little more concise in our aggregation I propose 4 categories:
    * Mean Cols: These values can naturally be meaned
    * Min Cols: MinTemp as its already a min value
    * Max Cols: MaxTemp and MaxSustainedWind - already a max value
    * round_cols: For binary variables (mean is done first to replicate a percentage, then rounded to get binary)

In [ ]:
mean_cols = [
    'MeanTemp',
    'DewPoint',
    'Percipitation',
    'WindSpeed',
    'Gust',
    'SnowDepth',
]
min_cols = [
    'MinTemp'
]
max_cols = [
    'MaxTemp',
    'MaxSustainedWind'
]
round_cols = [
    'Rain',
    'SnowIce'
]

mean_df = wd_localized.groupby("Datetime")[mean_cols].mean()
min_df = wd_localized.groupby("Datetime")[min_cols].min()
max_df = wd_localized.groupby("Datetime")[max_cols].max()
round_df = wd_localized.groupby("Datetime")[round_cols].mean().round().astype(np.int8)
wd_full = pd.concat([mean_df, min_df, max_df, round_df], axis=1)
wd_full = build_temporal_features(wd_full, "Datetime")
wd_full["Season"] = wd_full["Season"].astype("category")
wd_full = wd_full.set_index("Datetime")

wd_hist = wd_full.loc[wd_full["Year"] < 2016]
wd_curr = wd_full.loc[wd_full["Year"] >= 2016]

# wd_full.tail()
# wd_full.to_csv("Weather_Aggregated_Full.csv")

### Impute Missing Data



These are the columns we need to impute

In [ ]:
impute_cols = [
    'MeanTemp', 'MinTemp', 'MaxTemp', 'DewPoint',
    'Percipitation', 'WindSpeed', 'MaxSustainedWind',
    'Gust', 'Rain', 'SnowDepth', 'SnowIce',
]

According to our analysis, we are missing 49 days of weather data. We need to impute this data before we merge the datasets.

In [ ]:
days_missing = (pd.to_datetime("12-31-2018") - wd_curr.index.max()).days
print(f"Total Days Missing: {days_missing} days")

Before imputing (or really just forecasting) these values, note that the goal of the project is to forecast the call volume in the next 7 days for the 311 data. To do this it may be useful to actually forecast the weather values for the 7 days after December 31, 2018. That way we can include more features in our final model.

For now lets plot the current figure for MeanTemp<br><br>
**NOTE: If you do not have the right plotly and jupyterlab versions installed in the kernel running jupyter, plots may not render. Refer to the EDA Tab in the Gradio section to see this graph.**

In [ ]:
from utils import plot_timeseries
fig = plot_timeseries(wd_full, "MeanTemp")
fig

#### Naive Imputation

In [ ]:
from utils import MyNaiveImputer

my_imputer = MyNaiveImputer(wd_full, time_steps=days_missing+7)
imputers = {
    "Mean": my_imputer.impute_all(impute_cols, strategy="mean"),
    "Median": my_imputer.impute_all(impute_cols, strategy="median"),
    "Max": my_imputer.impute_all(impute_cols, strategy="max"),
    "Min": my_imputer.impute_all(impute_cols, strategy="min")
}

In [ ]:
col = "MeanTemp"
plt.figure(figsize=(15,5))
plt.plot(wd_full.index[-400:], wd_full[col][-400:], label="Actual")
for method in ["Mean", "Max", "Min"]:
    plt.plot(imputers[method]["Datetime"], imputers[method][col], label=method)

plt.legend()

#### Robust Imputation (Unused)

For robust imputation, we would need to build a model to forecast each column. The problem would essentially shift from a univariate time forecast, to a multivariate time forecast. These two processes are extremely different as they require a special kind of models to predict. Based on the directions in the case study, I am going to shy away from creating a weather forecast. However, I provide one helper function below that I would use as an initial start to implementing this imputation method.

This function fits an XGBoost model on the data and outputs the feature importance graph. Theoretically I would use this feature importance graph to help me determine the feature interactions in the multivariate forecast. Again, if the task were to create a multivariate forecast, I would definitely pursue this path as it is much more robust than the simple method above. I may attempt to revisit this later in the study.

In [ ]:
from utils import get_feature_importance

fig, model = get_feature_importance(wd_full, "MeanTemp")

#### Decision

Based on some logic and the graphs above, each variable will use its own imputation method. The mapping of methods is shown below and the reasoning can be seen in the [gradio application](https://dna-casestudy.com/).

We will use the simple imputation method to fill these missing values. Additionally, rather than just imputing the missing days, we will also impute the next 7 days to match with the 7 day forecast of 311 Service calls. <br> 
This is so we can now treat this variable as a future covariate (in other words a weather forecast). Even though the instructions say this is not a weather forecast problem, this simple imputation is not computationally expensive.<br>
Although lacking in robustness, it can serve as an alternative to a forecast and we can use this variable without inherent lags.

In [ ]:
from utils import impute_missing_weather

def impute_all_data(data):
    # We will calculate the imputation for the next 7 days after 12/31/2018
    # This will act as our "Weather Forecast"
    time_steps = 49 + 7
    
    # Impute Cols
    impute_cols = [
        'MeanTemp', 'MinTemp', 'MaxTemp', 'DewPoint',
        'Percipitation', 'WindSpeed', 'MaxSustainedWind',
        'Gust', 'Rain', 'SnowDepth', 'SnowIce',
    ]
    
    # Mean Vars
    mean_vars = ["WindSpeed", "MaxSustainedWind", "Gust", "SnowDepth"]
    min_vars = ["SnowIce", "MeanTemp", "MinTemp", "MaxTemp", "DewPoint", "Percipitation"]
    max_vars = ["Rain"]
    
    # Use the imported function to create the imputed data
    preds_mean = impute_missing_weather(data, strategy="mean", time_steps=time_steps, impute_cols=mean_vars)
    preds_min = impute_missing_weather(data, strategy="min", time_steps=time_steps, impute_cols=min_vars)
    preds_max = impute_missing_weather(data, strategy="max", time_steps=time_steps, impute_cols=max_vars)
    all_preds = pd.concat([preds_mean, preds_min, preds_max], axis=1).loc[:, impute_cols]
    all_preds = build_temporal_features(all_preds, "Datetime").set_index("Datetime")
    
    wd_df = pd.concat([data, all_preds], axis=0)
    # Only take dates past 2016
    wd_df = wd_df.loc[wd_df["Year"] >= 2016]

    return wd_df

# wd_df = impute_all_data(wd_full)

## One Call to Build Them All (Weather)

In [ ]:
# Build all weather data from file
def build_weather_data(filename):
    # Use pandas to read file
    weather_data = pd.read_csv(filename)
    
    # Quickly aggregate Year, Month, Day into a datetime object
    # This is because the 311 data uses datetime
    weather_data["Datetime"] = weather_data["Year"].astype("str") + "-" + weather_data["Month"].astype("str") + "-" + weather_data["Day"].astype("str")
    weather_data = create_datetime(weather_data, "Datetime", format="%Y-%m-%d")

    # LOCALIZE
    # Pre-recorded min/max values from the service data (so we don't need again)
    lat_min = 40.49804421521046
    lat_max = 40.91294056699566
    long_min = -74.25521082506387
    long_max = -73.70038354802529

    # Create the conditions for location matching
    mincon_lat = weather_data["Latitude"] >= lat_min
    maxcon_lat = weather_data["Latitude"] <= lat_max
    mincon_long = weather_data["Longitude"] >= long_min
    maxcon_long = weather_data["Longitude"] <= long_max

    # Localize our data to match the service data
    wd_localized = weather_data.loc[mincon_lat & maxcon_lat & mincon_long & maxcon_long]
    drop_cols = [
        "USAF",
        "WBAN",
        "StationName",
        "State",
        "Latitude",
        "Longitude"
    ]
    wd_localized = wd_localized.drop(columns=drop_cols)

    # AGGREGATE
    # Map columns with aggregation method
    mean_cols = [
        'MeanTemp',
        'DewPoint',
        'Percipitation',
        'WindSpeed',
        'Gust',
        'SnowDepth',
    ]
    min_cols = [
        'MinTemp'
    ]
    max_cols = [
        'MaxTemp',
        'MaxSustainedWind'
    ]
    round_cols = [
        'Rain',
        'SnowIce'
    ]

    # Perform Aggregation
    mean_df = wd_localized.groupby("Datetime")[mean_cols].mean()
    min_df = wd_localized.groupby("Datetime")[min_cols].min()
    max_df = wd_localized.groupby("Datetime")[max_cols].max()
    round_df = wd_localized.groupby("Datetime")[round_cols].mean().round().astype(np.int8)
    wd_full = pd.concat([mean_df, min_df, max_df, round_df], axis=1)

    # Add seasonal features
    wd_full = build_temporal_features(wd_full, "Datetime")
    wd_full["Season"] = wd_full["Season"].astype("category")
    wd_full = wd_full.set_index("Datetime")
    
    # We will calculate the imputation for the next 7 days after 12/31/2018
    # Along with the 49 missing days
    # This will act as our "Weather Forecast"
    time_steps = 49 + 7
    
    # Impute Cols
    impute_cols = [
        'MeanTemp', 'MinTemp', 'MaxTemp', 'DewPoint',
        'Percipitation', 'WindSpeed', 'MaxSustainedWind',
        'Gust', 'Rain', 'SnowDepth', 'SnowIce',
    ]
    
    # Mean Vars
    mean_vars = ["WindSpeed", "MaxSustainedWind", "Gust", "SnowDepth"]
    min_vars = ["SnowIce", "MeanTemp", "MinTemp", "MaxTemp", "DewPoint", "Percipitation"]
    max_vars = ["Rain"]
    
    # Use the imported function to create the imputed data
    preds_mean = impute_missing_weather(wd_full, strategy="mean", time_steps=time_steps, impute_cols=mean_vars)
    preds_min = impute_missing_weather(wd_full, strategy="min", time_steps=time_steps, impute_cols=min_vars)
    preds_max = impute_missing_weather(wd_full, strategy="max", time_steps=time_steps, impute_cols=max_vars)
    all_preds = pd.concat([preds_mean, preds_min, preds_max], axis=1)
    all_preds = build_temporal_features(all_preds.loc[:, impute_cols], "Datetime")
    all_preds = all_preds.set_index("Datetime")

    wd_curr = wd_full.loc[wd_full["Year"] >= 2016]
    wd_df = pd.concat([wd_full, all_preds], axis=0, join="outer")

    return wd_df

## 311 Service Data

### Variables to Drop

**Variables to Exclude:**<br>
1) Unique Key: This is just a unique identifier label. Can be removed because it just matches to each distinct case, which is simply a row
3) Agency Name: Most likely correlated with Agency (which will be kept)
4) Location Type: Many distinct categories (161), high number of missing values (22.3%)
5) Incident Zip & Name, City, Address, Street Name, Cross Street 1 & 2, Intersection Street 1 & 2: All these location variables are captured by the Long/Lat
6) Address Type: Highly imbalanced, information seems not to useful
7) Landmark: High number of missing (99.9%)
8) Facility Type: High number of missing (68.4%)
9) Status: Most status categories are closed (>90%). Irrelevant to forecasting (assumes a case already exists)
10) Due Date: Irrelevant to forecasting (assumes a case already exists)
11) Resolution Description, Action Updated Date: Irrelevant to forecasting (assumes a case already exists)
12) Community Board: Correlates highly with Burough. Keep Burough remove Community board.
13) BBL (Burough Block Lot): High number of categories, correlated with Burough
14) X & Y Coordinate (State Plane): Correlated with Latitude Longitude
13) Park Facility Name: 97.2% of values are Unspecified. Too many distinct categories (1000+)
14) Park Borough: Correlates with Borough
15) Vehicle Type, Taxi Company Borough, Taxi Pick Up Location: 99% Missing
16) Bridge Highway * Variables, Bridge Highway, Road Ramp: 99% Missing
17) Latitude, Longitude, Location: Will keep as placeholder, but won't be used in model. Other variables provide better description of location (such as Burough)
17) Created Year: Inferred from created date

In [ ]:
drop_cols = [
    "Unique Key",
    "Agency Name",
    "Location Type",
    "Incident Zip",
    "Incident Address",
    "Street Name",
    "Cross Street 1",
    "Cross Street 2",
    "Intersection Street 1",
    "Intersection Street 2",
    "Address Type",
    "City",
    "Landmark",
    "Facility Type",
    "Status",
    "Due Date",
    "Resolution Description",
    "Resolution Action Updated Date",
    "Community Board",
    "BBL",
    "X Coordinate (State Plane)",
    "Y Coordinate (State Plane)",
    "Open Data Channel Type",
    "Park Facility Name",
    "Park Borough",
    "Vehicle Type",
    "Taxi Company Borough",
    "Taxi Pick Up Location",
    "Bridge Highway Name",
    "Bridge Highway Direction",
    "Road Ramp",
    "Bridge Highway Segment",
    "Location",
    "Created Year"
]

FEATURES = {
    "num": ["Target", "num_closed_tickets"],
    "cat": ["Agency", "Complaint Type", "Descriptor", "Borough"],
    "time": ["Year", "Month", "Day", "DayOfWeek", "DayOfYear", "is_weekend", "is_holiday", "Season"]
}

service_data = service_data.drop(drop_cols)
service_data = create_datetime(service_data, "Created Date")

sd_grouped = service_data.rename({"Created Date": "Datetime"}).group_by("Datetime").agg(
    pl.len().alias("Target"),

    # Categorical Features Will be added separately
    # pl.col("Agency").implode().flatten(),
    # pl.col("Complaint Type").implode().flatten(),
    # pl.col("Descriptor").implode().flatten(),
    # pl.col("Borough").implode().flatten(),

    # # Location Removed - Borough better explanation of location
    # pl.col("Latitude").mean(),
    # pl.col("Longitude").mean(),
).sort(by="Datetime")

I will create two sets of new features in our Service Dataset.
1. Num_closed_tickets: Use the closed date to find the number of closed tickets by day
2. Categorical Features: We will use categorical features to find the number of open tickets by category by day

### Number of Closed Tickets

Looking at the closed date variable, there are noticeably many different errors. For instance look at the query below. You can see there are potential typos. Mainly, why is there a closed date for 1900. This does not make sense.<br>

**NOTE: You may presume that the error shown below may be from incorrect date parsing. But, let it be known I looked at both the raw string and the parsed date variable. The error is replicated in both the raw and formatted column**

In [ ]:
service_data = create_datetime(service_data, "Closed Date")
service_data.sort("Closed Date")["Closed Date"].value_counts()

Another error with this data is that there are some records with null values and some records where the closed date is less than the created date. The latter of the two logically doesn't make sense. It is most likely either a typo again or an error in the data processing.

In [ ]:
number_of_point_errors = len(service_data.filter(
    (pl.col("Created Date") - pl.col("Closed Date")  > pl.duration(days=1))
))
number_of_null_errors = service_data.sort("Closed Date")["Closed Date"].value_counts()[0]["count"][0]
print(f"Number of records where the Closed date is before the created date: {number_of_point_errors} records")
print(f"Number of null records: {number_of_null_errors} records")
print(f"Errors / Total records: {(number_of_null_errors+number_of_point_errors)/len(service_data)}")

**Problem:** Typos in the data and null values.<br>

**My Solution**: For typos related to dates past the 2018 window. These datapoints will be filtered out from the data. Because of the unreliability of this datapoint in particular, I am hesitant to use this as a future covariate, where I would be obliged to use datapoints outside the 2018 window. Instead, I will take a safer approach and just treat it like a past covariate. So I will only be focused on data before 2018 window. For the case of null values and when the closed date < created date, I will impute values for those columns. The imputation value will be the mean of the time difference between the created and closed dates. Given these errors only account for 2% of the total data (seen above), I believe it is safe to impute naively like this.

In [ ]:
mean_diff = service_data.with_columns(
    diff_created_closed = pl.col("Closed Date") - pl.col("Created Date")
).filter((pl.col("Closed Date").dt.year() >= 2016) & (pl.col("Closed Date").dt.year() < 2020))["diff_created_closed"].mean().days
print(f"Mean Time Diff: {mean_diff} days")

Solution Code: Fill null with mean diff and fill bad condition with mean diff

In [ ]:
service_data = service_data.with_columns(
    Closed_Date_New = pl.when(pl.col("Created Date") - pl.col("Closed Date")  > pl.duration(days=1))
                        .then(pl.col("Created Date") + pl.duration(days=mean_diff))
                        .otherwise(pl.col("Closed Date")).fill_null(pl.col("Created Date") + pl.duration(days=mean_diff))
)

# Check for no null values
assert service_data["Closed_Date_New"].is_null().sum() == 0

Below is the final aggregation code for the num_closed tickets by date. We will do some feature engineering in a later step.

To prevent Data Leakage where future data is leaked into past data. We need to perform two group by steps. The purpose of the first step is to make sure we only sum tickets that were created on either the same or previous day relative to the listed closed date; the second performs the grouped summation by closed date. This is a little messy but the basic point is, because there is variability in the difference between closed and created date, doing a one-step summation by closed date would lead to leakage.

In [ ]:
closed_tickets = service_data.group_by(["Closed_Date_New", "Created Date"]) \
.agg((pl.when(pl.col("Created Date") <= pl.col("Closed_Date_New")).then(1).otherwise(0)).sum().alias("count")) \
.sort("Closed_Date_New") \
.filter((pl.col("Closed_Date_New").dt.year() >= 2016) & (pl.col("Closed_Date_New").dt.year() < 2019)) \
.group_by("Closed_Date_New").agg(pl.col("count").sum().alias("num_closed_tickets"))

ct_df = closed_tickets.with_columns(
    pl.col("num_closed_tickets") # Rename Column
)

Concatenatation to the final service dataframe

In [ ]:
# First lets make sure the lengths are the same so the concat works horizontally (feature <-> feature)
assert len(sd_grouped) == len(ct_df)

sd_df = pl.concat([sd_grouped, ct_df.drop("Closed_Date_New")], how="horizontal")

### Categorical Feature Processing

The main problem to solve is how to encode these categories. For the four main categorical features we selected (Agency, Complaint Type, Descriptor, Borough), after grouping by the created date, we can see that there are multiple instances of categories per feature. The question to solve is how can we take this information and encode it into a useful feature.

#### Feature Distribution

First we need to understand the general breakdown of the categorical features:<br>
1. How many categories are there?
2. Is there any way to efficiently group the categories?

In [ ]:
service_data.with_columns(
    pl.col("Borough").n_unique().alias("Borough Count"),
    pl.col("Agency").n_unique().alias("Agency Count"),
    pl.col("Complaint Type").n_unique().alias("Complaint Type Count"),
    pl.col("Descriptor").n_unique().alias("Descriptor Count")
)[["Borough Count", "Agency Count", "Complaint Type Count", "Descriptor Count"]].head(1)

Borough will be the easiest to encode as there are only 9 features. Complaint Type and Descriptor will be the most difficult to encode as they have 100/1000+ features. Agency has 30 features but it may be possible to encode them still.

#### Step 1: Grouping each category

It is not efficient to have 1000+ categories for a single feature. I will need to reduce the number of categories per categorical feature.

**Borough**<br>
This is the easiest case. I will create a mapping that groups the small categories all together. Namely: Unspecified, 2017, 2016, and null will go in the "OTHER" category.

In [ ]:
Borough_Map = {
    "Unspecified": "OTHER",
    "2017": "OTHER",
    None: "OTHER",
    "2016": "OTHER"
}
service_data = service_data.with_columns(
    pl.col("Borough").replace(Borough_Map)
)

**Agency**<br>
For this case, I need to see all the categories.

The work below is from manual research into each agency in the list of unique agencies. I have grouped them together based on my own judgement of what that agency most likely does.

In [ ]:
Agency_Map = {
    "NYPD": "Security",
    "HPD": "Buildings",
    "DOT": "Transportation",
    # "DSNY": "Sanitation", # Sanitation and Environment are similar, will group
    "DSNY": "Environment & Sanitation",
    "DEP": "Environment & Sanitation",
    "DOB": "Buildings",
    "DOE": "Buildings",
    "DPR": "Parks",
    "DOHMH": "Health",
    # "DOF": "Finance", # Finance I will group in Other as there aren't too many of these
    "DOF": "Other",
    "DHS": "Security",
    "TLC": "Transportation",
    "HRA": "Other",
    "DCA": "Other",
    "DFTA": "Other",
    "EDC": "Other",
    "DOITT": "Other",
    "DCAS": "Other",
    "NYCEM": "Other",
    "ACS": "Other",
    "3-1-1": "Other",
    "TAX": "Other",
    "DCP": "Other",
    "DORIS": "Other",
    "FDNY": "Other",
    "TAT": "Other",
    "COIB": "Other",
    "CEO": "Other",
    "MOC": "Other",
    "OMB": "Other"
}

service_data = service_data.with_columns(
    pl.col("Agency").replace(Agency_Map).alias("AG") # AG Shorthand for Agency Groups
)
service_data["AG"].value_counts(sort=True)

**Decision: Use Agency Groups as proxy for Agency**

**Complaint Type**<br>
Lets see the categories for complaint type

First lets see how Complaint Type and Agency are related

In [ ]:
nunique_pairs = len(service_data.group_by(["Complaint Type", "Agency"]).len())
nunique_complaints = service_data["Complaint Type"].n_unique()
diff = nunique_pairs - nunique_complaints
print(f"Number of Unique Pairs of (Complaint Type, Agency): {nunique_pairs}")
print(f"Number of Complaint Types filed by multiple Agencies: {diff}")

There are 299 unique pairs of Complaint and Agency out of 271 unique Complaint types; thus, ~10% of complaint types will not be uniquely grouped by the previous Agency group we created. Practically, this means the prior work we did in grouping the agencies actually translates well to how we would group complaint types. Because complaint types are mostly unique to the agency that filed them, the agency group can serve as a proxy descriptor group for complaint types.<br>

NOTE: One option is to use these complaint types as a subcategory for agency group; however, this will cause our model to suffer from the curse of dimensionality. It is not worth bringing in this large number of extra features

**Decision: Remove Complaint Type as a variable. Use Agency Groups as proxy**

**Descriptor**<br>
Getting groups of categories for descriptor is a bit more complicated. As you can see below, we have 1000+ unique descriptors. My proposed solution is to use a Language Model to extract topics from this column. I will use a python library called [BERTopic](https://github.com/MaartenGr/BERTopic) to do so.

The code below is commented out as it was pretrained using the code below. We can load the pretrained model directly instead.

In [ ]:
# Store descriptors as pandas dataframe (polars not supported)
# Drop any nan values, and we only care about the unique values
descriptor_docs = service_data["Descriptor"].unique().to_numpy()

In [ ]:
# from bertopic import BERTopic
# from sklearn.feature_extraction.text import CountVectorizer
# from sentence_transformers import SentenceTransformer
# from umap import UMAP
# import torch

# # Use a Vectorizer (basically a model that removes stopwords and controls the term frequency counting)
# # BERTopic uses a clusterd TF-IDF score for word importance (c-TF-IDF)
# # This is an NLP concept often used in information retrieval (can explain if asked)
# vectorizer_model = CountVectorizer(stop_words="english", min_df=2, ngram_range=(1,2))
# umap_model = UMAP(n_components=10, n_neighbors=40, min_dist=0.0)

# # Precalculating the document embeddings speeds up BERTopic performance
# # This takes some time to run (approximately 5 minutes)
# # It will be commented out as it isn't needed to run the model
# device = "cuda" if torch.cuda.is_available() else "cpu"
# embedding_model = SentenceTransformer("all-MiniLM-L6-v2", device=device)
# embeddings = embedding_model.encode(descriptor_docs, batch_size=2048, device=device, show_progress_bar=True)

# # Create BERTopic model
# topic_model = BERTopic(
#     embedding_model=embedding_model,
#     vectorizer_model=vectorizer_model,
#     umap_model=umap_model,
#     top_n_words=5,
#     nr_topics=8,
#     verbose=True,
# )

# topic, probs = topic_model.fit_transform(descriptor_docs, embeddings)

# embedding_model_name = "sentence-transformers/all-MiniLM-L6-v2"
# topic_model.save("models/BERTopic", serialization="safetensors", save_ctfidf=True, save_embedding_model=embedding_model_name)

ERRORS: DUE TO EMAIL FILE SHARING ERRORS/BLOCKAGE, THIS CODE IS COMMENTED OUT. I LOAD THE doc_to_topic map MANUALLY

In [ ]:
# # Load model and get predictions
# topic_model = BERTopic.load("models/BERTopic")
# topics, probs = topic_model.transform(descriptor_docs)

# # Visualize if wanted
# # topic_model.visualize_barchart(list(range(-1,6,1)))

# # Create a topic to ID map
# topic_df = topic_model.get_topic_info()
# topic_id_map = {row["Topic"]: row["Name"][2:] for _, row in topic_df.iterrows()}
# topic_id_map[-1] = topic_id_map[-1][1:] # Fix for the -1 topic case

# # For each document (descriptor string) get a mapping of topics
# doc_to_topic_map = defaultdict(str)
# for topic_id, doc in zip(topics, descriptor_docs):
#     topic = topic_id_map[topic_id]
#     doc_to_topic_map[doc] = topic

In [ ]:
doc_to_topic_map = {"Damaged/Defective": "damaged_sign_sidewalk_missing", "Catch Basin Search (SC2)": "water_basin_litter_missed", "No Consent Form": "license_complaint_illegal_violation", "Delays": "order_property_inspection_condition", "FDNY Referral - Pilot": "license_complaint_illegal_violation", "Adult Establishment": "damaged_sign_sidewalk_missing", "Temporary Amusement Device License": "license_complaint_illegal_violation", "ROOFING": "damaged_sign_sidewalk_missing", "The ABCs of Housing - Chinese": "damaged_sign_sidewalk_missing", "RAIN GARDEN FLOODING (SRGFLD)": "water_basin_litter_missed", "Domestic Strays": "noise_animal_truck_dead", "Co-op or Condo Abatement": "order_property_inspection_condition", "CARBON MONOXIDE DETECTOR": "odor_food_air_smoke", "E5 Loose Rubbish": "water_basin_litter_missed", "Plate Missing/Moved-Exposing Hole (SB4)": "damaged_sign_sidewalk_missing", "Facility Unregistered": "license_complaint_illegal_violation", "Lighting - Garage": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - English": "english_emergency_spanish_chinese", "Dealer in Devices for Disabled License": "license_complaint_illegal_violation", "Excise Taxes-Refund": "exemption_commercial_tax_business", "Plate Noisy/Sunken/Raised (WF5)": "noise_animal_truck_dead", "Plate Condition - Shifted": "order_property_inspection_condition", "MCI Abatement": "order_property_inspection_condition", "Going Out of Business Sale License": "license_complaint_illegal_violation", "Failure to Comply with Annual Crane Inspection": "license_complaint_illegal_violation", "Booting Company License": "license_complaint_illegal_violation", "Crane/Suspension Scaffold - No Permit/License/Cert./Unsafe/Illegal": "license_complaint_illegal_violation", "Stalled Construction Site": "damaged_sign_sidewalk_missing", "ER5 Comm. Recyc. (Bldg Mgmt)": "order_property_inspection_condition", "M.A.R.C.H. Program (Interagency)": "license_complaint_illegal_violation", "General Bad Condition": "order_property_inspection_condition", "Ped Multiple Lamps": "damaged_sign_sidewalk_missing", "Plate Condition - Anti-Skid": "order_property_inspection_condition", "Inadequate or No Heat": "odor_food_air_smoke", "Office of Preventive Technical Assistance/OPTA": "order_property_inspection_condition", "1RE missed collection for E-waste": "water_basin_litter_missed", "Bowstring Truss Tracking Complaint": "license_complaint_illegal_violation", "ALJ Division": "order_property_inspection_condition", "Chemical Spill (IAC)": "water_basin_litter_missed", "Chemical Spill/Release (HA1)": "water_basin_litter_missed", "Miscellaneous": "order_property_inspection_condition", "Sidewalk Grating - Defective": "damaged_sign_sidewalk_missing", "Defective Hardware": "damaged_sign_sidewalk_missing", "DOOR TO DUMBWAITER": "damaged_sign_sidewalk_missing", "Street Flooding (SJ)": "order_property_inspection_condition", "1RO Missed Recycling Organics": "water_basin_litter_missed", "Sign Defect - Lot": "damaged_sign_sidewalk_missing", "Door Open with Air Conditioning On": "odor_food_air_smoke", "Medicaid": "english_emergency_spanish_chinese", "Broken Curb": "damaged_sign_sidewalk_missing", "Street Light Dayburning": "damaged_sign_sidewalk_missing", "Defective Street Cut (WZZ1)": "damaged_sign_sidewalk_missing", "LED Pedestrian Unit": "damaged_sign_sidewalk_missing", "Illegal Commercial Or Manufacturing Use In a C1 Or C2 Zone": "license_complaint_illegal_violation", "Illness Caused by Drinking Water": "water_basin_litter_missed", "unknown odor/taste in drinking water (QA6)": "odor_food_air_smoke", "Sewer Backup (Use Comments) (SA)": "water_basin_litter_missed", "Status Call": "order_property_inspection_condition", "Parking Permit Improper Use": "license_complaint_illegal_violation", "OUTLET/SWITCH": "damaged_sign_sidewalk_missing", "Blocked Sidewalk": "damaged_sign_sidewalk_missing", "Police Report Requested": "order_property_inspection_condition", "In-Line Fuse Missing": "damaged_sign_sidewalk_missing", "Commercial ICIP or ICAP Exemption": "exemption_commercial_tax_business", "Copy of Approval Order": "license_complaint_illegal_violation", "Accessibility Accommodations": "order_property_inspection_condition", "Curb Cut/Driveway/Carport - Illegal": "license_complaint_illegal_violation", "Dry Cleaning Vapors (PERC)": "odor_food_air_smoke", "Multiple St Lts Dayburning": "odor_food_air_smoke", "Seasonal Mobile Food Vendor License": "license_complaint_illegal_violation", "Documents Not Returned": "license_complaint_illegal_violation", "Noise: Loud Music/Nighttime(Mark Date And Time) (NP1)": "noise_animal_truck_dead", "Contractor Responsibility/VENDEX": "license_complaint_illegal_violation", "Cigarette Vending Machine": "license_complaint_illegal_violation", "Hurricane Preparedness - Spanish": "english_emergency_spanish_chinese", "Inattentive": "noise_animal_truck_dead", "Suspended (Hanging) Scaffolds - No Pmt/Lic/Dangerous/Accident": "damaged_sign_sidewalk_missing", "Zoning - Non-Conforming/Illegal Vehicle Storage": "license_complaint_illegal_violation", "Rates Not Posted": "license_complaint_illegal_violation", "Illegal Use Of Hose - Private Residence": "license_complaint_illegal_violation", "Flooded": "water_basin_litter_missed", "Chronic Speeding": "license_complaint_illegal_violation", "Detached Trailer": "order_property_inspection_condition", "Car Service Company Report": "license_complaint_illegal_violation", "Status of Request to file Paper RPIE": "license_complaint_illegal_violation", "Double Parked Blocking Vehicle": "damaged_sign_sidewalk_missing", "Ready NY - Russian - Pocket Size": "english_emergency_spanish_chinese", "Maintenance Cover": "order_property_inspection_condition", "Rat Sighting": "noise_animal_truck_dead", "Broken Water Fountain": "water_basin_litter_missed", "Marine Flasher": "order_property_inspection_condition", "In Car": "order_property_inspection_condition", "Posted Parking Sign Violation": "license_complaint_illegal_violation", "Food Source/Protection": "odor_food_air_smoke", "Commercial Rent Tax- Refund": "exemption_commercial_tax_business", "Tenant Refusal": "license_complaint_illegal_violation", "Air: Smoke, Residential (AA1)": "odor_food_air_smoke", "Lost and Found": "order_property_inspection_condition", "HEAVY FLOW": "water_basin_litter_missed", "Leak (Use Comments) (WA2)": "water_basin_litter_missed", "Ready NY - Russian - Full Size": "english_emergency_spanish_chinese", "Commercial 421A Exemption": "exemption_commercial_tax_business", "Oil Spill Into Basin/Sewer - Small (IABS)": "water_basin_litter_missed", "Licensed Home Improvement Contractor Bumper Sticker": "license_complaint_illegal_violation", "Food Worker Hygiene": "odor_food_air_smoke", "Accident - Construction/Plumbing": "order_property_inspection_condition", "Ready NY Guide - Pocket Sized - English": "english_emergency_spanish_chinese", "Failure to Post Calorie Information": "license_complaint_illegal_violation", "Bees/Wasps - Not a beekeper": "noise_animal_truck_dead", "Taste/Odor, Chemical (QA2)": "odor_food_air_smoke", "Traffic Camera": "damaged_sign_sidewalk_missing", "Real Estate Services": "order_property_inspection_condition", "Building": "damaged_sign_sidewalk_missing", "Hyd Valve Box Cover Missing (WV2)": "water_basin_litter_missed", "Emergency Notice": "order_property_inspection_condition", "Advance Fee": "license_complaint_illegal_violation", "Cleanliness": "odor_food_air_smoke", "Frozen Dessert Manufacturer License": "license_complaint_illegal_violation", "Crash Cushion Defect": "damaged_sign_sidewalk_missing", "Fleet": "order_property_inspection_condition", "Plants- Odor Related Problems (PO1)": "odor_food_air_smoke", "Fixture/Luminaire Door Open": "damaged_sign_sidewalk_missing", "Parking Card Stuck in Meter": "license_complaint_illegal_violation", "Damaged Telephone": "damaged_sign_sidewalk_missing", "Illegal Conversion Of Residential Building/Space": "license_complaint_illegal_violation", "Illegal Tree Removal/Topo. Change in SNAD": "order_property_inspection_condition", "E12 Illegal Dumping Surveillance": "license_complaint_illegal_violation", "Seizure of Funds": "license_complaint_illegal_violation", "Facility Construction": "damaged_sign_sidewalk_missing", "Inspection Work Order (DOB)": "license_complaint_illegal_violation", "City Planning Commission": "damaged_sign_sidewalk_missing", "Time Insufficient": "order_property_inspection_condition", "Notice of Housing Code Enforcement Issues": "order_property_inspection_condition", "Guard Rail - Street": "damaged_sign_sidewalk_missing", "Commercial 421B Exemption": "exemption_commercial_tax_business", "Air Conditioning Problem": "odor_food_air_smoke", "APARTMENT ONLY": "damaged_sign_sidewalk_missing", "Wasting Faucets,Sinks,Flushometer,Urinal,Etc. - Private Residence (CWR)": "water_basin_litter_missed", "Lack of Supplies": "order_property_inspection_condition", "Ready NY - Chinese Simplified - Full Size": "english_emergency_spanish_chinese", "Noise, Other Animals (NR6)": "noise_animal_truck_dead", "Cellar Door Open/Unprotected": "damaged_sign_sidewalk_missing", "Unauthorized Climbing": "license_complaint_illegal_violation", "Remove Mortgage": "damaged_sign_sidewalk_missing", "Sidewalk Staircase": "damaged_sign_sidewalk_missing", "Wood Pole Missing": "damaged_sign_sidewalk_missing", "CMU Communication": "noise_animal_truck_dead", "OUTLET COVER": "damaged_sign_sidewalk_missing", "Illegal Tow": "order_property_inspection_condition", "Projects": "damaged_sign_sidewalk_missing", "Yield": "order_property_inspection_condition", "Egress - Doors Locked/Blocked/Improper/No Secondary Means": "damaged_sign_sidewalk_missing", "Housing Information Guide For Tenants and Owners Notice": "license_complaint_illegal_violation", "Detector Sensor": "noise_animal_truck_dead", "Cave-in": "noise_animal_truck_dead", "Partial Access": "order_property_inspection_condition", "Scale Inaccurate": "order_property_inspection_condition", "Cat": "noise_animal_truck_dead", "Noise, Ice Cream Truck (NR4)": "noise_animal_truck_dead", "ER1 Resident Recyc. (Owner/Manager": "license_complaint_illegal_violation", "E30 Transfer Station": "water_basin_litter_missed", "Ready NY - Kids - Elementary School Students": "english_emergency_spanish_chinese", "WINDOW PANE": "damaged_sign_sidewalk_missing", "Construction Enforcement Work Order (DOB)": "license_complaint_illegal_violation", "Ready NY - Businesses - English": "english_emergency_spanish_chinese", "V.E.S.T. Program (DOB & NYPD)": "license_complaint_illegal_violation", "Culvert Blocked/Needs Cleaning (SE)": "water_basin_litter_missed", "General Vendor Waiting List Application": "license_complaint_illegal_violation", "Sprinkler System - Inadequate": "water_basin_litter_missed", "Electronics and Home Appliance Service Dealer License": "license_complaint_illegal_violation", "Police Report Not Requested": "license_complaint_illegal_violation", "15S Re-Plow/Spread/Ice-Snow Cond.": "order_property_inspection_condition", "Lamppost Wire Exposed": "damaged_sign_sidewalk_missing", "Copy of Notice of Property Value": "license_complaint_illegal_violation", "Announcements": "order_property_inspection_condition", "Door": "damaged_sign_sidewalk_missing", "Condition Attracting Rodents": "noise_animal_truck_dead", "Returns Not Filed": "exemption_commercial_tax_business", "Do Not Enter": "damaged_sign_sidewalk_missing", "E1 Improper Disposal": "water_basin_litter_missed", "Waive Penalty for Late Payment": "license_complaint_illegal_violation", "9 Spill/Oil etc": "water_basin_litter_missed", "Bracket Arm Broken": "damaged_sign_sidewalk_missing", "Demand for Cash": "exemption_commercial_tax_business", "General Counsel": "damaged_sign_sidewalk_missing", "Gas Utility Referral": "license_complaint_illegal_violation", "After Hours Work - Illegal": "license_complaint_illegal_violation", "Unincorporated Business Tax - Return Filing": "exemption_commercial_tax_business", "Unleashed Dog in Public": "noise_animal_truck_dead", "Hydrant Defective (WC2)": "water_basin_litter_missed", "Plumbing Enforcement Work Order (DOB)": "license_complaint_illegal_violation", "Ready NY My Emergency Plan - Korean": "english_emergency_spanish_chinese", "Fire Alarm Lamp Cycling": "damaged_sign_sidewalk_missing", "Driver Complaint": "license_complaint_illegal_violation", "TAC Report": "order_property_inspection_condition", "Full Term Tattoo License": "license_complaint_illegal_violation", "Mapping Information": "order_property_inspection_condition", "ENTIRE BUILDING": "damaged_sign_sidewalk_missing", "Dirt, Litter, Debris - Lot": "water_basin_litter_missed", "Building Shaking/Vibrating/Structural Stability": "damaged_sign_sidewalk_missing", "Personal Veteran Exemption": "exemption_commercial_tax_business", "Secondhand Dealer Auto License": "license_complaint_illegal_violation", "Business Tax": "exemption_commercial_tax_business", "Illegal Conversion No Access Follow - UP": "license_complaint_illegal_violation", "High Grass": "order_property_inspection_condition", "Lighting": "damaged_sign_sidewalk_missing", "Stop": "order_property_inspection_condition", "MAINTENANCE": "order_property_inspection_condition", "1 or 2": "order_property_inspection_condition", "22 Weeds": "noise_animal_truck_dead", "Integrity Complaint Referral": "license_complaint_illegal_violation", "2 Bulk-Missed Collection": "water_basin_litter_missed", "Sightseeing Bus License": "license_complaint_illegal_violation", "Red Lt Camera Feed": "damaged_sign_sidewalk_missing", "Fountain - Over 5 Gallons": "water_basin_litter_missed", "WINDOW GUARD BROKEN/MISSING": "damaged_sign_sidewalk_missing", "Copy of Statement": "order_property_inspection_condition", "\\E4 18\\\"\\\" Law\\\"\"": "order_property_inspection_condition", "Stop Temporary": "order_property_inspection_condition", "Farm Animal": "noise_animal_truck_dead", "Catch Basin Sunken/Damaged/Raised (SC1)": "water_basin_litter_missed", "General Inquiry": "order_property_inspection_condition", "Planted More Than 2 Years Ago": "water_basin_litter_missed", "Structurally Compromised Building (LL33/08)": "damaged_sign_sidewalk_missing", "For One Address": "order_property_inspection_condition", "Relocation of Bus Stop Shelter": "order_property_inspection_condition", "Mitchell-Lama Housing List": "order_property_inspection_condition", "Semi-Annual Homeless Shelter Inspection: Plumbing": "order_property_inspection_condition", "Dead End Sign": "damaged_sign_sidewalk_missing", "No Statement of Job Conditions": "order_property_inspection_condition", "1 Missed Collection": "order_property_inspection_condition", "Landlord Inquiries": "order_property_inspection_condition", "\\Smoking Signs - \\\"\\\"No Smoking\\\"\\\" Signs Not Observed on Construction Site\\\"\"": "odor_food_air_smoke", "Dirty/Inadequate Equip./Facility": "order_property_inspection_condition", "DAMP SPOT": "order_property_inspection_condition", "SPRINKLER": "order_property_inspection_condition", "Kitchen/Food Prep Area": "odor_food_air_smoke", "ROOF DOOR/HATCH": "damaged_sign_sidewalk_missing", "FENCING": "damaged_sign_sidewalk_missing", "Dirt, Litter, Debris - Garage": "water_basin_litter_missed", "Demolition Notification Received": "damaged_sign_sidewalk_missing", "In Post Base": "damaged_sign_sidewalk_missing", "Lamppost Base Door/Cover Damaged": "damaged_sign_sidewalk_missing", "Zoning and Land Use Questions/Information": "order_property_inspection_condition", "Beekeeping - Honeybees": "noise_animal_truck_dead", "Graffiti - Highway": "damaged_sign_sidewalk_missing", "Warning Buzzer": "noise_animal_truck_dead", "Loose Plate": "order_property_inspection_condition", "Commercial UDAAP Exemption": "exemption_commercial_tax_business", "Commercial 421G Exemption": "exemption_commercial_tax_business", "Restroom Non-Complaince With Local Law 79/16": "license_complaint_illegal_violation", "Summer Heat - Spanish": "english_emergency_spanish_chinese", "Wood Pole Knocked Down": "damaged_sign_sidewalk_missing", "Missing Complaint Sign": "license_complaint_illegal_violation", "Fence": "damaged_sign_sidewalk_missing", "Incorrect Amount Paid": "license_complaint_illegal_violation", "Ready NY - French - Full Size": "english_emergency_spanish_chinese", "Animal Odor": "noise_animal_truck_dead", "Roof Gutters": "damaged_sign_sidewalk_missing", "RPIE": "order_property_inspection_condition", "Payment Misapplied": "license_complaint_illegal_violation", "Dumpster - Causing Damage": "water_basin_litter_missed", "Cellar Door Defective": "damaged_sign_sidewalk_missing", "EEO": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - Italian": "english_emergency_spanish_chinese", "Pawn Broker License": "license_complaint_illegal_violation", "Hydrant Running (WC3)": "water_basin_litter_missed", "MOLD": "odor_food_air_smoke", "Barbershop License": "license_complaint_illegal_violation", "Base Door": "damaged_sign_sidewalk_missing", "Tax Commission Rules": "exemption_commercial_tax_business", "Personal Exemptions": "exemption_commercial_tax_business", "Ped Lamp": "damaged_sign_sidewalk_missing", "Food Stamp": "odor_food_air_smoke", "SIGNAGE MISSING": "damaged_sign_sidewalk_missing", "Electronics/Phones": "order_property_inspection_condition", "Animal Grooming License": "license_complaint_illegal_violation", "Ready NY - Pets - English": "english_emergency_spanish_chinese", "Non-Disclosure of Fees": "exemption_commercial_tax_business", "Loud Talking": "noise_animal_truck_dead", "Wildlife Sighting": "noise_animal_truck_dead", "Flavored Tobacco": "odor_food_air_smoke", "Bag/Wallet": "order_property_inspection_condition", "Beach/Pool Water": "water_basin_litter_missed", "No Water (WNW)": "water_basin_litter_missed", "Building Information/Construction History": "damaged_sign_sidewalk_missing", "Language Access Coordinator": "english_emergency_spanish_chinese", "Investigative Inspection": "order_property_inspection_condition", "Illegal Dumping": "order_property_inspection_condition", "Elevator - Multiple Devices On Property": "order_property_inspection_condition", "Property Address Incorrect": "order_property_inspection_condition", "WATER SUPPLY": "water_basin_litter_missed", "Billing Address Incorrect": "license_complaint_illegal_violation", "Food Worker Activity": "odor_food_air_smoke", "Car/Truck Horn": "noise_animal_truck_dead", "Underage - Licensed Est": "license_complaint_illegal_violation", "Gaming Cafe License": "license_complaint_illegal_violation", "TOILET": "water_basin_litter_missed", "No Receipt": "license_complaint_illegal_violation", "Contrary To LL 58/87(Handicapped Access)": "order_property_inspection_condition", "Condo or Co-op Abatement": "order_property_inspection_condition", "Equipment": "order_property_inspection_condition", "HomeFirst Down Payment Information": "license_complaint_illegal_violation", "Injury/Safety": "damaged_sign_sidewalk_missing", "Manhole Overflow (Use Comments) (SA1)": "water_basin_litter_missed", "15 Street Cond/Dump-Out/Drop-Off": "order_property_inspection_condition", "Strip Paving": "order_property_inspection_condition", "1C Uncollected Xmas Trees": "order_property_inspection_condition", "Fixture(S)": "damaged_sign_sidewalk_missing", "For Violation": "license_complaint_illegal_violation", "Working Contrary To Stop Work Order": "order_property_inspection_condition", "Elevator - Single Device On Property/No Alternate Service": "order_property_inspection_condition", "St Name - Attached to Pole": "damaged_sign_sidewalk_missing", "Handwashing": "odor_food_air_smoke", "Waterway-Oil/Gasoline (IHB)": "water_basin_litter_missed", "Turtle Under 4 inches Long": "noise_animal_truck_dead", "No Permit or License": "license_complaint_illegal_violation", "Non Retail Food Processing Establishment License": "license_complaint_illegal_violation", "WALL": "damaged_sign_sidewalk_missing", "Bike Rack Repair": "damaged_sign_sidewalk_missing", "Open Excavation (WZZ2)": "order_property_inspection_condition", "No Dial Tone": "noise_animal_truck_dead", "Push Button": "damaged_sign_sidewalk_missing", "Pothole - Highway": "damaged_sign_sidewalk_missing", "Homeless Issue": "order_property_inspection_condition", "Summer Heat - English": "english_emergency_spanish_chinese", "Sidewalk Violation": "damaged_sign_sidewalk_missing", "Semi-Annual Homeless Shelter Inspection: Construction": "order_property_inspection_condition", "Non-Delivery of Papers": "license_complaint_illegal_violation", "Oil Spill On Street, Small (HQS)": "water_basin_litter_missed", "For Letter of Defect": "order_property_inspection_condition", "Business Opportunities/RFPs": "order_property_inspection_condition", "Pedestrian Signal": "damaged_sign_sidewalk_missing", "Pedestrian Ramp Defective": "damaged_sign_sidewalk_missing", "Sign": "damaged_sign_sidewalk_missing", "GUTTER/LEADER": "damaged_sign_sidewalk_missing", "Guard Rail - Highway": "damaged_sign_sidewalk_missing", "Too Few on Duty": "order_property_inspection_condition", "Billing Dispute": "license_complaint_illegal_violation", "Hurricane Preparedness - Arabic": "english_emergency_spanish_chinese", "Food Protection": "odor_food_air_smoke", "Graffiti - Bridge": "damaged_sign_sidewalk_missing", "Special Events": "order_property_inspection_condition", "Commercial Government Exemption": "exemption_commercial_tax_business", "Puddle on Driveway": "water_basin_litter_missed", "2R Bulk-Missed Recy Collection": "water_basin_litter_missed", "Affecting Sewer or Foundation": "water_basin_litter_missed", "Personal STAR Exemption": "exemption_commercial_tax_business", "Credit Card Limitations Not Posted": "license_complaint_illegal_violation", "Heat Bulletin": "order_property_inspection_condition", "Chronic Stoplight Violation": "damaged_sign_sidewalk_missing", "E9 Snow / Icy Sidewalk": "order_property_inspection_condition", "Construction - Change Grade/Watercourse": "order_property_inspection_condition", "Documents/Paperwork Missing": "order_property_inspection_condition", "Plate Missing/Moved-Exposing Hole (WF4)": "damaged_sign_sidewalk_missing", "Street Cleaning - ASP": "order_property_inspection_condition", "Plate Condition - Open": "order_property_inspection_condition", "Timer Defect - Fast/Fail": "damaged_sign_sidewalk_missing", "Cabaret License": "license_complaint_illegal_violation", "Tow Truck Company License": "license_complaint_illegal_violation", "Vehicle Complaint": "license_complaint_illegal_violation", "Taste/Odor, Musty/Stale (QA4)": "odor_food_air_smoke", "Veh Signal Sec Door": "damaged_sign_sidewalk_missing", "Auction House License": "license_complaint_illegal_violation", "Other Billing Issue": "license_complaint_illegal_violation", "Spanish Transaction": "english_emergency_spanish_chinese", "Street Con Game": "damaged_sign_sidewalk_missing", "Other Water Problem (Use Comments) (WZZ)": "water_basin_litter_missed", "High Interest Loan": "order_property_inspection_condition", "Birth Certificate Before 1910 Order Form": "license_complaint_illegal_violation", "Full Term Mobile Food Unit Permit": "license_complaint_illegal_violation", "Ready NY Beat the Heat - English": "english_emergency_spanish_chinese", "GARBAGE/RECYCLING STORAGE": "water_basin_litter_missed", "1RB Missed Recycling - M/G/Pl": "water_basin_litter_missed", "Oil Spill On Street, Large (HQL)": "water_basin_litter_missed", "Pool or Billiard Hall License": "license_complaint_illegal_violation", "Smoking Violation": "license_complaint_illegal_violation", "Musical Instrument": "noise_animal_truck_dead", "1L Missed Recycling Leaves": "water_basin_litter_missed", "JANITOR/SUPER": "damaged_sign_sidewalk_missing", "Congestion/Gridlock": "order_property_inspection_condition", "Tattoo Artist Unlicensed": "license_complaint_illegal_violation", "Illegal Use Of Hose - Private Residence  (CCR)": "license_complaint_illegal_violation", "Supervisory": "order_property_inspection_condition", "Blocking Sidewalk": "damaged_sign_sidewalk_missing", "Ticket Scalping": "license_complaint_illegal_violation", "Housing Quality Standards (HQS) Inspections FAQs - Spanish": "order_property_inspection_condition", "Tortured": "noise_animal_truck_dead", "Gasoline Spill (IAA)": "water_basin_litter_missed", "The ABCs of Housing": "damaged_sign_sidewalk_missing", "Other Housing Options": "damaged_sign_sidewalk_missing", "Non-Delivery Goods/Services": "license_complaint_illegal_violation", "Snake": "noise_animal_truck_dead", "Relocation of Parking Meter": "license_complaint_illegal_violation", "Container - Under 5 Gallons": "water_basin_litter_missed", "Lamppost Leaning": "damaged_sign_sidewalk_missing", "Sign/Awning/Marquee - Illegal/No Permit": "license_complaint_illegal_violation", "Re-inspection": "order_property_inspection_condition", "Senior Citizen Home Assistance Program (SCHAP) Loan": "exemption_commercial_tax_business", "REFRIGERATOR": "odor_food_air_smoke", "Air: Smoke, Vehicular (AA4)": "odor_food_air_smoke", "Media Inquiries": "noise_animal_truck_dead", "Industrial Laundry Delivery License Application": "license_complaint_illegal_violation", "Curb Violation": "license_complaint_illegal_violation", "Transducer-Loop": "noise_animal_truck_dead", "Stoop Line Stand License": "license_complaint_illegal_violation", "The ABCs of Housing - Korean": "damaged_sign_sidewalk_missing", "Speed Limit": "license_complaint_illegal_violation", "Accident - Elevator": "damaged_sign_sidewalk_missing", "Executive": "damaged_sign_sidewalk_missing", "Damaged Bench": "damaged_sign_sidewalk_missing", "Blocked - ATM": "order_property_inspection_condition", "Clothing Damage": "order_property_inspection_condition", "Veh Signal Lens": "damaged_sign_sidewalk_missing", "Water Meter Stolen/Missing - Private Residence (CLR)": "order_property_inspection_condition", "Electronic Sign - Portable": "damaged_sign_sidewalk_missing", "SCRIE Miscellaneous": "order_property_inspection_condition", "Personal Clergy Exemption": "exemption_commercial_tax_business", "Illegal Activity by Phone": "license_complaint_illegal_violation", "Traffic Sign or Signal Blocked": "damaged_sign_sidewalk_missing", "ID Requirement Not Posted": "license_complaint_illegal_violation", "Temporary Food Service Establishment Permit": "license_complaint_illegal_violation", "Reinspection": "order_property_inspection_condition", "Garage or Parking Lot License": "license_complaint_illegal_violation", "Messenger": "noise_animal_truck_dead", "Certificate of No Harassment - Zoning": "license_complaint_illegal_violation", "E8 Canine Violation": "noise_animal_truck_dead", "Wastewater Into Catch Basin (IEB)": "water_basin_litter_missed", "Technician Unlicensed": "license_complaint_illegal_violation", "Posted Notice Or Order Removed/Tampered With": "license_complaint_illegal_violation", "New Bus Stop Shelter Placement": "damaged_sign_sidewalk_missing", "American Flag": "damaged_sign_sidewalk_missing", "Noise: Manufacturing Noise (NK1)": "noise_animal_truck_dead", "Signs of Rodents": "noise_animal_truck_dead", "Dogs or Cats Sold": "noise_animal_truck_dead", "Relocation of Muni Meter": "order_property_inspection_condition", "Line/Marking - After Repaving": "damaged_sign_sidewalk_missing", "Oil Spill Into Basin/Sewer - Large (IABL)": "water_basin_litter_missed", "Snow Removal Requested": "order_property_inspection_condition", "Excavation Undermining Adjacent Building": "damaged_sign_sidewalk_missing", "Building Permit - None": "license_complaint_illegal_violation", "21 Collection Truck Noise": "noise_animal_truck_dead", "Flood Light Lamp Dim": "damaged_sign_sidewalk_missing", "Food Temperature": "odor_food_air_smoke", "Tree Alive - in Poor Condition": "damaged_sign_sidewalk_missing", "Newsstand License": "license_complaint_illegal_violation", "E2A Storage Of Receptacles": "water_basin_litter_missed", "Catch Basin Clogged/Flooding (Use Comments) (SC)": "water_basin_litter_missed", "E1A Litter Basket / Improper Use": "water_basin_litter_missed", "Closed without Notice": "order_property_inspection_condition", "Ready NY - Korean - Full Size": "english_emergency_spanish_chinese", "Interest Dispute": "license_complaint_illegal_violation", "In Conduit": "order_property_inspection_condition", "HOUSING QUALITY STANDARDS": "order_property_inspection_condition", "Failure To Maintain": "order_property_inspection_condition", "Failed Street Repair": "damaged_sign_sidewalk_missing", "Paid in Advance": "license_complaint_illegal_violation", "Ready NY - Small and Mid-Sized Companies": "english_emergency_spanish_chinese", "Puddle in Ground": "water_basin_litter_missed", "Plumbing": "water_basin_litter_missed", "E2 Receptacle Violation": "water_basin_litter_missed", "Sign - In Danger Of Falling": "damaged_sign_sidewalk_missing", "Unrequested Services Provided": "license_complaint_illegal_violation", "Locker Break-in/Incident": "damaged_sign_sidewalk_missing", "Public Complaint - Comm Location": "license_complaint_illegal_violation", "Garbage or Litter": "water_basin_litter_missed", "Glassware Broken": "damaged_sign_sidewalk_missing", "On Messenger": "damaged_sign_sidewalk_missing", "6 Overflowing Litter Baskets": "water_basin_litter_missed", "Shelter for Homeless Animals License": "noise_animal_truck_dead", "E13 Throw-Out": "water_basin_litter_missed", "MICROWAVE": "odor_food_air_smoke", "Food Preparation Location": "odor_food_air_smoke", "Equipment Not Safe": "order_property_inspection_condition", "Ewaste appointment": "order_property_inspection_condition", "Facility General": "order_property_inspection_condition", "Beach/Pool/Sauna Unpermitted": "water_basin_litter_missed", "Smoke/Odor": "odor_food_air_smoke", "BBS Failure": "order_property_inspection_condition", "Unsafe Worksite": "order_property_inspection_condition", "Non-Compliance w/Lightweight Materials": "order_property_inspection_condition", "Special Agency Projects/Initiatives": "order_property_inspection_condition", "Insects / Pests": "noise_animal_truck_dead", "Home Improvement Salesperson License": "license_complaint_illegal_violation", "Illegal Activity": "order_property_inspection_condition", "Locksmith License": "license_complaint_illegal_violation", "Employment Agency License": "license_complaint_illegal_violation", "No Shelter": "damaged_sign_sidewalk_missing", "Noise: Boat(Engine,Music,Etc) (NR10)": "noise_animal_truck_dead", "Applied to Wrong Ticket": "license_complaint_illegal_violation", "Commercial DAMP Exemption": "exemption_commercial_tax_business", "Ped Flasher": "damaged_sign_sidewalk_missing", "Dumpster - Construction Waste": "water_basin_litter_missed", "Unauthorized Film Shoot": "license_complaint_illegal_violation", "Ethernet Cable": "damaged_sign_sidewalk_missing", "Support Bracket": "damaged_sign_sidewalk_missing", "TAL 2 Wheelchair": "order_property_inspection_condition", "Request Large Bulky Item Collection": "order_property_inspection_condition", "Dirty Water (WE)": "water_basin_litter_missed", "No Sampling Required, Requested Information (QG2)": "license_complaint_illegal_violation", "Layaway Terms Not Provided": "exemption_commercial_tax_business", "Ferret": "noise_animal_truck_dead", "POWER OUTAGE": "damaged_sign_sidewalk_missing", "Unauthorized Posting of Signs": "license_complaint_illegal_violation", "Sewer or Drain": "water_basin_litter_missed", "PAVEMENT": "order_property_inspection_condition", "3 or More": "order_property_inspection_condition", "Elevator - Defective/Not Working": "damaged_sign_sidewalk_missing", "421A Exemption": "exemption_commercial_tax_business", "Ready NY - Kids - Middle and High School Students": "english_emergency_spanish_chinese", "Water Meter Broken/Leaking - Other (CMO)": "water_basin_litter_missed", "1R Missed Recycling-All Materials": "water_basin_litter_missed", "Animal Boarding License": "license_complaint_illegal_violation", "Neglected": "order_property_inspection_condition", "Food Contains Foreign Object": "odor_food_air_smoke", "Glassware Missing": "damaged_sign_sidewalk_missing", "Unsafe Chemical, Abandoned (HC2)": "water_basin_litter_missed", "Community Outreach": "damaged_sign_sidewalk_missing", "No Access": "order_property_inspection_condition", "Damaged or Leaking Roof": "damaged_sign_sidewalk_missing", "Bare Hands in Contact w/ Food": "odor_food_air_smoke", "Fountain - Under 5 Gallons": "water_basin_litter_missed", "Property Misclassification": "order_property_inspection_condition", "Curb Defect-Metal Protruding": "damaged_sign_sidewalk_missing", "Snow or Ice": "order_property_inspection_condition", "Tax Exemption": "exemption_commercial_tax_business", "Blocked - Construction": "damaged_sign_sidewalk_missing", "Labor Violation": "license_complaint_illegal_violation", "SCRIE Application Denial": "order_property_inspection_condition", "Driver Compliment": "order_property_inspection_condition", "PORCH/BALCONY": "damaged_sign_sidewalk_missing", "Crack Sealing": "order_property_inspection_condition", "Ready NY - Chinese Traditional - Full Size": "english_emergency_spanish_chinese", "Damaged Other": "damaged_sign_sidewalk_missing", "Mandated Reporters": "order_property_inspection_condition", "Color": "damaged_sign_sidewalk_missing", "Branch Cracked and Will Fall": "damaged_sign_sidewalk_missing", "Street Cave-In *Dep Internal Use Only* (SG1)": "order_property_inspection_condition", "SST Tracking Complaint": "license_complaint_illegal_violation", "Annual Report": "order_property_inspection_condition", "Underground": "damaged_sign_sidewalk_missing", "Other Water Problem (Use Comments) (QZZ)": "water_basin_litter_missed", "Facilities Management": "order_property_inspection_condition", "Disclosure Not Provided": "order_property_inspection_condition", "Other": "order_property_inspection_condition", "Elevator In (Fdny) Readiness - None": "damaged_sign_sidewalk_missing", "Ready NY - Polish - Full Size": "english_emergency_spanish_chinese", "Facility Complaint": "order_property_inspection_condition", "Cigarette Sale to Minor": "license_complaint_illegal_violation", "PESTS": "noise_animal_truck_dead", "Mouse Sighting": "noise_animal_truck_dead", "Swimming Pool Cover": "water_basin_litter_missed", "Food Worker Illness": "odor_food_air_smoke", "Improper Sale of Items": "license_complaint_illegal_violation", "Loud Television": "noise_animal_truck_dead", "Broken/Defective": "damaged_sign_sidewalk_missing", "Child or Minor Tanning": "damaged_sign_sidewalk_missing", "Fiscal and Business Management": "exemption_commercial_tax_business", "Copy of Account Information": "license_complaint_illegal_violation", "Smoking": "odor_food_air_smoke", "Air: Smoke, Other (Use Comments) (AA5)": "odor_food_air_smoke", "Ventilation": "odor_food_air_smoke", "Fixture/Luminaire Missing": "damaged_sign_sidewalk_missing", "Veh Signal Visor": "damaged_sign_sidewalk_missing", "Shisha": "order_property_inspection_condition", "Exposure Unnecessary": "order_property_inspection_condition", "Rodents/Insects/Garbage": "noise_animal_truck_dead", "Home Ownership Kit": "order_property_inspection_condition", "Advertising Sign/Billboard/Posters/Flexible Fabric - Illegal": "license_complaint_illegal_violation", "Electronic Sign - Overhead": "damaged_sign_sidewalk_missing", "APS": "damaged_sign_sidewalk_missing", "15I Street Condition Ice-Non Storm": "order_property_inspection_condition", "Rooster": "noise_animal_truck_dead", "Sewer Odor (SA2)": "odor_food_air_smoke", "Air: Odor/Fumes, Restaurant (AD2)": "odor_food_air_smoke", "Junction Box": "damaged_sign_sidewalk_missing", "Excise Taxes-Audit": "exemption_commercial_tax_business", "Exit/Route": "damaged_sign_sidewalk_missing", "Banging/Pounding": "noise_animal_truck_dead", "Use Indoor": "damaged_sign_sidewalk_missing", "Amusement Ride": "order_property_inspection_condition", "Lamppost Missing": "damaged_sign_sidewalk_missing", "Marriage Certificate Order Form": "license_complaint_illegal_violation", "Litter": "water_basin_litter_missed", "Misleading Appraisal": "order_property_inspection_condition", "Dogs or Cats Not Sold": "noise_animal_truck_dead", "Loud Music/Party": "noise_animal_truck_dead", "Construction": "damaged_sign_sidewalk_missing", "Warning Signal": "damaged_sign_sidewalk_missing", "Sample Suspected Gas Leak Notice": "water_basin_litter_missed", "General Business Tax - Return filing": "exemption_commercial_tax_business", "Playing in Unsuitable Place": "order_property_inspection_condition", "General Business Tax - Other": "exemption_commercial_tax_business", "Speed Board Sign": "damaged_sign_sidewalk_missing", "Suspected Street Cut": "damaged_sign_sidewalk_missing", "Scrap Metal Processor License": "license_complaint_illegal_violation", "Fixture/Luminaire Out Of Position": "damaged_sign_sidewalk_missing", "Privately Owned Public Space/Non-Compliance": "exemption_commercial_tax_business", "Unsanitary Condition": "odor_food_air_smoke", "Unclean Condition": "order_property_inspection_condition", "Public Event Seating": "damaged_sign_sidewalk_missing", "General Business Tax - Refund": "exemption_commercial_tax_business", "C1 Request Xmas Trees Collection": "english_emergency_spanish_chinese", "No or Defective Headphones": "noise_animal_truck_dead", "Initial": "english_emergency_spanish_chinese", "Milk/Dairy Products": "odor_food_air_smoke", "Initial Application": "order_property_inspection_condition", "3 Sweeping/Missed-Inadequate": "order_property_inspection_condition", "No Parking, Standing, Stopping": "damaged_sign_sidewalk_missing", "Over Capacity": "order_property_inspection_condition", "Nursing Home": "order_property_inspection_condition", "New Lead Law Rights and Requirements": "license_complaint_illegal_violation", "Fire Alarm Lamp Out": "damaged_sign_sidewalk_missing", "General Street Vendor License": "license_complaint_illegal_violation", "In Public": "order_property_inspection_condition", "Lights From Parking Lot Shining On Building": "damaged_sign_sidewalk_missing", "Excavation Tracking Complaint": "order_property_inspection_condition", "E3A Dirty Area/Alleyway": "order_property_inspection_condition", "Graffiti - Tunnel": "damaged_sign_sidewalk_missing", "Removing Wildlife": "noise_animal_truck_dead", "New Con Ed Service Request": "license_complaint_illegal_violation", "Lamppost Base Door/Cover Missing": "damaged_sign_sidewalk_missing", "Hitting Power/Phone Lines": "damaged_sign_sidewalk_missing", "Excise Taxes-Other": "exemption_commercial_tax_business", "Wear & Tear": "damaged_sign_sidewalk_missing", "SKYLIGHT": "damaged_sign_sidewalk_missing", "General Business Tax- Audit": "exemption_commercial_tax_business", "Noise:  lawn care equipment (NCL)": "noise_animal_truck_dead", "VENTILATION SYSTEM": "odor_food_air_smoke", "Ver Message Sign": "damaged_sign_sidewalk_missing", "Unlicensed Vendors": "license_complaint_illegal_violation", "Missing/Stump": "damaged_sign_sidewalk_missing", "Noise: Construction Before/After Hours (NM1)": "noise_animal_truck_dead", "Lost Coin": "order_property_inspection_condition", "Other Animal": "noise_animal_truck_dead", "Equipment Maintenance": "order_property_inspection_condition", "Rooftank Leak Or Overflow (CKO)": "water_basin_litter_missed", "Housing Quality Standards (HQS) Inspections FAQs - English": "order_property_inspection_condition", "Interior Demo Tracking Complaint": "license_complaint_illegal_violation", "Cellar Door New": "damaged_sign_sidewalk_missing", "Structural Stability Impacted - New Building Under Construction": "damaged_sign_sidewalk_missing", "Rodents/Mice": "noise_animal_truck_dead", "Structure - Indoors": "damaged_sign_sidewalk_missing", "Dust Cover": "order_property_inspection_condition", "Request To Open A Hydrant (WC4)": "water_basin_litter_missed", "Cons - Contrary/Beyond Approved Plans/Permits": "license_complaint_illegal_violation", "No Certificate Of Occupancy/Illegal/Contrary To CO": "license_complaint_illegal_violation", "Condulet Cover": "order_property_inspection_condition", "Dissatisfaction with Provider": "license_complaint_illegal_violation", "Car Not Available": "order_property_inspection_condition", "Fire Globe Missing": "damaged_sign_sidewalk_missing", "Bracket Arm Bent": "damaged_sign_sidewalk_missing", "RPIE - Filing and Technical Issues": "license_complaint_illegal_violation", "SCRIE Application Appeal": "license_complaint_illegal_violation", "Air: Dust, Construction/Demolition (AE4)": "order_property_inspection_condition", "Safety Equipment/Signs": "order_property_inspection_condition", "Amount Owed Dispute": "license_complaint_illegal_violation", "Hurricane Preparedness - Russian": "english_emergency_spanish_chinese", "Card - DOF Confirmation Number Issued": "license_complaint_illegal_violation", "Foreign Attachment On Lamppost": "exemption_commercial_tax_business", "Hangers": "damaged_sign_sidewalk_missing", "Veh Sgnl Mult Lamps": "damaged_sign_sidewalk_missing", "Other Agency Charge": "license_complaint_illegal_violation", "Snow/Ice": "order_property_inspection_condition", "In Prohibited Area": "order_property_inspection_condition", "Pathogens License": "license_complaint_illegal_violation", "E3B Sidewalk Obstruction": "damaged_sign_sidewalk_missing", "Elevator Not Inspected/Illegal/No Permit": "license_complaint_illegal_violation", "Door Lock": "damaged_sign_sidewalk_missing", "Plants- Noise Related Problems (PN1)": "noise_animal_truck_dead", "FOIL Request - Request for Records": "exemption_commercial_tax_business", "Illegal Use Of A Hydrant (CIN)": "water_basin_litter_missed", "Vent/Exhaust - Illegal/Improper": "odor_food_air_smoke", "Mental Health": "order_property_inspection_condition", "Site Conditions Endangering Workers": "order_property_inspection_condition", "6R Overflowing Recycling Baskets": "water_basin_litter_missed", "Personal Other Exemption": "exemption_commercial_tax_business", "Placement": "damaged_sign_sidewalk_missing", "Inspection Requests/Complaints": "order_property_inspection_condition", "Air: Odor, Nail Salon (AD8)": "odor_food_air_smoke", "Best - High-Rise Tracking Complaint": "order_property_inspection_condition", "Harassment": "order_property_inspection_condition", "Amusement Ride Accident/Incident": "order_property_inspection_condition", "Sewage": "water_basin_litter_missed", "Post": "damaged_sign_sidewalk_missing", "12 Dead Animals": "noise_animal_truck_dead", "Initial - Construction": "damaged_sign_sidewalk_missing", "Settlement Reduction Not Shown": "order_property_inspection_condition", "Hitting Building": "damaged_sign_sidewalk_missing", "Sidewalk Collapsed": "damaged_sign_sidewalk_missing", "EXPY Sign Fixt Cover": "damaged_sign_sidewalk_missing", "Hydrant Running Full (WA4)": "water_basin_litter_missed", "Other Health Matters": "odor_food_air_smoke", "EZ PASS READER": "order_property_inspection_condition", "Damaged/Defective Parts": "damaged_sign_sidewalk_missing", "CEILING": "damaged_sign_sidewalk_missing", "Commercial Overnight Parking": "damaged_sign_sidewalk_missing", "Damaged/Defective Goods": "order_property_inspection_condition", "Sodium Warning": "order_property_inspection_condition", "After Hours - Licensed Est": "license_complaint_illegal_violation", "EXPY Sign Reflector": "damaged_sign_sidewalk_missing", "Controller Cabinet": "damaged_sign_sidewalk_missing", "SEWER": "water_basin_litter_missed", "Image of Ticket": "damaged_sign_sidewalk_missing", "Street Light Lamp Dim": "damaged_sign_sidewalk_missing", "Leaky Roof": "order_property_inspection_condition", "Portable Amusement Ride License": "license_complaint_illegal_violation", "Status of Appeal": "license_complaint_illegal_violation", "Foundation": "damaged_sign_sidewalk_missing", "Not Certified": "license_complaint_illegal_violation", "Equipment Malfunction": "order_property_inspection_condition", "Controller Flasher": "damaged_sign_sidewalk_missing", "New Building": "damaged_sign_sidewalk_missing", "Process Server Organization License": "license_complaint_illegal_violation", "Summer Heat - Chinese": "english_emergency_spanish_chinese", "Information Technology": "order_property_inspection_condition", "Other/Unknown": "order_property_inspection_condition", "Home Improvement Contractor License": "license_complaint_illegal_violation", "Lack of Safety Equipment": "order_property_inspection_condition", "Allergy Information": "odor_food_air_smoke", "Time Clock Maladjusted": "damaged_sign_sidewalk_missing", "Real Property Tax Assessment/Correction": "exemption_commercial_tax_business", "Box Cover": "damaged_sign_sidewalk_missing", "Damaged Door": "damaged_sign_sidewalk_missing", "Full Term Mobile Food Vendor License": "license_complaint_illegal_violation", "Tree Leaning/Uprooted": "damaged_sign_sidewalk_missing", "Defective/Missing Curb Piece (SC4)": "damaged_sign_sidewalk_missing", "Defective Water Sampling Station (QSS)": "water_basin_litter_missed", "Lien Sale": "license_complaint_illegal_violation", "Beach/Pool Closure": "water_basin_litter_missed", "Illegal Conversion Of Commercial Bldg/Space To Other Uses": "license_complaint_illegal_violation", "Illegal/Unfair Booting": "license_complaint_illegal_violation", "Fence - None/Inadequate": "damaged_sign_sidewalk_missing", "Car Dealer - Used": "license_complaint_illegal_violation", "Touchscreen/Button Not Working": "damaged_sign_sidewalk_missing", "Blocked Bike Lane": "damaged_sign_sidewalk_missing", "Minor Received Tattoo": "license_complaint_illegal_violation", "Flood Light Lamp Missing": "damaged_sign_sidewalk_missing", "Death Certificate Before 1949 Order Form": "license_complaint_illegal_violation", "Personal SCHE Exemption": "exemption_commercial_tax_business", "Card - Charged Twice": "license_complaint_illegal_violation", "Vehicle Report": "order_property_inspection_condition", "FIRE ESCAPE": "damaged_sign_sidewalk_missing", "Sidewalk Pull Box Co": "damaged_sign_sidewalk_missing", "Hummock": "noise_animal_truck_dead", "RTMS": "order_property_inspection_condition", "Workplace - 10 or Less Staff": "order_property_inspection_condition", "Street Light Cycling": "damaged_sign_sidewalk_missing", "Electrical Wiring Defective/Exposed": "damaged_sign_sidewalk_missing", "Seasonal Food Cart Vendor Permit": "license_complaint_illegal_violation", "Prohibited Item Sale to Minor": "license_complaint_illegal_violation", "Noise, Barking Dog (NR5)": "noise_animal_truck_dead", "E6 Commercial Waste Disposal": "water_basin_litter_missed", "Highway Fence": "damaged_sign_sidewalk_missing", "Exposure from Nearby Facility": "order_property_inspection_condition", "About NYC Opportunity": "english_emergency_spanish_chinese", "Manhole Cover Broken/Making Noise (SB)": "noise_animal_truck_dead", "Detour": "order_property_inspection_condition", "School Crossing": "damaged_sign_sidewalk_missing", "General Maintenance": "order_property_inspection_condition", "Compressed Air License": "license_complaint_illegal_violation", "Equipment Complaint": "license_complaint_illegal_violation", "No Idling": "noise_animal_truck_dead", "DOOR": "damaged_sign_sidewalk_missing", "Removing Flowers/Plants": "water_basin_litter_missed", "Lane Control Signal": "damaged_sign_sidewalk_missing", "Building - Vacant, Open And Unguarded": "damaged_sign_sidewalk_missing", "installation of hydrant side post (WHFP)": "water_basin_litter_missed", "User Unlicensed": "license_complaint_illegal_violation", "Poison Ivy": "noise_animal_truck_dead", "Newspaper Box Complaint": "license_complaint_illegal_violation", "Hydrant Leaking (WC1)": "water_basin_litter_missed", "E10 Street Obstruction": "damaged_sign_sidewalk_missing", "Contamination Risk": "odor_food_air_smoke", "False Advertising": "order_property_inspection_condition", "Auctioneer License": "license_complaint_illegal_violation", "One Way": "order_property_inspection_condition", "Honorary": "order_property_inspection_condition", "Book/Stationery": "damaged_sign_sidewalk_missing", "Obstructing Public Use": "license_complaint_illegal_violation", "BASIN/SINK": "water_basin_litter_missed", "SLOW LEAK": "water_basin_litter_missed", "Absent": "order_property_inspection_condition", "Restrooms": "order_property_inspection_condition", "Pothole - Tunnel": "damaged_sign_sidewalk_missing", "BUILDING COLLAPSE/FIRE, (ASBESTOS RELATED) *FOR DEP INTERNAL USE ONLY* (HH2)": "odor_food_air_smoke", "Painted Line/Marking": "damaged_sign_sidewalk_missing", "Conduit": "order_property_inspection_condition", "Overexposure During Treatment": "order_property_inspection_condition", "12P Dead Deer": "noise_animal_truck_dead", "Boiler - Fumes/Smoke/Carbon Monoxide": "odor_food_air_smoke", "The ABCs of Housing - Russian": "english_emergency_spanish_chinese", "DAMAGE STRUCTURE/RAILING (SRGDM)": "damaged_sign_sidewalk_missing", "Required Signage Not Posted": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - Spanish": "english_emergency_spanish_chinese", "Tie Rods": "damaged_sign_sidewalk_missing", "3A Sweeping/Missed": "order_property_inspection_condition", "Multiple Street Lights Out": "damaged_sign_sidewalk_missing", "Sign Missing or Defective": "damaged_sign_sidewalk_missing", "Wood Pole Wires Exposed": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - Haitian Creole": "english_emergency_spanish_chinese", "Safety Netting/Guard Rails - Damaged/Inadequate/None (6 Stories/75 Feet Or Less)": "damaged_sign_sidewalk_missing", "Overnight Commercial Storage": "order_property_inspection_condition", "Out of Order": "order_property_inspection_condition", "Cars Parked on Sidewalk/Street": "damaged_sign_sidewalk_missing", "Capital Construction": "damaged_sign_sidewalk_missing", "Unsafe Chemical, Storage (HC1)": "water_basin_litter_missed", "Inhalation Therapy Supervising Technician License": "license_complaint_illegal_violation", "The ABCs of Housing - Haitian Creole": "english_emergency_spanish_chinese", "Container - Over 5 Gallons": "water_basin_litter_missed", "Grass/Weeds": "noise_animal_truck_dead", "Jewelry": "order_property_inspection_condition", "Sightseeing Guide License": "license_complaint_illegal_violation", "Minor Access": "order_property_inspection_condition", "Phone Blocking Sidewalk": "damaged_sign_sidewalk_missing", "BOILER": "odor_food_air_smoke", "Asbestos": "odor_food_air_smoke", "Bracket Arm Missing": "damaged_sign_sidewalk_missing", "Hydrant Knocked Over/Missing (WC)": "water_basin_litter_missed", "Toilet Facility": "water_basin_litter_missed", "Temporary": "order_property_inspection_condition", "Unauthorized Tree Pruning": "license_complaint_illegal_violation", "Toxic Chemical/Material": "odor_food_air_smoke", "Ticket Seller Business License Application": "license_complaint_illegal_violation", "Registration Clearance Request": "license_complaint_illegal_violation", "Appeals Division": "order_property_inspection_condition", "Wood Pole Leaning": "damaged_sign_sidewalk_missing", "Gas Hook-Up/Piping - Illegal Or Defective": "license_complaint_illegal_violation", "Non-med Compressed Gas - New": "odor_food_air_smoke", "Marine Lamp": "damaged_sign_sidewalk_missing", "Control Panel Damaged": "damaged_sign_sidewalk_missing", "Tires": "order_property_inspection_condition", "Dishwashing/Utensils": "odor_food_air_smoke", "Property": "order_property_inspection_condition", "10A Adopt-A-Basket": "order_property_inspection_condition", "Semi-Annual Homeless Shelter Inspection: Electrical": "order_property_inspection_condition", "Other Sewer Problem (Use Comments) (SZZ)": "water_basin_litter_missed", "Lost/Missing Person": "order_property_inspection_condition", "E3 Dirty Sidewalk": "order_property_inspection_condition", "WINDOW FRAME": "damaged_sign_sidewalk_missing", "Telco Connection Blk": "order_property_inspection_condition", "Marine Globe": "damaged_sign_sidewalk_missing", "MAILBOX": "damaged_sign_sidewalk_missing", "Scale Inaccurate/Broken": "damaged_sign_sidewalk_missing", "Sidewalk Grating - Missing": "damaged_sign_sidewalk_missing", "Pedestrian Sign": "damaged_sign_sidewalk_missing", "The ABCs of Housing - Arabic": "english_emergency_spanish_chinese", "Failure To Retain Water/Improper Drainage- (LL103/89)": "water_basin_litter_missed", "Best - Low-Rise Tracking Complaint": "order_property_inspection_condition", "Driver Complaint - Passenger": "license_complaint_illegal_violation", "Enforcement Work Order (DOB)": "license_complaint_illegal_violation", "WINDOW/FRAME": "damaged_sign_sidewalk_missing", "Air: Other Air Problem (Use Comments) (AZZ)": "odor_food_air_smoke", "Snow on Overpass": "order_property_inspection_condition", "Plumbing-Defective/Leaking/Not Maintained": "water_basin_litter_missed", "Car Service Company Complaint": "license_complaint_illegal_violation", "Chemical Odor (HD1)": "odor_food_air_smoke", "NYPD": "english_emergency_spanish_chinese", "10 Litter Basket / Request": "water_basin_litter_missed", "Noise: Other Noise Sources (Use Comments) (NZZ)": "noise_animal_truck_dead", "Fallen Debris from Tunnel": "order_property_inspection_condition", "Cloudy Or Milky, Other (Use Comments) (QBZ)": "noise_animal_truck_dead", "Entire Tree Has Fallen Down": "damaged_sign_sidewalk_missing", "Permit/License/Certificate": "license_complaint_illegal_violation", "Fallen Debris from Bridge": "order_property_inspection_condition", "Human Capital": "order_property_inspection_condition", "Air: Open Fire, Construction/Demolition (AC4)": "damaged_sign_sidewalk_missing", "Because of Violation": "license_complaint_illegal_violation", "Bag": "order_property_inspection_condition", "Application Portability": "order_property_inspection_condition", "Ready NY - Businesses - Spanish": "english_emergency_spanish_chinese", "Other - Explain Below": "order_property_inspection_condition", "Veh Signal Lamp": "damaged_sign_sidewalk_missing", "Pigeon Waste": "water_basin_litter_missed", "Commercial Exemptions": "exemption_commercial_tax_business", "DRIE Exemption": "exemption_commercial_tax_business", "Interruption of Essential Services Notice": "license_complaint_illegal_violation", "Sway Bar": "damaged_sign_sidewalk_missing", "High Pressure Sales": "order_property_inspection_condition", "14 Derelict Vehicles": "order_property_inspection_condition", "Licensee Complaint": "license_complaint_illegal_violation", "Injured Wildlife": "noise_animal_truck_dead", "Graffiti/Dirty Condition": "order_property_inspection_condition", "Flood Light Lamp Out": "damaged_sign_sidewalk_missing", "Marshal - Not Reflected": "order_property_inspection_condition", "Unlicensed Day Care": "license_complaint_illegal_violation", "Graffiti": "damaged_sign_sidewalk_missing", "Status of Payment Adjustment": "license_complaint_illegal_violation", "Damaged Vehicle": "damaged_sign_sidewalk_missing", "Blank Out Matrix Sgn": "order_property_inspection_condition", "Lamppost Base Door/Cover Open": "damaged_sign_sidewalk_missing", "E11 Litter Surveillance": "water_basin_litter_missed", "Contract Dispute": "license_complaint_illegal_violation", "Certificate of No Harassment (CONH) Application": "license_complaint_illegal_violation", "Loan Offer": "order_property_inspection_condition", "High Water Pressure (WHP)": "water_basin_litter_missed", "Pedicab Driver": "order_property_inspection_condition", "Installation/Work Quality": "damaged_sign_sidewalk_missing", "Contact Sign Not Posted": "damaged_sign_sidewalk_missing", "Water Meter Stolen/Missing - Other (CLO)": "water_basin_litter_missed", "Plumbing Problem": "water_basin_litter_missed", "BELL/BUZZER/INTERCOM": "damaged_sign_sidewalk_missing", "Accident - Cranes/Derricks/Suspension Scaffold": "order_property_inspection_condition", "Graffiti/Litter on Phone": "order_property_inspection_condition", "Property Value": "order_property_inspection_condition", "Ready NY My Emergency Plan - Russian": "english_emergency_spanish_chinese", "Status of Hearing": "noise_animal_truck_dead", "Letter Grading": "order_property_inspection_condition", "Other (Explain Below)": "damaged_sign_sidewalk_missing", "Ready NY - Flooding": "english_emergency_spanish_chinese", "Certificate of No Harassment (CONH) Exemption": "exemption_commercial_tax_business", "License Violation": "license_complaint_illegal_violation", "14B Derelict Bicycle": "order_property_inspection_condition", "Weather Head": "damaged_sign_sidewalk_missing", "Use of Newly Seeded Lawn": "order_property_inspection_condition", "E14 ASP/Restricted Parking": "license_complaint_illegal_violation", "Clear Water With Other Particles (Use Comments) (QEZ)": "water_basin_litter_missed", "Line/Marking - Faded": "damaged_sign_sidewalk_missing", "Water": "water_basin_litter_missed", "Pet Store - New License": "license_complaint_illegal_violation", "Dead Branches in Tree": "damaged_sign_sidewalk_missing", "Illegal Use Of Hose - Other (CCO)": "license_complaint_illegal_violation", "Milk Not Pasteurized": "odor_food_air_smoke", "Hours of Operation": "order_property_inspection_condition", "DOOR/FRAME": "damaged_sign_sidewalk_missing", "Complaince Inspection": "order_property_inspection_condition", "LOW WATER PRESSURE - WLWP": "water_basin_litter_missed", "Garbage": "order_property_inspection_condition", "Coin or Card Did Not Register": "license_complaint_illegal_violation", "Car/Truck Music": "noise_animal_truck_dead", "NO LIGHTING": "damaged_sign_sidewalk_missing", "LED Lense": "damaged_sign_sidewalk_missing", "House/Property Damaged": "damaged_sign_sidewalk_missing", "Animal Waste": "water_basin_litter_missed", "Lost Property": "order_property_inspection_condition", "Canopy Complaint": "damaged_sign_sidewalk_missing", "Conflict Monitor": "damaged_sign_sidewalk_missing", "Lamppost Knocked Down": "damaged_sign_sidewalk_missing", "Wrong Amount Paid or Withdrawn": "license_complaint_illegal_violation", "DOOR FRAME": "damaged_sign_sidewalk_missing", "Material Stored Improperly": "water_basin_litter_missed", "Iguana": "noise_animal_truck_dead", "Ready NY - Arabic - Full Size": "english_emergency_spanish_chinese", "Heating Problem": "odor_food_air_smoke", "Food Service Establishment License": "license_complaint_illegal_violation", "Illness/Injury": "damaged_sign_sidewalk_missing", "Safety Netting/Guard Rails - Damaged/Inadequate/None (Over 6 Stories/75 Feet)": "damaged_sign_sidewalk_missing", "Derelict Vehicles": "order_property_inspection_condition", "BATHTUB/SHOWER": "water_basin_litter_missed", "Noise: Alarms (NR3)": "noise_animal_truck_dead", "Bus Stop": "order_property_inspection_condition", "Con Edison Referral": "damaged_sign_sidewalk_missing", "Street Light Lamp Missing": "damaged_sign_sidewalk_missing", "Truck Route Violation": "license_complaint_illegal_violation", "Blocking Street": "damaged_sign_sidewalk_missing", "Information on Contracts and Contractors": "license_complaint_illegal_violation", "Status of PV Refund": "exemption_commercial_tax_business", "Sign Defect - Garage": "damaged_sign_sidewalk_missing", "Locksmith Apprentice License": "license_complaint_illegal_violation", "Vehicle Signal": "damaged_sign_sidewalk_missing", "Dead End Signal": "damaged_sign_sidewalk_missing", "High Pressure to Take on Loan/Debt": "water_basin_litter_missed", "Condo Billing Issue": "license_complaint_illegal_violation", "Depression Maintenance": "order_property_inspection_condition", "Existing Building": "damaged_sign_sidewalk_missing", "Flower Planters": "noise_animal_truck_dead", "Secondhand Dealer General License": "license_complaint_illegal_violation", "SMOKE DETECTOR": "odor_food_air_smoke", "Receipt Incomplete/Not Given": "license_complaint_illegal_violation", "Winter Health and Safety Tips Guide": "order_property_inspection_condition", "Concrete In Catch Basin (IEA)": "water_basin_litter_missed", "Misapplied Payment": "license_complaint_illegal_violation", "COOKING GAS": "odor_food_air_smoke", "Foreign Attachment On Wood Pole": "damaged_sign_sidewalk_missing", "Sidewalk Cafe License": "license_complaint_illegal_violation", "null": "order_property_inspection_condition", "STEAM PIPE/RISER": "water_basin_litter_missed", "New Automatic Public Toilet Request": "water_basin_litter_missed", "FLOOR": "damaged_sign_sidewalk_missing", "Non-Compliance w/TTPN 1/00 - Vertical Enlargements": "license_complaint_illegal_violation", "Clear Water With Organisms (Insects, Worms) (QE2)": "water_basin_litter_missed", "Flood Light Lamp Cycling": "damaged_sign_sidewalk_missing", "Swimming Pool - Unmaintained": "water_basin_litter_missed", "Ped Lens": "damaged_sign_sidewalk_missing", "Commercial Green Roof or Solar Panel Exemption": "exemption_commercial_tax_business", "Other School Condition": "order_property_inspection_condition", "News Gathering": "noise_animal_truck_dead", "Ped Visor": "damaged_sign_sidewalk_missing", "Certificate of No Harassment or Exemption - SRO": "license_complaint_illegal_violation", "Permission to Publish Contract": "license_complaint_illegal_violation", "Energy": "damaged_sign_sidewalk_missing", "Safety Inspection-Retaining Walls (May 2005)": "order_property_inspection_condition", "Driver Report": "license_complaint_illegal_violation", "Air: Odor, Sweet From Unknown Source (AZ1)": "odor_food_air_smoke", "3B Sweeping/Inadequate": "order_property_inspection_condition", "Dog Off Leash": "noise_animal_truck_dead", "Debt Collection Agency License": "license_complaint_illegal_violation", "Complaint": "order_property_inspection_condition", "Noise: Jack Hammering (NC2)": "noise_animal_truck_dead", "Assisted Living": "order_property_inspection_condition", "ULURP Project Status Questions": "order_property_inspection_condition", "Catering Establishment License": "license_complaint_illegal_violation", "Voluntary": "order_property_inspection_condition", "Taste/Odor, Sewer (QA5)": "odor_food_air_smoke", "Cable Television": "damaged_sign_sidewalk_missing", "Odor": "odor_food_air_smoke", "Commercial Rent Tax-Other": "exemption_commercial_tax_business", "WIRING": "damaged_sign_sidewalk_missing", "Excessive Water In Basement (WEFB)": "water_basin_litter_missed", "Smoking Ban - Smoking on Construction Site": "license_complaint_illegal_violation", "Commercial Not For Profit Exemption": "exemption_commercial_tax_business", "Wall/Retaining Wall - Bulging/Cracked": "damaged_sign_sidewalk_missing", "Taste": "odor_food_air_smoke", "Clothing/Glasses": "damaged_sign_sidewalk_missing", "Use Outside": "damaged_sign_sidewalk_missing", "Double Parked Blocking Traffic": "damaged_sign_sidewalk_missing", "Veh Signal Head": "damaged_sign_sidewalk_missing", "Pigeon Odor": "odor_food_air_smoke", "Debris - Falling Or In Danger Of Falling": "order_property_inspection_condition", "Branch or Limb Has Fallen Down": "damaged_sign_sidewalk_missing", "Decision and Order": "order_property_inspection_condition", "Unlicensed/Illegal/Improper Work In Progress": "license_complaint_illegal_violation", "Toy Gun Sale": "noise_animal_truck_dead", "Flood Light Lamp Dayburning": "damaged_sign_sidewalk_missing", "Injury or Illness from Tanning": "damaged_sign_sidewalk_missing", "Commercial ICP or ICAP Exemption": "exemption_commercial_tax_business", "Ready NY - Reference Card": "english_emergency_spanish_chinese", "Large Number of Mosquitoes": "noise_animal_truck_dead", "Metal Protruding - Sign Stump": "damaged_sign_sidewalk_missing", "Sidewalk Shed/Pipe Scafford - Inadequate Defective/None": "order_property_inspection_condition", "Amusement Arcade License": "license_complaint_illegal_violation", "Commercial CEP or CRP Exemption": "exemption_commercial_tax_business", "Manhole Cover Missing (Emergency) (SA3)": "order_property_inspection_condition", "Hydrotest": "water_basin_litter_missed", "Bodega/Deli/Supermarket": "odor_food_air_smoke", "Retail Laundry License Application": "license_complaint_illegal_violation", "Sewage Leak": "water_basin_litter_missed", "Electronics Store License": "license_complaint_illegal_violation", "Ready NY - Spanish - Pocket Size": "english_emergency_spanish_chinese", "Wood Pole Damaged": "damaged_sign_sidewalk_missing", "Vehicle": "order_property_inspection_condition", "Waterway-Floatables (IHC)": "water_basin_litter_missed", "Basement": "damaged_sign_sidewalk_missing", "Bill Received in Error": "license_complaint_illegal_violation", "Refund/Credit Info or Status": "license_complaint_illegal_violation", "Plate Noisy/Sunken/Raised (SB5)": "order_property_inspection_condition", "Fixture/Luminaire Damaged": "damaged_sign_sidewalk_missing", "Ready NY - English - Full Size": "english_emergency_spanish_chinese", "Commercial J51 Exemption": "exemption_commercial_tax_business", "Insurance Information Requested": "license_complaint_illegal_violation", "Puddle on Roof": "order_property_inspection_condition", "Exchange/Refund/Return": "exemption_commercial_tax_business", "Performance": "order_property_inspection_condition", "Pet/Animal": "noise_animal_truck_dead", "Noise: Private Carting Noise (NQ1)": "noise_animal_truck_dead", "Fire Alarm Lamp Missing": "damaged_sign_sidewalk_missing", "Tow Truck Driver License": "license_complaint_illegal_violation", "Blocked Hydrant": "water_basin_litter_missed", "EFT or Online Payment Problem": "license_complaint_illegal_violation", "Lead Kit Request (Residential) (L10)": "order_property_inspection_condition", "15R Street Cond/Ref.W Door": "damaged_sign_sidewalk_missing", "Chained": "damaged_sign_sidewalk_missing", "Tobacco Retail Dealer License Application": "license_complaint_illegal_violation", "E15 Illegal Postering": "license_complaint_illegal_violation", "Update Tenant Information": "license_complaint_illegal_violation", "Sports Equipment": "order_property_inspection_condition", "Secondhand Dealer Firearms License": "license_complaint_illegal_violation", "Dirt, Debris, Litter Complaint": "order_property_inspection_condition", "BBQ Outside Authorized Area": "license_complaint_illegal_violation", "Ready NY My Emergency Plan - Polish": "english_emergency_spanish_chinese", "Citywide Procurement": "license_complaint_illegal_violation", "CABINET": "damaged_sign_sidewalk_missing", "Hurricane Preparedness - English": "english_emergency_spanish_chinese", "Sustainability Enforcement Work Order": "license_complaint_illegal_violation", "Bird Bath": "noise_animal_truck_dead", "Individual Process Server License": "license_complaint_illegal_violation", "Graffiti or Vandalism": "damaged_sign_sidewalk_missing", "WiFi/Internet Not Working/Slow": "damaged_sign_sidewalk_missing", "SEP - Professional Certification Compliance Audit": "license_complaint_illegal_violation", "Det-Sens Cabinet": "order_property_inspection_condition", "Disruptive Passenger": "damaged_sign_sidewalk_missing", "Driver Complaint - Non Passenger": "license_complaint_illegal_violation", "Bikes in Buildings": "damaged_sign_sidewalk_missing", "Illegal. Commercial Use In Resident Zone": "license_complaint_illegal_violation", "Electronic Fund Transfer (EFT) Problem": "license_complaint_illegal_violation", "General Complaint": "license_complaint_illegal_violation", "Cigarette Retail Dealer License": "license_complaint_illegal_violation", "Green Roof or Solar Panel Exemption": "exemption_commercial_tax_business", "Not Received - Vending Machine": "license_complaint_illegal_violation", "Billing Name Incorrect": "license_complaint_illegal_violation", "Reflector/Louvre": "damaged_sign_sidewalk_missing", "Birth/Death Certificates": "license_complaint_illegal_violation", "Dust from Construction": "order_property_inspection_condition", "Building Foundation": "damaged_sign_sidewalk_missing", "St Name - Over Intersection": "damaged_sign_sidewalk_missing", "Traffic Signal Light": "damaged_sign_sidewalk_missing", "Grease In Sewer/Catch Basin (IDG)": "water_basin_litter_missed", "Concrete Barrier": "damaged_sign_sidewalk_missing", "Lamppost Damaged": "damaged_sign_sidewalk_missing", "SRO - Illegal Work/No Permit/Change In Occupancy/Use": "license_complaint_illegal_violation", "Street Light Feed": "damaged_sign_sidewalk_missing", "Summer Heat - Russian": "english_emergency_spanish_chinese", "Sewage Odor": "odor_food_air_smoke", "Sign Blocked by Tree": "damaged_sign_sidewalk_missing", "Aided/Injury": "damaged_sign_sidewalk_missing", "Wasting Faucets,Sinks,Flushometer,Urinal,Etc. - Other (CWO)": "water_basin_litter_missed", "Chemical Vapors/Gases/Odors": "odor_food_air_smoke", "Pothole": "order_property_inspection_condition", "Biking/Rollerblading off Path": "damaged_sign_sidewalk_missing", "Unincorporated Business Tax - Refund": "exemption_commercial_tax_business", "ABANDONED APARTMENT UNIT": "order_property_inspection_condition", "On Structure": "damaged_sign_sidewalk_missing", "Property Value Dispute": "order_property_inspection_condition", "Rough, Pitted or Cracked Roads": "order_property_inspection_condition", "Dirty/Graffiti": "order_property_inspection_condition", "Payment Not Posted": "license_complaint_illegal_violation", "Application Appeal": "license_complaint_illegal_violation", "Budget": "order_property_inspection_condition", "Debt Not Owed": "license_complaint_illegal_violation", "Inadequate Support Shoring": "damaged_sign_sidewalk_missing", "Planted Less Than 2 Years Ago": "water_basin_litter_missed", "Ready NY - English - Pocket Size": "english_emergency_spanish_chinese", "1RE Recycling Electronics": "water_basin_litter_missed", "Disabled Device Dealer": "license_complaint_illegal_violation", "Drag Racing": "order_property_inspection_condition", "NYC.gov Web Site": "english_emergency_spanish_chinese", "Ready NY - Chinese Traditional - Pocket Size": "english_emergency_spanish_chinese", "Mssg Sign Multi Lamp": "damaged_sign_sidewalk_missing", "Electrical Enforcement Work Order (DOB)": "license_complaint_illegal_violation", "Advice Request": "order_property_inspection_condition", "Credit Card Stuck in Meter": "license_complaint_illegal_violation", "Unauthorized Tree Removal": "license_complaint_illegal_violation", "Mast Arm": "damaged_sign_sidewalk_missing", "Hydrant Locking Device Request (Use Comments) (WC5)": "water_basin_litter_missed", "Bent/Loose": "damaged_sign_sidewalk_missing", "Laundry Jobber License": "license_complaint_illegal_violation", "Extra Parts": "damaged_sign_sidewalk_missing", "Bracket Arm Loose": "damaged_sign_sidewalk_missing", "Mandatory Tip": "order_property_inspection_condition", "Filing and Technical Issues": "license_complaint_illegal_violation", "Street Light Out": "damaged_sign_sidewalk_missing", "Genealogy Research Application": "order_property_inspection_condition", "Price Not Posted": "license_complaint_illegal_violation", "Non-Public Schools": "exemption_commercial_tax_business", "Education Support, Policy, and Practice": "english_emergency_spanish_chinese", "Snow Emergency": "order_property_inspection_condition", "Apply Payment or Credit": "license_complaint_illegal_violation", "Fixture/Luminaire Hanging": "damaged_sign_sidewalk_missing", "RADIATOR": "order_property_inspection_condition", "Unincorporated Business Tax - Other": "exemption_commercial_tax_business", "Hurricane Preparedness - Chinese": "english_emergency_spanish_chinese", "Adjacent Buildings Not Protected": "damaged_sign_sidewalk_missing", "Water Meter Broken/Leaking - Private Residence (CMR)": "water_basin_litter_missed", "Ready NY - Haitian Creole - Full Size": "english_emergency_spanish_chinese", "Decorative Necklace Lighting": "damaged_sign_sidewalk_missing", "Air: Odor/Fumes, Vehicle Idling (AD3)": "odor_food_air_smoke", "Defacement": "order_property_inspection_condition", "DRY WEATHER DISCHARGE - DWD": "water_basin_litter_missed", "Card - No DOF Confirmation Number Issued": "license_complaint_illegal_violation", "Sewer Break (SBR)": "water_basin_litter_missed", "Air: Odor/Fumes, Dry Cleaners (AD1)": "odor_food_air_smoke", "ER2 Resident Recyc. (Tenant)": "license_complaint_illegal_violation", "Flashing Hazard": "damaged_sign_sidewalk_missing", "EXPY Fixture": "damaged_sign_sidewalk_missing", "Clear Street Light": "damaged_sign_sidewalk_missing", "Multi Agency Joint Inspection": "order_property_inspection_condition", "Tree Trunk Split": "damaged_sign_sidewalk_missing", "Monkey": "noise_animal_truck_dead", "Construction Safety Compliance Action": "order_property_inspection_condition", "Deck Inspection": "order_property_inspection_condition", "SEWAGE": "water_basin_litter_missed", "Plate Condition - Noisy": "noise_animal_truck_dead", "Other (complaint details)": "license_complaint_illegal_violation", "No Bill of Rights": "license_complaint_illegal_violation", "Demolition - Unsafe": "order_property_inspection_condition", "Property Misclassified": "order_property_inspection_condition", "Remove Hydrant Locking Device (WC6)": "water_basin_litter_missed", "To FDNY Approved System": "license_complaint_illegal_violation", "Gender Pricing": "exemption_commercial_tax_business", "Laundry License": "license_complaint_illegal_violation", "Debris - Excessive": "order_property_inspection_condition", "Horse Drawn Carriage Driver License": "license_complaint_illegal_violation", "Unsafe Use of Playground": "order_property_inspection_condition", "Mailed - Not Reflected": "damaged_sign_sidewalk_missing", "City Rebate": "exemption_commercial_tax_business", "ECR Commercial Routing Sticker": "license_complaint_illegal_violation", "Waterway-Color (IHD)": "water_basin_litter_missed", "Other Hazmats": "order_property_inspection_condition", "Plumbing Work - Unlicensed/Illegal/Improper Work In Progress": "license_complaint_illegal_violation", "Illegal Conversion Of Manufacturing/Industrial Space": "license_complaint_illegal_violation", "No Status Call": "damaged_sign_sidewalk_missing", "Sediment": "water_basin_litter_missed", "Glassware Hanging": "damaged_sign_sidewalk_missing", "Landmark Bldg - Illegal Work": "license_complaint_illegal_violation", "Ready NY- Pandemic Flu": "english_emergency_spanish_chinese", "Unsecured Facility": "order_property_inspection_condition", "Trespassing": "order_property_inspection_condition", "Manhole Sunken/Damaged/Raised (SB1)": "water_basin_litter_missed", "Air: Smoke, Chimney or vent (AS1)": "odor_food_air_smoke", "Puddle on Sidewalk": "water_basin_litter_missed", "Finance Business Center - Not Reflected": "license_complaint_illegal_violation", "Dead/Dying Tree": "damaged_sign_sidewalk_missing", "ACRIS Incorrect": "damaged_sign_sidewalk_missing", "Wireless Antenna": "damaged_sign_sidewalk_missing", "Debt Collection Agency": "license_complaint_illegal_violation", "Communications/Intergovernmental": "damaged_sign_sidewalk_missing", "Pesticide": "odor_food_air_smoke", "Overcharge": "order_property_inspection_condition", "Temporary Tattoo License": "license_complaint_illegal_violation", "Noise: Construction Equipment (NC1)": "noise_animal_truck_dead", "Broken Glass": "damaged_sign_sidewalk_missing", "Do Not Block the Box": "damaged_sign_sidewalk_missing", "Nuisance/Truant": "noise_animal_truck_dead", "Ready NY - Spanish - Full Size": "english_emergency_spanish_chinese", "Scale Dealer or Repairer License": "license_complaint_illegal_violation", "Possible Water Main Break (Use Comments) (WA1)": "water_basin_litter_missed", "Hurricane Preparedness - Haitian Creole": "english_emergency_spanish_chinese", "Broken Lock": "damaged_sign_sidewalk_missing", "Noise: Vehicle (NR2)": "noise_animal_truck_dead", "Property Refunds and Credits": "exemption_commercial_tax_business", "Odor In Sewer/Catch Basin (ICB)": "odor_food_air_smoke", "Personal Crime Victim or Good Samaritan Exemption": "exemption_commercial_tax_business", "ER4 City Agency (Inst. Recycling)": "order_property_inspection_condition", "Broken Window": "damaged_sign_sidewalk_missing", "Fire Hydrant Emergency (FHE)": "water_basin_litter_missed", "Food Spoiled": "odor_food_air_smoke", "Rodent Sighting": "noise_animal_truck_dead", "Sandy: Building Destroyed": "damaged_sign_sidewalk_missing", "Taste/Odor, Bitter/Metallic (QA3)": "odor_food_air_smoke", "Damaged or Missing Ad Box": "damaged_sign_sidewalk_missing", "Rent Discrepancy": "license_complaint_illegal_violation", "Facade (LL11/98)- Unsafe Notification": "damaged_sign_sidewalk_missing", "Homestead": "damaged_sign_sidewalk_missing", "Dog": "noise_animal_truck_dead", "Illegal Hotel Rooms In Residential Building": "damaged_sign_sidewalk_missing", "General Vendor Distributor License": "license_complaint_illegal_violation", "Recycling Electronics": "water_basin_litter_missed", "Cash Assistance": "order_property_inspection_condition", "Cable": "damaged_sign_sidewalk_missing", "Snow Removal": "order_property_inspection_condition", "STAIRS": "damaged_sign_sidewalk_missing", "Damaged Leg or Pole Bent": "damaged_sign_sidewalk_missing", "Det-Sens Amplifier": "noise_animal_truck_dead", "Warning Signal Lamp": "damaged_sign_sidewalk_missing", "Food Contaminated": "odor_food_air_smoke", "Photocell (PEC) Missing": "damaged_sign_sidewalk_missing", "Asbestos Complaint (B1)": "license_complaint_illegal_violation", "Structure - Outdoors": "damaged_sign_sidewalk_missing", "Bicycle Chained to Tree": "damaged_sign_sidewalk_missing", "Facility Maintenance": "order_property_inspection_condition", "Trees and Sidewalks Program": "damaged_sign_sidewalk_missing", "Taste/Odor, Chlorine (QA1)": "odor_food_air_smoke", "Material Storage - Unsafe": "order_property_inspection_condition", "Retaining Wall Tracking Complaint": "damaged_sign_sidewalk_missing", "DCP/BSA Compliance Inspection": "license_complaint_illegal_violation", "Property - Other Billing Issue": "license_complaint_illegal_violation", "Sidewalk Blocked": "damaged_sign_sidewalk_missing", "Broken Sidewalk": "damaged_sign_sidewalk_missing", "Unauthorized Bus Layover": "license_complaint_illegal_violation", "Enclosure Cap": "order_property_inspection_condition", "Engine Idling": "noise_animal_truck_dead", "Guide Rail": "damaged_sign_sidewalk_missing", "Waterway-Sewage (IHA)": "water_basin_litter_missed", "Tow Truck Exemption License": "exemption_commercial_tax_business", "Natural Gas In Sewer/Catch Basin (IFB)": "water_basin_litter_missed", "Cell Phone Store": "order_property_inspection_condition", "With License Plate": "order_property_inspection_condition", "Retail Store": "order_property_inspection_condition", "Commercial Other Exemption": "exemption_commercial_tax_business", "Failure to Comply with Vacate Order": "license_complaint_illegal_violation", "Boiler - Defective/Inoperative/No Permit": "odor_food_air_smoke", "Sidewalk Consultation": "damaged_sign_sidewalk_missing", "Roots Damaged": "damaged_sign_sidewalk_missing", "Noise: air condition/ventilation equipment (NV1)": "noise_animal_truck_dead", "Controller": "damaged_sign_sidewalk_missing", "Trunk Damaged": "damaged_sign_sidewalk_missing", "Application Renewal": "license_complaint_illegal_violation", "Labor violation": "license_complaint_illegal_violation", "Plumbing Work - Illegal/No Permit/Standpipe/Sprinkler": "license_complaint_illegal_violation", "Highway Flooding (SH)": "water_basin_litter_missed", "The ABCs of Housing - Spanish": "english_emergency_spanish_chinese", "Unlicensed": "license_complaint_illegal_violation", "Lane Station": "damaged_sign_sidewalk_missing", "Defective Streetlight": "damaged_sign_sidewalk_missing", "Catch Basin Grating Missing (SA4)": "water_basin_litter_missed", "Noise: Loud Music/Daytime (Mark Date And Time) (NN1)": "noise_animal_truck_dead", "Inaccurate Meter": "order_property_inspection_condition", "Branches Damaged": "damaged_sign_sidewalk_missing", "Broken Fence": "damaged_sign_sidewalk_missing", "Sidewalk Caf\u00c3\u00a9": "damaged_sign_sidewalk_missing", "Street Fair Vendor License": "license_complaint_illegal_violation", "List of Outstanding Tickets": "order_property_inspection_condition", "ELECTRIC/GAS RANGE": "odor_food_air_smoke", "Administration": "damaged_sign_sidewalk_missing", "1RG Missed Recycling Paper": "water_basin_litter_missed", "Guard Rail - Bridge": "damaged_sign_sidewalk_missing", "Turn Signal": "damaged_sign_sidewalk_missing", "Rough Pavement": "order_property_inspection_condition", "Best - DM Tracking Complaint": "license_complaint_illegal_violation", "RAIN GARDEN DEBRIS (SRGDBR)": "water_basin_litter_missed", "LIGHTING": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - Traditional Chinese": "english_emergency_spanish_chinese", "Elevator - Dangerous Condition/Shaft Open/Unguarded": "order_property_inspection_condition", "E7 Private Carter Spillage": "water_basin_litter_missed", "Personal DHE Exemption": "exemption_commercial_tax_business", "Oil, Grease In Water (QD1)": "water_basin_litter_missed", "Damaged Toilet/Sink": "water_basin_litter_missed", "Time Switch": "damaged_sign_sidewalk_missing", "NO WATER - WNW": "water_basin_litter_missed", "Dead Animal": "noise_animal_truck_dead", "Cloudy Or Milky Water (QB1)": "water_basin_litter_missed", "8 Request to Clean Vacant Lot": "order_property_inspection_condition", "ER6 Comm. Recyc. (Comm. Tenant)": "license_complaint_illegal_violation", "Electrical - Unlicensed/Illegal/Improper Work In Progress": "license_complaint_illegal_violation", "Accident/Explosion - Boiler": "odor_food_air_smoke"}

Apply doc_to_topic_map on service data

In [ ]:
service_data = service_data.with_columns(
    pl.col("Descriptor").replace(doc_to_topic_map).alias("DG") # DG Shorthand for descriptor Groups
)

#### Step 2: How to encode

My proposed method for how to encode each feature is to basically treat each category of the feature as a summed numerical variable. For each day, I will calculate the total number of tickets associated with each category and use that as the feature vector. For instance, I will encode the fact there were 300 tickets filed to the BRONX on 01/01/2016 as a row to the category vector: Borough_BRONX. To do this, first we one hot encode the categories, then we aggregate across each day via summation.

In [ ]:
# Redefine our categorical features based on analysis above
FEATURES['cat'] = ["AG", "Borough", "DG"]

One Hot Encoding

In [ ]:
service_data = service_data.to_dummies(columns=FEATURES['cat'])

# Uncomment to show head
# service_data.select(pl.col('^AG_.*$'), pl.col('^Borough_.*$')).head()

Aggregate across Date by summing the counts

In [ ]:
cat_df = service_data.rename({"Created Date": "Datetime"}).group_by("Datetime").agg(
    # Categorical Features Sum
    pl.col('^AG_.*$').sum(),
    pl.col('^Borough_.*$').sum(),
    pl.col('^DG_.*$').sum(),
).sort(by="Datetime")

# cat_df.head()

#### Step 3: Concatenate to Final Dataframe

In [ ]:
sd_df = pl.concat([sd_df, cat_df.drop("Datetime")], how="horizontal")

## One Call to Build Them All (311 Service)

Build all service features with one function

In [ ]:
def build_service_data(filename):
    # Loading data directly with polars leads to errors
    # Some rows end up missing for an unknown reason
    # FIX: Load in pandas then convert to polars
    service_data_pd = pd.read_csv(filename)

    # Quick test to assure the unique key is in fact unique
    assert service_data_pd["Unique Key"].nunique() == len(service_data_pd)
    
    # Load from pandas Dataframe
    service_data_pd["Incident Zip"] = service_data_pd["Incident Zip"].astype("string")
    service_data_pd["BBL"] = service_data_pd["BBL"].astype("string")
    service_data = pl.DataFrame(service_data_pd)
    
    # Clear some ram
    del service_data_pd
    gc.collect()

    drop_cols = [
        "Unique Key", "Agency Name", "Location Type", "Incident Zip",
        "Incident Address", "Street Name", "Cross Street 1",
        "Cross Street 2", "Intersection Street 1", "Intersection Street 2",
        "Address Type", "City", "Landmark", "Facility Type",
        "Status", "Due Date", "Resolution Description",
        "Resolution Action Updated Date", "Community Board",
        "BBL", "X Coordinate (State Plane)", "Y Coordinate (State Plane)",
        "Open Data Channel Type", "Park Facility Name", "Park Borough",
        "Vehicle Type", "Taxi Company Borough", "Taxi Pick Up Location",
        "Bridge Highway Name", "Bridge Highway Direction", "Road Ramp",
        "Bridge Highway Segment", "Location", "Created Year"
    ]

    # Drop columns and create the date variable
    service_data = service_data.drop(drop_cols)
    service_data = create_datetime(service_data, "Created Date")
    service_data = create_datetime(service_data, "Closed Date")

    # Group by date to get the number of Created tickets (as target)
    sd_grouped = service_data.rename({"Created Date": "Datetime"}).group_by("Datetime").agg(
        pl.len().alias("Target"),
    ).sort(by="Datetime")

    # Calculate the number of closed tickets
    # Mean diff used to filter service data
    # mean_diff = service_data.with_columns(
    #     diff_created_closed = pl.col("Closed Date") - pl.col("Created Date")
    # ).filter((pl.col("Closed Date").dt.year() >= 2016) & (pl.col("Closed Date").dt.year() < 2020))["diff_created_closed"].mean().days
    # Mean diff precalculated as 
    mean_diff = 13

    # Create new Closed date with errors filled using the mean diff above
    service_data = service_data.with_columns(
        Closed_Date_New = pl.when(pl.col("Created Date") - pl.col("Closed Date")  > pl.duration(days=1))
                                .then(pl.col("Created Date") + pl.duration(days=mean_diff))
                                .otherwise(pl.col("Closed Date")).fill_null(pl.col("Created Date") + pl.duration(days=mean_diff))
    )

    # Filter tickets such that the closed date < the created date to prevent future data leakage in our dataset
    # We want to make sure future data is not accidentally leaked across other points in our data
    closed_tickets = service_data.group_by(["Closed_Date_New", "Created Date"]) \
        .agg((pl.when(pl.col("Created Date") <= pl.col("Closed_Date_New")).then(1).otherwise(0)).sum().alias("count")) \
        .sort("Closed_Date_New") \
        .filter((pl.col("Closed_Date_New").dt.year() >= 2016) & (pl.col("Closed_Date_New").dt.year() < 2019)) \
        .group_by("Closed_Date_New").agg(pl.col("count").sum().alias("num_closed_tickets"))

    # Rename this column to num closed tickets
    ct_df = closed_tickets.with_columns(
        pl.col("num_closed_tickets")
    )

    # Concat the new columns into our data
    sd_df = pl.concat([sd_grouped, ct_df.drop("Closed_Date_New")], how="horizontal")

    assert len(sd_grouped) == len(ct_df)

    # CATEGORICAL FEATURE MAPPING
    # MAPPING FOR BOROUGH
    Borough_Map = {
        "Unspecified": "OTHER",
        "2017": "OTHER",
        None: "OTHER",
        "2016": "OTHER"
    }
    service_data = service_data.with_columns(
        pl.col("Borough").replace(Borough_Map)
    )

    # MAPPING FOR AGENCY
    # This mapping was done Manually
    Agency_Map = {
        "NYPD": "Security", "HPD": "Buildings", "DOT": "Transportation",
        "DSNY": "Environment & Sanitation", "DEP": "Environment & Sanitation",
        "DOB": "Buildings", "DOE": "Buildings", "DPR": "Parks",
        "DOHMH": "Health", "DOF": "Other", "DHS": "Security",
        "TLC": "Transportation", "HRA": "Other", "DCA": "Other",
        "DFTA": "Other", "EDC": "Other", "DOITT": "Other", "OMB": "Other",
        "DCAS": "Other", "NYCEM": "Other", "ACS": "Other", "3-1-1": "Other",
        "TAX": "Other", "DCP": "Other", "DORIS": "Other", "FDNY": "Other",
        "TAT": "Other", "COIB": "Other", "CEO": "Other", "MOC": "Other",
    }
    
    service_data = service_data.with_columns(
        pl.col("Agency").replace(Agency_Map).alias("AG") # AG Shorthand for Agency Groups
    )


    # Mapping for Descriptor using BERTopic
    # Store descriptors as pandas dataframe (polars not supported)
    # Drop any nan values, and we only care about the unique values
    descriptor_docs = service_data["Descriptor"].unique().to_numpy()
    
    # # Build our topic mapping using the pretrained BERTopic model
    # # Load model and get predictions
    # topic_model = BERTopic.load("models/BERTopic")
    # topics, probs = topic_model.transform(descriptor_docs)
    
    # # Visualize if wanted
    # # topic_model.visualize_barchart(list(range(-1,6,1)))
    
    # # Create a topic to ID map
    # topic_df = topic_model.get_topic_info()
    # topic_id_map = {row["Topic"]: row["Name"][2:] for _, row in topic_df.iterrows()}
    # topic_id_map[-1] = topic_id_map[-1][1:] # Fix for the -1 topic case
    
    # # For each document (descriptor string) get a mapping of topics
    # doc_to_topic_map = defaultdict(str)
    # for topic_id, doc in zip(topics, descriptor_docs):
    #     topic = topic_id_map[topic_id]
    #     doc_to_topic_map[doc] = topic
    doc_to_topic_map = {"Damaged/Defective": "damaged_sign_sidewalk_missing", "Catch Basin Search (SC2)": "water_basin_litter_missed", "No Consent Form": "license_complaint_illegal_violation", "Delays": "order_property_inspection_condition", "FDNY Referral - Pilot": "license_complaint_illegal_violation", "Adult Establishment": "damaged_sign_sidewalk_missing", "Temporary Amusement Device License": "license_complaint_illegal_violation", "ROOFING": "damaged_sign_sidewalk_missing", "The ABCs of Housing - Chinese": "damaged_sign_sidewalk_missing", "RAIN GARDEN FLOODING (SRGFLD)": "water_basin_litter_missed", "Domestic Strays": "noise_animal_truck_dead", "Co-op or Condo Abatement": "order_property_inspection_condition", "CARBON MONOXIDE DETECTOR": "odor_food_air_smoke", "E5 Loose Rubbish": "water_basin_litter_missed", "Plate Missing/Moved-Exposing Hole (SB4)": "damaged_sign_sidewalk_missing", "Facility Unregistered": "license_complaint_illegal_violation", "Lighting - Garage": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - English": "english_emergency_spanish_chinese", "Dealer in Devices for Disabled License": "license_complaint_illegal_violation", "Excise Taxes-Refund": "exemption_commercial_tax_business", "Plate Noisy/Sunken/Raised (WF5)": "noise_animal_truck_dead", "Plate Condition - Shifted": "order_property_inspection_condition", "MCI Abatement": "order_property_inspection_condition", "Going Out of Business Sale License": "license_complaint_illegal_violation", "Failure to Comply with Annual Crane Inspection": "license_complaint_illegal_violation", "Booting Company License": "license_complaint_illegal_violation", "Crane/Suspension Scaffold - No Permit/License/Cert./Unsafe/Illegal": "license_complaint_illegal_violation", "Stalled Construction Site": "damaged_sign_sidewalk_missing", "ER5 Comm. Recyc. (Bldg Mgmt)": "order_property_inspection_condition", "M.A.R.C.H. Program (Interagency)": "license_complaint_illegal_violation", "General Bad Condition": "order_property_inspection_condition", "Ped Multiple Lamps": "damaged_sign_sidewalk_missing", "Plate Condition - Anti-Skid": "order_property_inspection_condition", "Inadequate or No Heat": "odor_food_air_smoke", "Office of Preventive Technical Assistance/OPTA": "order_property_inspection_condition", "1RE missed collection for E-waste": "water_basin_litter_missed", "Bowstring Truss Tracking Complaint": "license_complaint_illegal_violation", "ALJ Division": "order_property_inspection_condition", "Chemical Spill (IAC)": "water_basin_litter_missed", "Chemical Spill/Release (HA1)": "water_basin_litter_missed", "Miscellaneous": "order_property_inspection_condition", "Sidewalk Grating - Defective": "damaged_sign_sidewalk_missing", "Defective Hardware": "damaged_sign_sidewalk_missing", "DOOR TO DUMBWAITER": "damaged_sign_sidewalk_missing", "Street Flooding (SJ)": "order_property_inspection_condition", "1RO Missed Recycling Organics": "water_basin_litter_missed", "Sign Defect - Lot": "damaged_sign_sidewalk_missing", "Door Open with Air Conditioning On": "odor_food_air_smoke", "Medicaid": "english_emergency_spanish_chinese", "Broken Curb": "damaged_sign_sidewalk_missing", "Street Light Dayburning": "damaged_sign_sidewalk_missing", "Defective Street Cut (WZZ1)": "damaged_sign_sidewalk_missing", "LED Pedestrian Unit": "damaged_sign_sidewalk_missing", "Illegal Commercial Or Manufacturing Use In a C1 Or C2 Zone": "license_complaint_illegal_violation", "Illness Caused by Drinking Water": "water_basin_litter_missed", "unknown odor/taste in drinking water (QA6)": "odor_food_air_smoke", "Sewer Backup (Use Comments) (SA)": "water_basin_litter_missed", "Status Call": "order_property_inspection_condition", "Parking Permit Improper Use": "license_complaint_illegal_violation", "OUTLET/SWITCH": "damaged_sign_sidewalk_missing", "Blocked Sidewalk": "damaged_sign_sidewalk_missing", "Police Report Requested": "order_property_inspection_condition", "In-Line Fuse Missing": "damaged_sign_sidewalk_missing", "Commercial ICIP or ICAP Exemption": "exemption_commercial_tax_business", "Copy of Approval Order": "license_complaint_illegal_violation", "Accessibility Accommodations": "order_property_inspection_condition", "Curb Cut/Driveway/Carport - Illegal": "license_complaint_illegal_violation", "Dry Cleaning Vapors (PERC)": "odor_food_air_smoke", "Multiple St Lts Dayburning": "odor_food_air_smoke", "Seasonal Mobile Food Vendor License": "license_complaint_illegal_violation", "Documents Not Returned": "license_complaint_illegal_violation", "Noise: Loud Music/Nighttime(Mark Date And Time) (NP1)": "noise_animal_truck_dead", "Contractor Responsibility/VENDEX": "license_complaint_illegal_violation", "Cigarette Vending Machine": "license_complaint_illegal_violation", "Hurricane Preparedness - Spanish": "english_emergency_spanish_chinese", "Inattentive": "noise_animal_truck_dead", "Suspended (Hanging) Scaffolds - No Pmt/Lic/Dangerous/Accident": "damaged_sign_sidewalk_missing", "Zoning - Non-Conforming/Illegal Vehicle Storage": "license_complaint_illegal_violation", "Rates Not Posted": "license_complaint_illegal_violation", "Illegal Use Of Hose - Private Residence": "license_complaint_illegal_violation", "Flooded": "water_basin_litter_missed", "Chronic Speeding": "license_complaint_illegal_violation", "Detached Trailer": "order_property_inspection_condition", "Car Service Company Report": "license_complaint_illegal_violation", "Status of Request to file Paper RPIE": "license_complaint_illegal_violation", "Double Parked Blocking Vehicle": "damaged_sign_sidewalk_missing", "Ready NY - Russian - Pocket Size": "english_emergency_spanish_chinese", "Maintenance Cover": "order_property_inspection_condition", "Rat Sighting": "noise_animal_truck_dead", "Broken Water Fountain": "water_basin_litter_missed", "Marine Flasher": "order_property_inspection_condition", "In Car": "order_property_inspection_condition", "Posted Parking Sign Violation": "license_complaint_illegal_violation", "Food Source/Protection": "odor_food_air_smoke", "Commercial Rent Tax- Refund": "exemption_commercial_tax_business", "Tenant Refusal": "license_complaint_illegal_violation", "Air: Smoke, Residential (AA1)": "odor_food_air_smoke", "Lost and Found": "order_property_inspection_condition", "HEAVY FLOW": "water_basin_litter_missed", "Leak (Use Comments) (WA2)": "water_basin_litter_missed", "Ready NY - Russian - Full Size": "english_emergency_spanish_chinese", "Commercial 421A Exemption": "exemption_commercial_tax_business", "Oil Spill Into Basin/Sewer - Small (IABS)": "water_basin_litter_missed", "Licensed Home Improvement Contractor Bumper Sticker": "license_complaint_illegal_violation", "Food Worker Hygiene": "odor_food_air_smoke", "Accident - Construction/Plumbing": "order_property_inspection_condition", "Ready NY Guide - Pocket Sized - English": "english_emergency_spanish_chinese", "Failure to Post Calorie Information": "license_complaint_illegal_violation", "Bees/Wasps - Not a beekeper": "noise_animal_truck_dead", "Taste/Odor, Chemical (QA2)": "odor_food_air_smoke", "Traffic Camera": "damaged_sign_sidewalk_missing", "Real Estate Services": "order_property_inspection_condition", "Building": "damaged_sign_sidewalk_missing", "Hyd Valve Box Cover Missing (WV2)": "water_basin_litter_missed", "Emergency Notice": "order_property_inspection_condition", "Advance Fee": "license_complaint_illegal_violation", "Cleanliness": "odor_food_air_smoke", "Frozen Dessert Manufacturer License": "license_complaint_illegal_violation", "Crash Cushion Defect": "damaged_sign_sidewalk_missing", "Fleet": "order_property_inspection_condition", "Plants- Odor Related Problems (PO1)": "odor_food_air_smoke", "Fixture/Luminaire Door Open": "damaged_sign_sidewalk_missing", "Parking Card Stuck in Meter": "license_complaint_illegal_violation", "Damaged Telephone": "damaged_sign_sidewalk_missing", "Illegal Conversion Of Residential Building/Space": "license_complaint_illegal_violation", "Illegal Tree Removal/Topo. Change in SNAD": "order_property_inspection_condition", "E12 Illegal Dumping Surveillance": "license_complaint_illegal_violation", "Seizure of Funds": "license_complaint_illegal_violation", "Facility Construction": "damaged_sign_sidewalk_missing", "Inspection Work Order (DOB)": "license_complaint_illegal_violation", "City Planning Commission": "damaged_sign_sidewalk_missing", "Time Insufficient": "order_property_inspection_condition", "Notice of Housing Code Enforcement Issues": "order_property_inspection_condition", "Guard Rail - Street": "damaged_sign_sidewalk_missing", "Commercial 421B Exemption": "exemption_commercial_tax_business", "Air Conditioning Problem": "odor_food_air_smoke", "APARTMENT ONLY": "damaged_sign_sidewalk_missing", "Wasting Faucets,Sinks,Flushometer,Urinal,Etc. - Private Residence (CWR)": "water_basin_litter_missed", "Lack of Supplies": "order_property_inspection_condition", "Ready NY - Chinese Simplified - Full Size": "english_emergency_spanish_chinese", "Noise, Other Animals (NR6)": "noise_animal_truck_dead", "Cellar Door Open/Unprotected": "damaged_sign_sidewalk_missing", "Unauthorized Climbing": "license_complaint_illegal_violation", "Remove Mortgage": "damaged_sign_sidewalk_missing", "Sidewalk Staircase": "damaged_sign_sidewalk_missing", "Wood Pole Missing": "damaged_sign_sidewalk_missing", "CMU Communication": "noise_animal_truck_dead", "OUTLET COVER": "damaged_sign_sidewalk_missing", "Illegal Tow": "order_property_inspection_condition", "Projects": "damaged_sign_sidewalk_missing", "Yield": "order_property_inspection_condition", "Egress - Doors Locked/Blocked/Improper/No Secondary Means": "damaged_sign_sidewalk_missing", "Housing Information Guide For Tenants and Owners Notice": "license_complaint_illegal_violation", "Detector Sensor": "noise_animal_truck_dead", "Cave-in": "noise_animal_truck_dead", "Partial Access": "order_property_inspection_condition", "Scale Inaccurate": "order_property_inspection_condition", "Cat": "noise_animal_truck_dead", "Noise, Ice Cream Truck (NR4)": "noise_animal_truck_dead", "ER1 Resident Recyc. (Owner/Manager": "license_complaint_illegal_violation", "E30 Transfer Station": "water_basin_litter_missed", "Ready NY - Kids - Elementary School Students": "english_emergency_spanish_chinese", "WINDOW PANE": "damaged_sign_sidewalk_missing", "Construction Enforcement Work Order (DOB)": "license_complaint_illegal_violation", "Ready NY - Businesses - English": "english_emergency_spanish_chinese", "V.E.S.T. Program (DOB & NYPD)": "license_complaint_illegal_violation", "Culvert Blocked/Needs Cleaning (SE)": "water_basin_litter_missed", "General Vendor Waiting List Application": "license_complaint_illegal_violation", "Sprinkler System - Inadequate": "water_basin_litter_missed", "Electronics and Home Appliance Service Dealer License": "license_complaint_illegal_violation", "Police Report Not Requested": "license_complaint_illegal_violation", "15S Re-Plow/Spread/Ice-Snow Cond.": "order_property_inspection_condition", "Lamppost Wire Exposed": "damaged_sign_sidewalk_missing", "Copy of Notice of Property Value": "license_complaint_illegal_violation", "Announcements": "order_property_inspection_condition", "Door": "damaged_sign_sidewalk_missing", "Condition Attracting Rodents": "noise_animal_truck_dead", "Returns Not Filed": "exemption_commercial_tax_business", "Do Not Enter": "damaged_sign_sidewalk_missing", "E1 Improper Disposal": "water_basin_litter_missed", "Waive Penalty for Late Payment": "license_complaint_illegal_violation", "9 Spill/Oil etc": "water_basin_litter_missed", "Bracket Arm Broken": "damaged_sign_sidewalk_missing", "Demand for Cash": "exemption_commercial_tax_business", "General Counsel": "damaged_sign_sidewalk_missing", "Gas Utility Referral": "license_complaint_illegal_violation", "After Hours Work - Illegal": "license_complaint_illegal_violation", "Unincorporated Business Tax - Return Filing": "exemption_commercial_tax_business", "Unleashed Dog in Public": "noise_animal_truck_dead", "Hydrant Defective (WC2)": "water_basin_litter_missed", "Plumbing Enforcement Work Order (DOB)": "license_complaint_illegal_violation", "Ready NY My Emergency Plan - Korean": "english_emergency_spanish_chinese", "Fire Alarm Lamp Cycling": "damaged_sign_sidewalk_missing", "Driver Complaint": "license_complaint_illegal_violation", "TAC Report": "order_property_inspection_condition", "Full Term Tattoo License": "license_complaint_illegal_violation", "Mapping Information": "order_property_inspection_condition", "ENTIRE BUILDING": "damaged_sign_sidewalk_missing", "Dirt, Litter, Debris - Lot": "water_basin_litter_missed", "Building Shaking/Vibrating/Structural Stability": "damaged_sign_sidewalk_missing", "Personal Veteran Exemption": "exemption_commercial_tax_business", "Secondhand Dealer Auto License": "license_complaint_illegal_violation", "Business Tax": "exemption_commercial_tax_business", "Illegal Conversion No Access Follow - UP": "license_complaint_illegal_violation", "High Grass": "order_property_inspection_condition", "Lighting": "damaged_sign_sidewalk_missing", "Stop": "order_property_inspection_condition", "MAINTENANCE": "order_property_inspection_condition", "1 or 2": "order_property_inspection_condition", "22 Weeds": "noise_animal_truck_dead", "Integrity Complaint Referral": "license_complaint_illegal_violation", "2 Bulk-Missed Collection": "water_basin_litter_missed", "Sightseeing Bus License": "license_complaint_illegal_violation", "Red Lt Camera Feed": "damaged_sign_sidewalk_missing", "Fountain - Over 5 Gallons": "water_basin_litter_missed", "WINDOW GUARD BROKEN/MISSING": "damaged_sign_sidewalk_missing", "Copy of Statement": "order_property_inspection_condition", "\\E4 18\\\"\\\" Law\\\"\"": "order_property_inspection_condition", "Stop Temporary": "order_property_inspection_condition", "Farm Animal": "noise_animal_truck_dead", "Catch Basin Sunken/Damaged/Raised (SC1)": "water_basin_litter_missed", "General Inquiry": "order_property_inspection_condition", "Planted More Than 2 Years Ago": "water_basin_litter_missed", "Structurally Compromised Building (LL33/08)": "damaged_sign_sidewalk_missing", "For One Address": "order_property_inspection_condition", "Relocation of Bus Stop Shelter": "order_property_inspection_condition", "Mitchell-Lama Housing List": "order_property_inspection_condition", "Semi-Annual Homeless Shelter Inspection: Plumbing": "order_property_inspection_condition", "Dead End Sign": "damaged_sign_sidewalk_missing", "No Statement of Job Conditions": "order_property_inspection_condition", "1 Missed Collection": "order_property_inspection_condition", "Landlord Inquiries": "order_property_inspection_condition", "\\Smoking Signs - \\\"\\\"No Smoking\\\"\\\" Signs Not Observed on Construction Site\\\"\"": "odor_food_air_smoke", "Dirty/Inadequate Equip./Facility": "order_property_inspection_condition", "DAMP SPOT": "order_property_inspection_condition", "SPRINKLER": "order_property_inspection_condition", "Kitchen/Food Prep Area": "odor_food_air_smoke", "ROOF DOOR/HATCH": "damaged_sign_sidewalk_missing", "FENCING": "damaged_sign_sidewalk_missing", "Dirt, Litter, Debris - Garage": "water_basin_litter_missed", "Demolition Notification Received": "damaged_sign_sidewalk_missing", "In Post Base": "damaged_sign_sidewalk_missing", "Lamppost Base Door/Cover Damaged": "damaged_sign_sidewalk_missing", "Zoning and Land Use Questions/Information": "order_property_inspection_condition", "Beekeeping - Honeybees": "noise_animal_truck_dead", "Graffiti - Highway": "damaged_sign_sidewalk_missing", "Warning Buzzer": "noise_animal_truck_dead", "Loose Plate": "order_property_inspection_condition", "Commercial UDAAP Exemption": "exemption_commercial_tax_business", "Commercial 421G Exemption": "exemption_commercial_tax_business", "Restroom Non-Complaince With Local Law 79/16": "license_complaint_illegal_violation", "Summer Heat - Spanish": "english_emergency_spanish_chinese", "Wood Pole Knocked Down": "damaged_sign_sidewalk_missing", "Missing Complaint Sign": "license_complaint_illegal_violation", "Fence": "damaged_sign_sidewalk_missing", "Incorrect Amount Paid": "license_complaint_illegal_violation", "Ready NY - French - Full Size": "english_emergency_spanish_chinese", "Animal Odor": "noise_animal_truck_dead", "Roof Gutters": "damaged_sign_sidewalk_missing", "RPIE": "order_property_inspection_condition", "Payment Misapplied": "license_complaint_illegal_violation", "Dumpster - Causing Damage": "water_basin_litter_missed", "Cellar Door Defective": "damaged_sign_sidewalk_missing", "EEO": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - Italian": "english_emergency_spanish_chinese", "Pawn Broker License": "license_complaint_illegal_violation", "Hydrant Running (WC3)": "water_basin_litter_missed", "MOLD": "odor_food_air_smoke", "Barbershop License": "license_complaint_illegal_violation", "Base Door": "damaged_sign_sidewalk_missing", "Tax Commission Rules": "exemption_commercial_tax_business", "Personal Exemptions": "exemption_commercial_tax_business", "Ped Lamp": "damaged_sign_sidewalk_missing", "Food Stamp": "odor_food_air_smoke", "SIGNAGE MISSING": "damaged_sign_sidewalk_missing", "Electronics/Phones": "order_property_inspection_condition", "Animal Grooming License": "license_complaint_illegal_violation", "Ready NY - Pets - English": "english_emergency_spanish_chinese", "Non-Disclosure of Fees": "exemption_commercial_tax_business", "Loud Talking": "noise_animal_truck_dead", "Wildlife Sighting": "noise_animal_truck_dead", "Flavored Tobacco": "odor_food_air_smoke", "Bag/Wallet": "order_property_inspection_condition", "Beach/Pool Water": "water_basin_litter_missed", "No Water (WNW)": "water_basin_litter_missed", "Building Information/Construction History": "damaged_sign_sidewalk_missing", "Language Access Coordinator": "english_emergency_spanish_chinese", "Investigative Inspection": "order_property_inspection_condition", "Illegal Dumping": "order_property_inspection_condition", "Elevator - Multiple Devices On Property": "order_property_inspection_condition", "Property Address Incorrect": "order_property_inspection_condition", "WATER SUPPLY": "water_basin_litter_missed", "Billing Address Incorrect": "license_complaint_illegal_violation", "Food Worker Activity": "odor_food_air_smoke", "Car/Truck Horn": "noise_animal_truck_dead", "Underage - Licensed Est": "license_complaint_illegal_violation", "Gaming Cafe License": "license_complaint_illegal_violation", "TOILET": "water_basin_litter_missed", "No Receipt": "license_complaint_illegal_violation", "Contrary To LL 58/87(Handicapped Access)": "order_property_inspection_condition", "Condo or Co-op Abatement": "order_property_inspection_condition", "Equipment": "order_property_inspection_condition", "HomeFirst Down Payment Information": "license_complaint_illegal_violation", "Injury/Safety": "damaged_sign_sidewalk_missing", "Manhole Overflow (Use Comments) (SA1)": "water_basin_litter_missed", "15 Street Cond/Dump-Out/Drop-Off": "order_property_inspection_condition", "Strip Paving": "order_property_inspection_condition", "1C Uncollected Xmas Trees": "order_property_inspection_condition", "Fixture(S)": "damaged_sign_sidewalk_missing", "For Violation": "license_complaint_illegal_violation", "Working Contrary To Stop Work Order": "order_property_inspection_condition", "Elevator - Single Device On Property/No Alternate Service": "order_property_inspection_condition", "St Name - Attached to Pole": "damaged_sign_sidewalk_missing", "Handwashing": "odor_food_air_smoke", "Waterway-Oil/Gasoline (IHB)": "water_basin_litter_missed", "Turtle Under 4 inches Long": "noise_animal_truck_dead", "No Permit or License": "license_complaint_illegal_violation", "Non Retail Food Processing Establishment License": "license_complaint_illegal_violation", "WALL": "damaged_sign_sidewalk_missing", "Bike Rack Repair": "damaged_sign_sidewalk_missing", "Open Excavation (WZZ2)": "order_property_inspection_condition", "No Dial Tone": "noise_animal_truck_dead", "Push Button": "damaged_sign_sidewalk_missing", "Pothole - Highway": "damaged_sign_sidewalk_missing", "Homeless Issue": "order_property_inspection_condition", "Summer Heat - English": "english_emergency_spanish_chinese", "Sidewalk Violation": "damaged_sign_sidewalk_missing", "Semi-Annual Homeless Shelter Inspection: Construction": "order_property_inspection_condition", "Non-Delivery of Papers": "license_complaint_illegal_violation", "Oil Spill On Street, Small (HQS)": "water_basin_litter_missed", "For Letter of Defect": "order_property_inspection_condition", "Business Opportunities/RFPs": "order_property_inspection_condition", "Pedestrian Signal": "damaged_sign_sidewalk_missing", "Pedestrian Ramp Defective": "damaged_sign_sidewalk_missing", "Sign": "damaged_sign_sidewalk_missing", "GUTTER/LEADER": "damaged_sign_sidewalk_missing", "Guard Rail - Highway": "damaged_sign_sidewalk_missing", "Too Few on Duty": "order_property_inspection_condition", "Billing Dispute": "license_complaint_illegal_violation", "Hurricane Preparedness - Arabic": "english_emergency_spanish_chinese", "Food Protection": "odor_food_air_smoke", "Graffiti - Bridge": "damaged_sign_sidewalk_missing", "Special Events": "order_property_inspection_condition", "Commercial Government Exemption": "exemption_commercial_tax_business", "Puddle on Driveway": "water_basin_litter_missed", "2R Bulk-Missed Recy Collection": "water_basin_litter_missed", "Affecting Sewer or Foundation": "water_basin_litter_missed", "Personal STAR Exemption": "exemption_commercial_tax_business", "Credit Card Limitations Not Posted": "license_complaint_illegal_violation", "Heat Bulletin": "order_property_inspection_condition", "Chronic Stoplight Violation": "damaged_sign_sidewalk_missing", "E9 Snow / Icy Sidewalk": "order_property_inspection_condition", "Construction - Change Grade/Watercourse": "order_property_inspection_condition", "Documents/Paperwork Missing": "order_property_inspection_condition", "Plate Missing/Moved-Exposing Hole (WF4)": "damaged_sign_sidewalk_missing", "Street Cleaning - ASP": "order_property_inspection_condition", "Plate Condition - Open": "order_property_inspection_condition", "Timer Defect - Fast/Fail": "damaged_sign_sidewalk_missing", "Cabaret License": "license_complaint_illegal_violation", "Tow Truck Company License": "license_complaint_illegal_violation", "Vehicle Complaint": "license_complaint_illegal_violation", "Taste/Odor, Musty/Stale (QA4)": "odor_food_air_smoke", "Veh Signal Sec Door": "damaged_sign_sidewalk_missing", "Auction House License": "license_complaint_illegal_violation", "Other Billing Issue": "license_complaint_illegal_violation", "Spanish Transaction": "english_emergency_spanish_chinese", "Street Con Game": "damaged_sign_sidewalk_missing", "Other Water Problem (Use Comments) (WZZ)": "water_basin_litter_missed", "High Interest Loan": "order_property_inspection_condition", "Birth Certificate Before 1910 Order Form": "license_complaint_illegal_violation", "Full Term Mobile Food Unit Permit": "license_complaint_illegal_violation", "Ready NY Beat the Heat - English": "english_emergency_spanish_chinese", "GARBAGE/RECYCLING STORAGE": "water_basin_litter_missed", "1RB Missed Recycling - M/G/Pl": "water_basin_litter_missed", "Oil Spill On Street, Large (HQL)": "water_basin_litter_missed", "Pool or Billiard Hall License": "license_complaint_illegal_violation", "Smoking Violation": "license_complaint_illegal_violation", "Musical Instrument": "noise_animal_truck_dead", "1L Missed Recycling Leaves": "water_basin_litter_missed", "JANITOR/SUPER": "damaged_sign_sidewalk_missing", "Congestion/Gridlock": "order_property_inspection_condition", "Tattoo Artist Unlicensed": "license_complaint_illegal_violation", "Illegal Use Of Hose - Private Residence  (CCR)": "license_complaint_illegal_violation", "Supervisory": "order_property_inspection_condition", "Blocking Sidewalk": "damaged_sign_sidewalk_missing", "Ticket Scalping": "license_complaint_illegal_violation", "Housing Quality Standards (HQS) Inspections FAQs - Spanish": "order_property_inspection_condition", "Tortured": "noise_animal_truck_dead", "Gasoline Spill (IAA)": "water_basin_litter_missed", "The ABCs of Housing": "damaged_sign_sidewalk_missing", "Other Housing Options": "damaged_sign_sidewalk_missing", "Non-Delivery Goods/Services": "license_complaint_illegal_violation", "Snake": "noise_animal_truck_dead", "Relocation of Parking Meter": "license_complaint_illegal_violation", "Container - Under 5 Gallons": "water_basin_litter_missed", "Lamppost Leaning": "damaged_sign_sidewalk_missing", "Sign/Awning/Marquee - Illegal/No Permit": "license_complaint_illegal_violation", "Re-inspection": "order_property_inspection_condition", "Senior Citizen Home Assistance Program (SCHAP) Loan": "exemption_commercial_tax_business", "REFRIGERATOR": "odor_food_air_smoke", "Air: Smoke, Vehicular (AA4)": "odor_food_air_smoke", "Media Inquiries": "noise_animal_truck_dead", "Industrial Laundry Delivery License Application": "license_complaint_illegal_violation", "Curb Violation": "license_complaint_illegal_violation", "Transducer-Loop": "noise_animal_truck_dead", "Stoop Line Stand License": "license_complaint_illegal_violation", "The ABCs of Housing - Korean": "damaged_sign_sidewalk_missing", "Speed Limit": "license_complaint_illegal_violation", "Accident - Elevator": "damaged_sign_sidewalk_missing", "Executive": "damaged_sign_sidewalk_missing", "Damaged Bench": "damaged_sign_sidewalk_missing", "Blocked - ATM": "order_property_inspection_condition", "Clothing Damage": "order_property_inspection_condition", "Veh Signal Lens": "damaged_sign_sidewalk_missing", "Water Meter Stolen/Missing - Private Residence (CLR)": "order_property_inspection_condition", "Electronic Sign - Portable": "damaged_sign_sidewalk_missing", "SCRIE Miscellaneous": "order_property_inspection_condition", "Personal Clergy Exemption": "exemption_commercial_tax_business", "Illegal Activity by Phone": "license_complaint_illegal_violation", "Traffic Sign or Signal Blocked": "damaged_sign_sidewalk_missing", "ID Requirement Not Posted": "license_complaint_illegal_violation", "Temporary Food Service Establishment Permit": "license_complaint_illegal_violation", "Reinspection": "order_property_inspection_condition", "Garage or Parking Lot License": "license_complaint_illegal_violation", "Messenger": "noise_animal_truck_dead", "Certificate of No Harassment - Zoning": "license_complaint_illegal_violation", "E8 Canine Violation": "noise_animal_truck_dead", "Wastewater Into Catch Basin (IEB)": "water_basin_litter_missed", "Technician Unlicensed": "license_complaint_illegal_violation", "Posted Notice Or Order Removed/Tampered With": "license_complaint_illegal_violation", "New Bus Stop Shelter Placement": "damaged_sign_sidewalk_missing", "American Flag": "damaged_sign_sidewalk_missing", "Noise: Manufacturing Noise (NK1)": "noise_animal_truck_dead", "Signs of Rodents": "noise_animal_truck_dead", "Dogs or Cats Sold": "noise_animal_truck_dead", "Relocation of Muni Meter": "order_property_inspection_condition", "Line/Marking - After Repaving": "damaged_sign_sidewalk_missing", "Oil Spill Into Basin/Sewer - Large (IABL)": "water_basin_litter_missed", "Snow Removal Requested": "order_property_inspection_condition", "Excavation Undermining Adjacent Building": "damaged_sign_sidewalk_missing", "Building Permit - None": "license_complaint_illegal_violation", "21 Collection Truck Noise": "noise_animal_truck_dead", "Flood Light Lamp Dim": "damaged_sign_sidewalk_missing", "Food Temperature": "odor_food_air_smoke", "Tree Alive - in Poor Condition": "damaged_sign_sidewalk_missing", "Newsstand License": "license_complaint_illegal_violation", "E2A Storage Of Receptacles": "water_basin_litter_missed", "Catch Basin Clogged/Flooding (Use Comments) (SC)": "water_basin_litter_missed", "E1A Litter Basket / Improper Use": "water_basin_litter_missed", "Closed without Notice": "order_property_inspection_condition", "Ready NY - Korean - Full Size": "english_emergency_spanish_chinese", "Interest Dispute": "license_complaint_illegal_violation", "In Conduit": "order_property_inspection_condition", "HOUSING QUALITY STANDARDS": "order_property_inspection_condition", "Failure To Maintain": "order_property_inspection_condition", "Failed Street Repair": "damaged_sign_sidewalk_missing", "Paid in Advance": "license_complaint_illegal_violation", "Ready NY - Small and Mid-Sized Companies": "english_emergency_spanish_chinese", "Puddle in Ground": "water_basin_litter_missed", "Plumbing": "water_basin_litter_missed", "E2 Receptacle Violation": "water_basin_litter_missed", "Sign - In Danger Of Falling": "damaged_sign_sidewalk_missing", "Unrequested Services Provided": "license_complaint_illegal_violation", "Locker Break-in/Incident": "damaged_sign_sidewalk_missing", "Public Complaint - Comm Location": "license_complaint_illegal_violation", "Garbage or Litter": "water_basin_litter_missed", "Glassware Broken": "damaged_sign_sidewalk_missing", "On Messenger": "damaged_sign_sidewalk_missing", "6 Overflowing Litter Baskets": "water_basin_litter_missed", "Shelter for Homeless Animals License": "noise_animal_truck_dead", "E13 Throw-Out": "water_basin_litter_missed", "MICROWAVE": "odor_food_air_smoke", "Food Preparation Location": "odor_food_air_smoke", "Equipment Not Safe": "order_property_inspection_condition", "Ewaste appointment": "order_property_inspection_condition", "Facility General": "order_property_inspection_condition", "Beach/Pool/Sauna Unpermitted": "water_basin_litter_missed", "Smoke/Odor": "odor_food_air_smoke", "BBS Failure": "order_property_inspection_condition", "Unsafe Worksite": "order_property_inspection_condition", "Non-Compliance w/Lightweight Materials": "order_property_inspection_condition", "Special Agency Projects/Initiatives": "order_property_inspection_condition", "Insects / Pests": "noise_animal_truck_dead", "Home Improvement Salesperson License": "license_complaint_illegal_violation", "Illegal Activity": "order_property_inspection_condition", "Locksmith License": "license_complaint_illegal_violation", "Employment Agency License": "license_complaint_illegal_violation", "No Shelter": "damaged_sign_sidewalk_missing", "Noise: Boat(Engine,Music,Etc) (NR10)": "noise_animal_truck_dead", "Applied to Wrong Ticket": "license_complaint_illegal_violation", "Commercial DAMP Exemption": "exemption_commercial_tax_business", "Ped Flasher": "damaged_sign_sidewalk_missing", "Dumpster - Construction Waste": "water_basin_litter_missed", "Unauthorized Film Shoot": "license_complaint_illegal_violation", "Ethernet Cable": "damaged_sign_sidewalk_missing", "Support Bracket": "damaged_sign_sidewalk_missing", "TAL 2 Wheelchair": "order_property_inspection_condition", "Request Large Bulky Item Collection": "order_property_inspection_condition", "Dirty Water (WE)": "water_basin_litter_missed", "No Sampling Required, Requested Information (QG2)": "license_complaint_illegal_violation", "Layaway Terms Not Provided": "exemption_commercial_tax_business", "Ferret": "noise_animal_truck_dead", "POWER OUTAGE": "damaged_sign_sidewalk_missing", "Unauthorized Posting of Signs": "license_complaint_illegal_violation", "Sewer or Drain": "water_basin_litter_missed", "PAVEMENT": "order_property_inspection_condition", "3 or More": "order_property_inspection_condition", "Elevator - Defective/Not Working": "damaged_sign_sidewalk_missing", "421A Exemption": "exemption_commercial_tax_business", "Ready NY - Kids - Middle and High School Students": "english_emergency_spanish_chinese", "Water Meter Broken/Leaking - Other (CMO)": "water_basin_litter_missed", "1R Missed Recycling-All Materials": "water_basin_litter_missed", "Animal Boarding License": "license_complaint_illegal_violation", "Neglected": "order_property_inspection_condition", "Food Contains Foreign Object": "odor_food_air_smoke", "Glassware Missing": "damaged_sign_sidewalk_missing", "Unsafe Chemical, Abandoned (HC2)": "water_basin_litter_missed", "Community Outreach": "damaged_sign_sidewalk_missing", "No Access": "order_property_inspection_condition", "Damaged or Leaking Roof": "damaged_sign_sidewalk_missing", "Bare Hands in Contact w/ Food": "odor_food_air_smoke", "Fountain - Under 5 Gallons": "water_basin_litter_missed", "Property Misclassification": "order_property_inspection_condition", "Curb Defect-Metal Protruding": "damaged_sign_sidewalk_missing", "Snow or Ice": "order_property_inspection_condition", "Tax Exemption": "exemption_commercial_tax_business", "Blocked - Construction": "damaged_sign_sidewalk_missing", "Labor Violation": "license_complaint_illegal_violation", "SCRIE Application Denial": "order_property_inspection_condition", "Driver Compliment": "order_property_inspection_condition", "PORCH/BALCONY": "damaged_sign_sidewalk_missing", "Crack Sealing": "order_property_inspection_condition", "Ready NY - Chinese Traditional - Full Size": "english_emergency_spanish_chinese", "Damaged Other": "damaged_sign_sidewalk_missing", "Mandated Reporters": "order_property_inspection_condition", "Color": "damaged_sign_sidewalk_missing", "Branch Cracked and Will Fall": "damaged_sign_sidewalk_missing", "Street Cave-In *Dep Internal Use Only* (SG1)": "order_property_inspection_condition", "SST Tracking Complaint": "license_complaint_illegal_violation", "Annual Report": "order_property_inspection_condition", "Underground": "damaged_sign_sidewalk_missing", "Other Water Problem (Use Comments) (QZZ)": "water_basin_litter_missed", "Facilities Management": "order_property_inspection_condition", "Disclosure Not Provided": "order_property_inspection_condition", "Other": "order_property_inspection_condition", "Elevator In (Fdny) Readiness - None": "damaged_sign_sidewalk_missing", "Ready NY - Polish - Full Size": "english_emergency_spanish_chinese", "Facility Complaint": "order_property_inspection_condition", "Cigarette Sale to Minor": "license_complaint_illegal_violation", "PESTS": "noise_animal_truck_dead", "Mouse Sighting": "noise_animal_truck_dead", "Swimming Pool Cover": "water_basin_litter_missed", "Food Worker Illness": "odor_food_air_smoke", "Improper Sale of Items": "license_complaint_illegal_violation", "Loud Television": "noise_animal_truck_dead", "Broken/Defective": "damaged_sign_sidewalk_missing", "Child or Minor Tanning": "damaged_sign_sidewalk_missing", "Fiscal and Business Management": "exemption_commercial_tax_business", "Copy of Account Information": "license_complaint_illegal_violation", "Smoking": "odor_food_air_smoke", "Air: Smoke, Other (Use Comments) (AA5)": "odor_food_air_smoke", "Ventilation": "odor_food_air_smoke", "Fixture/Luminaire Missing": "damaged_sign_sidewalk_missing", "Veh Signal Visor": "damaged_sign_sidewalk_missing", "Shisha": "order_property_inspection_condition", "Exposure Unnecessary": "order_property_inspection_condition", "Rodents/Insects/Garbage": "noise_animal_truck_dead", "Home Ownership Kit": "order_property_inspection_condition", "Advertising Sign/Billboard/Posters/Flexible Fabric - Illegal": "license_complaint_illegal_violation", "Electronic Sign - Overhead": "damaged_sign_sidewalk_missing", "APS": "damaged_sign_sidewalk_missing", "15I Street Condition Ice-Non Storm": "order_property_inspection_condition", "Rooster": "noise_animal_truck_dead", "Sewer Odor (SA2)": "odor_food_air_smoke", "Air: Odor/Fumes, Restaurant (AD2)": "odor_food_air_smoke", "Junction Box": "damaged_sign_sidewalk_missing", "Excise Taxes-Audit": "exemption_commercial_tax_business", "Exit/Route": "damaged_sign_sidewalk_missing", "Banging/Pounding": "noise_animal_truck_dead", "Use Indoor": "damaged_sign_sidewalk_missing", "Amusement Ride": "order_property_inspection_condition", "Lamppost Missing": "damaged_sign_sidewalk_missing", "Marriage Certificate Order Form": "license_complaint_illegal_violation", "Litter": "water_basin_litter_missed", "Misleading Appraisal": "order_property_inspection_condition", "Dogs or Cats Not Sold": "noise_animal_truck_dead", "Loud Music/Party": "noise_animal_truck_dead", "Construction": "damaged_sign_sidewalk_missing", "Warning Signal": "damaged_sign_sidewalk_missing", "Sample Suspected Gas Leak Notice": "water_basin_litter_missed", "General Business Tax - Return filing": "exemption_commercial_tax_business", "Playing in Unsuitable Place": "order_property_inspection_condition", "General Business Tax - Other": "exemption_commercial_tax_business", "Speed Board Sign": "damaged_sign_sidewalk_missing", "Suspected Street Cut": "damaged_sign_sidewalk_missing", "Scrap Metal Processor License": "license_complaint_illegal_violation", "Fixture/Luminaire Out Of Position": "damaged_sign_sidewalk_missing", "Privately Owned Public Space/Non-Compliance": "exemption_commercial_tax_business", "Unsanitary Condition": "odor_food_air_smoke", "Unclean Condition": "order_property_inspection_condition", "Public Event Seating": "damaged_sign_sidewalk_missing", "General Business Tax - Refund": "exemption_commercial_tax_business", "C1 Request Xmas Trees Collection": "english_emergency_spanish_chinese", "No or Defective Headphones": "noise_animal_truck_dead", "Initial": "english_emergency_spanish_chinese", "Milk/Dairy Products": "odor_food_air_smoke", "Initial Application": "order_property_inspection_condition", "3 Sweeping/Missed-Inadequate": "order_property_inspection_condition", "No Parking, Standing, Stopping": "damaged_sign_sidewalk_missing", "Over Capacity": "order_property_inspection_condition", "Nursing Home": "order_property_inspection_condition", "New Lead Law Rights and Requirements": "license_complaint_illegal_violation", "Fire Alarm Lamp Out": "damaged_sign_sidewalk_missing", "General Street Vendor License": "license_complaint_illegal_violation", "In Public": "order_property_inspection_condition", "Lights From Parking Lot Shining On Building": "damaged_sign_sidewalk_missing", "Excavation Tracking Complaint": "order_property_inspection_condition", "E3A Dirty Area/Alleyway": "order_property_inspection_condition", "Graffiti - Tunnel": "damaged_sign_sidewalk_missing", "Removing Wildlife": "noise_animal_truck_dead", "New Con Ed Service Request": "license_complaint_illegal_violation", "Lamppost Base Door/Cover Missing": "damaged_sign_sidewalk_missing", "Hitting Power/Phone Lines": "damaged_sign_sidewalk_missing", "Excise Taxes-Other": "exemption_commercial_tax_business", "Wear & Tear": "damaged_sign_sidewalk_missing", "SKYLIGHT": "damaged_sign_sidewalk_missing", "General Business Tax- Audit": "exemption_commercial_tax_business", "Noise:  lawn care equipment (NCL)": "noise_animal_truck_dead", "VENTILATION SYSTEM": "odor_food_air_smoke", "Ver Message Sign": "damaged_sign_sidewalk_missing", "Unlicensed Vendors": "license_complaint_illegal_violation", "Missing/Stump": "damaged_sign_sidewalk_missing", "Noise: Construction Before/After Hours (NM1)": "noise_animal_truck_dead", "Lost Coin": "order_property_inspection_condition", "Other Animal": "noise_animal_truck_dead", "Equipment Maintenance": "order_property_inspection_condition", "Rooftank Leak Or Overflow (CKO)": "water_basin_litter_missed", "Housing Quality Standards (HQS) Inspections FAQs - English": "order_property_inspection_condition", "Interior Demo Tracking Complaint": "license_complaint_illegal_violation", "Cellar Door New": "damaged_sign_sidewalk_missing", "Structural Stability Impacted - New Building Under Construction": "damaged_sign_sidewalk_missing", "Rodents/Mice": "noise_animal_truck_dead", "Structure - Indoors": "damaged_sign_sidewalk_missing", "Dust Cover": "order_property_inspection_condition", "Request To Open A Hydrant (WC4)": "water_basin_litter_missed", "Cons - Contrary/Beyond Approved Plans/Permits": "license_complaint_illegal_violation", "No Certificate Of Occupancy/Illegal/Contrary To CO": "license_complaint_illegal_violation", "Condulet Cover": "order_property_inspection_condition", "Dissatisfaction with Provider": "license_complaint_illegal_violation", "Car Not Available": "order_property_inspection_condition", "Fire Globe Missing": "damaged_sign_sidewalk_missing", "Bracket Arm Bent": "damaged_sign_sidewalk_missing", "RPIE - Filing and Technical Issues": "license_complaint_illegal_violation", "SCRIE Application Appeal": "license_complaint_illegal_violation", "Air: Dust, Construction/Demolition (AE4)": "order_property_inspection_condition", "Safety Equipment/Signs": "order_property_inspection_condition", "Amount Owed Dispute": "license_complaint_illegal_violation", "Hurricane Preparedness - Russian": "english_emergency_spanish_chinese", "Card - DOF Confirmation Number Issued": "license_complaint_illegal_violation", "Foreign Attachment On Lamppost": "exemption_commercial_tax_business", "Hangers": "damaged_sign_sidewalk_missing", "Veh Sgnl Mult Lamps": "damaged_sign_sidewalk_missing", "Other Agency Charge": "license_complaint_illegal_violation", "Snow/Ice": "order_property_inspection_condition", "In Prohibited Area": "order_property_inspection_condition", "Pathogens License": "license_complaint_illegal_violation", "E3B Sidewalk Obstruction": "damaged_sign_sidewalk_missing", "Elevator Not Inspected/Illegal/No Permit": "license_complaint_illegal_violation", "Door Lock": "damaged_sign_sidewalk_missing", "Plants- Noise Related Problems (PN1)": "noise_animal_truck_dead", "FOIL Request - Request for Records": "exemption_commercial_tax_business", "Illegal Use Of A Hydrant (CIN)": "water_basin_litter_missed", "Vent/Exhaust - Illegal/Improper": "odor_food_air_smoke", "Mental Health": "order_property_inspection_condition", "Site Conditions Endangering Workers": "order_property_inspection_condition", "6R Overflowing Recycling Baskets": "water_basin_litter_missed", "Personal Other Exemption": "exemption_commercial_tax_business", "Placement": "damaged_sign_sidewalk_missing", "Inspection Requests/Complaints": "order_property_inspection_condition", "Air: Odor, Nail Salon (AD8)": "odor_food_air_smoke", "Best - High-Rise Tracking Complaint": "order_property_inspection_condition", "Harassment": "order_property_inspection_condition", "Amusement Ride Accident/Incident": "order_property_inspection_condition", "Sewage": "water_basin_litter_missed", "Post": "damaged_sign_sidewalk_missing", "12 Dead Animals": "noise_animal_truck_dead", "Initial - Construction": "damaged_sign_sidewalk_missing", "Settlement Reduction Not Shown": "order_property_inspection_condition", "Hitting Building": "damaged_sign_sidewalk_missing", "Sidewalk Collapsed": "damaged_sign_sidewalk_missing", "EXPY Sign Fixt Cover": "damaged_sign_sidewalk_missing", "Hydrant Running Full (WA4)": "water_basin_litter_missed", "Other Health Matters": "odor_food_air_smoke", "EZ PASS READER": "order_property_inspection_condition", "Damaged/Defective Parts": "damaged_sign_sidewalk_missing", "CEILING": "damaged_sign_sidewalk_missing", "Commercial Overnight Parking": "damaged_sign_sidewalk_missing", "Damaged/Defective Goods": "order_property_inspection_condition", "Sodium Warning": "order_property_inspection_condition", "After Hours - Licensed Est": "license_complaint_illegal_violation", "EXPY Sign Reflector": "damaged_sign_sidewalk_missing", "Controller Cabinet": "damaged_sign_sidewalk_missing", "SEWER": "water_basin_litter_missed", "Image of Ticket": "damaged_sign_sidewalk_missing", "Street Light Lamp Dim": "damaged_sign_sidewalk_missing", "Leaky Roof": "order_property_inspection_condition", "Portable Amusement Ride License": "license_complaint_illegal_violation", "Status of Appeal": "license_complaint_illegal_violation", "Foundation": "damaged_sign_sidewalk_missing", "Not Certified": "license_complaint_illegal_violation", "Equipment Malfunction": "order_property_inspection_condition", "Controller Flasher": "damaged_sign_sidewalk_missing", "New Building": "damaged_sign_sidewalk_missing", "Process Server Organization License": "license_complaint_illegal_violation", "Summer Heat - Chinese": "english_emergency_spanish_chinese", "Information Technology": "order_property_inspection_condition", "Other/Unknown": "order_property_inspection_condition", "Home Improvement Contractor License": "license_complaint_illegal_violation", "Lack of Safety Equipment": "order_property_inspection_condition", "Allergy Information": "odor_food_air_smoke", "Time Clock Maladjusted": "damaged_sign_sidewalk_missing", "Real Property Tax Assessment/Correction": "exemption_commercial_tax_business", "Box Cover": "damaged_sign_sidewalk_missing", "Damaged Door": "damaged_sign_sidewalk_missing", "Full Term Mobile Food Vendor License": "license_complaint_illegal_violation", "Tree Leaning/Uprooted": "damaged_sign_sidewalk_missing", "Defective/Missing Curb Piece (SC4)": "damaged_sign_sidewalk_missing", "Defective Water Sampling Station (QSS)": "water_basin_litter_missed", "Lien Sale": "license_complaint_illegal_violation", "Beach/Pool Closure": "water_basin_litter_missed", "Illegal Conversion Of Commercial Bldg/Space To Other Uses": "license_complaint_illegal_violation", "Illegal/Unfair Booting": "license_complaint_illegal_violation", "Fence - None/Inadequate": "damaged_sign_sidewalk_missing", "Car Dealer - Used": "license_complaint_illegal_violation", "Touchscreen/Button Not Working": "damaged_sign_sidewalk_missing", "Blocked Bike Lane": "damaged_sign_sidewalk_missing", "Minor Received Tattoo": "license_complaint_illegal_violation", "Flood Light Lamp Missing": "damaged_sign_sidewalk_missing", "Death Certificate Before 1949 Order Form": "license_complaint_illegal_violation", "Personal SCHE Exemption": "exemption_commercial_tax_business", "Card - Charged Twice": "license_complaint_illegal_violation", "Vehicle Report": "order_property_inspection_condition", "FIRE ESCAPE": "damaged_sign_sidewalk_missing", "Sidewalk Pull Box Co": "damaged_sign_sidewalk_missing", "Hummock": "noise_animal_truck_dead", "RTMS": "order_property_inspection_condition", "Workplace - 10 or Less Staff": "order_property_inspection_condition", "Street Light Cycling": "damaged_sign_sidewalk_missing", "Electrical Wiring Defective/Exposed": "damaged_sign_sidewalk_missing", "Seasonal Food Cart Vendor Permit": "license_complaint_illegal_violation", "Prohibited Item Sale to Minor": "license_complaint_illegal_violation", "Noise, Barking Dog (NR5)": "noise_animal_truck_dead", "E6 Commercial Waste Disposal": "water_basin_litter_missed", "Highway Fence": "damaged_sign_sidewalk_missing", "Exposure from Nearby Facility": "order_property_inspection_condition", "About NYC Opportunity": "english_emergency_spanish_chinese", "Manhole Cover Broken/Making Noise (SB)": "noise_animal_truck_dead", "Detour": "order_property_inspection_condition", "School Crossing": "damaged_sign_sidewalk_missing", "General Maintenance": "order_property_inspection_condition", "Compressed Air License": "license_complaint_illegal_violation", "Equipment Complaint": "license_complaint_illegal_violation", "No Idling": "noise_animal_truck_dead", "DOOR": "damaged_sign_sidewalk_missing", "Removing Flowers/Plants": "water_basin_litter_missed", "Lane Control Signal": "damaged_sign_sidewalk_missing", "Building - Vacant, Open And Unguarded": "damaged_sign_sidewalk_missing", "installation of hydrant side post (WHFP)": "water_basin_litter_missed", "User Unlicensed": "license_complaint_illegal_violation", "Poison Ivy": "noise_animal_truck_dead", "Newspaper Box Complaint": "license_complaint_illegal_violation", "Hydrant Leaking (WC1)": "water_basin_litter_missed", "E10 Street Obstruction": "damaged_sign_sidewalk_missing", "Contamination Risk": "odor_food_air_smoke", "False Advertising": "order_property_inspection_condition", "Auctioneer License": "license_complaint_illegal_violation", "One Way": "order_property_inspection_condition", "Honorary": "order_property_inspection_condition", "Book/Stationery": "damaged_sign_sidewalk_missing", "Obstructing Public Use": "license_complaint_illegal_violation", "BASIN/SINK": "water_basin_litter_missed", "SLOW LEAK": "water_basin_litter_missed", "Absent": "order_property_inspection_condition", "Restrooms": "order_property_inspection_condition", "Pothole - Tunnel": "damaged_sign_sidewalk_missing", "BUILDING COLLAPSE/FIRE, (ASBESTOS RELATED) *FOR DEP INTERNAL USE ONLY* (HH2)": "odor_food_air_smoke", "Painted Line/Marking": "damaged_sign_sidewalk_missing", "Conduit": "order_property_inspection_condition", "Overexposure During Treatment": "order_property_inspection_condition", "12P Dead Deer": "noise_animal_truck_dead", "Boiler - Fumes/Smoke/Carbon Monoxide": "odor_food_air_smoke", "The ABCs of Housing - Russian": "english_emergency_spanish_chinese", "DAMAGE STRUCTURE/RAILING (SRGDM)": "damaged_sign_sidewalk_missing", "Required Signage Not Posted": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - Spanish": "english_emergency_spanish_chinese", "Tie Rods": "damaged_sign_sidewalk_missing", "3A Sweeping/Missed": "order_property_inspection_condition", "Multiple Street Lights Out": "damaged_sign_sidewalk_missing", "Sign Missing or Defective": "damaged_sign_sidewalk_missing", "Wood Pole Wires Exposed": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - Haitian Creole": "english_emergency_spanish_chinese", "Safety Netting/Guard Rails - Damaged/Inadequate/None (6 Stories/75 Feet Or Less)": "damaged_sign_sidewalk_missing", "Overnight Commercial Storage": "order_property_inspection_condition", "Out of Order": "order_property_inspection_condition", "Cars Parked on Sidewalk/Street": "damaged_sign_sidewalk_missing", "Capital Construction": "damaged_sign_sidewalk_missing", "Unsafe Chemical, Storage (HC1)": "water_basin_litter_missed", "Inhalation Therapy Supervising Technician License": "license_complaint_illegal_violation", "The ABCs of Housing - Haitian Creole": "english_emergency_spanish_chinese", "Container - Over 5 Gallons": "water_basin_litter_missed", "Grass/Weeds": "noise_animal_truck_dead", "Jewelry": "order_property_inspection_condition", "Sightseeing Guide License": "license_complaint_illegal_violation", "Minor Access": "order_property_inspection_condition", "Phone Blocking Sidewalk": "damaged_sign_sidewalk_missing", "BOILER": "odor_food_air_smoke", "Asbestos": "odor_food_air_smoke", "Bracket Arm Missing": "damaged_sign_sidewalk_missing", "Hydrant Knocked Over/Missing (WC)": "water_basin_litter_missed", "Toilet Facility": "water_basin_litter_missed", "Temporary": "order_property_inspection_condition", "Unauthorized Tree Pruning": "license_complaint_illegal_violation", "Toxic Chemical/Material": "odor_food_air_smoke", "Ticket Seller Business License Application": "license_complaint_illegal_violation", "Registration Clearance Request": "license_complaint_illegal_violation", "Appeals Division": "order_property_inspection_condition", "Wood Pole Leaning": "damaged_sign_sidewalk_missing", "Gas Hook-Up/Piping - Illegal Or Defective": "license_complaint_illegal_violation", "Non-med Compressed Gas - New": "odor_food_air_smoke", "Marine Lamp": "damaged_sign_sidewalk_missing", "Control Panel Damaged": "damaged_sign_sidewalk_missing", "Tires": "order_property_inspection_condition", "Dishwashing/Utensils": "odor_food_air_smoke", "Property": "order_property_inspection_condition", "10A Adopt-A-Basket": "order_property_inspection_condition", "Semi-Annual Homeless Shelter Inspection: Electrical": "order_property_inspection_condition", "Other Sewer Problem (Use Comments) (SZZ)": "water_basin_litter_missed", "Lost/Missing Person": "order_property_inspection_condition", "E3 Dirty Sidewalk": "order_property_inspection_condition", "WINDOW FRAME": "damaged_sign_sidewalk_missing", "Telco Connection Blk": "order_property_inspection_condition", "Marine Globe": "damaged_sign_sidewalk_missing", "MAILBOX": "damaged_sign_sidewalk_missing", "Scale Inaccurate/Broken": "damaged_sign_sidewalk_missing", "Sidewalk Grating - Missing": "damaged_sign_sidewalk_missing", "Pedestrian Sign": "damaged_sign_sidewalk_missing", "The ABCs of Housing - Arabic": "english_emergency_spanish_chinese", "Failure To Retain Water/Improper Drainage- (LL103/89)": "water_basin_litter_missed", "Best - Low-Rise Tracking Complaint": "order_property_inspection_condition", "Driver Complaint - Passenger": "license_complaint_illegal_violation", "Enforcement Work Order (DOB)": "license_complaint_illegal_violation", "WINDOW/FRAME": "damaged_sign_sidewalk_missing", "Air: Other Air Problem (Use Comments) (AZZ)": "odor_food_air_smoke", "Snow on Overpass": "order_property_inspection_condition", "Plumbing-Defective/Leaking/Not Maintained": "water_basin_litter_missed", "Car Service Company Complaint": "license_complaint_illegal_violation", "Chemical Odor (HD1)": "odor_food_air_smoke", "NYPD": "english_emergency_spanish_chinese", "10 Litter Basket / Request": "water_basin_litter_missed", "Noise: Other Noise Sources (Use Comments) (NZZ)": "noise_animal_truck_dead", "Fallen Debris from Tunnel": "order_property_inspection_condition", "Cloudy Or Milky, Other (Use Comments) (QBZ)": "noise_animal_truck_dead", "Entire Tree Has Fallen Down": "damaged_sign_sidewalk_missing", "Permit/License/Certificate": "license_complaint_illegal_violation", "Fallen Debris from Bridge": "order_property_inspection_condition", "Human Capital": "order_property_inspection_condition", "Air: Open Fire, Construction/Demolition (AC4)": "damaged_sign_sidewalk_missing", "Because of Violation": "license_complaint_illegal_violation", "Bag": "order_property_inspection_condition", "Application Portability": "order_property_inspection_condition", "Ready NY - Businesses - Spanish": "english_emergency_spanish_chinese", "Other - Explain Below": "order_property_inspection_condition", "Veh Signal Lamp": "damaged_sign_sidewalk_missing", "Pigeon Waste": "water_basin_litter_missed", "Commercial Exemptions": "exemption_commercial_tax_business", "DRIE Exemption": "exemption_commercial_tax_business", "Interruption of Essential Services Notice": "license_complaint_illegal_violation", "Sway Bar": "damaged_sign_sidewalk_missing", "High Pressure Sales": "order_property_inspection_condition", "14 Derelict Vehicles": "order_property_inspection_condition", "Licensee Complaint": "license_complaint_illegal_violation", "Injured Wildlife": "noise_animal_truck_dead", "Graffiti/Dirty Condition": "order_property_inspection_condition", "Flood Light Lamp Out": "damaged_sign_sidewalk_missing", "Marshal - Not Reflected": "order_property_inspection_condition", "Unlicensed Day Care": "license_complaint_illegal_violation", "Graffiti": "damaged_sign_sidewalk_missing", "Status of Payment Adjustment": "license_complaint_illegal_violation", "Damaged Vehicle": "damaged_sign_sidewalk_missing", "Blank Out Matrix Sgn": "order_property_inspection_condition", "Lamppost Base Door/Cover Open": "damaged_sign_sidewalk_missing", "E11 Litter Surveillance": "water_basin_litter_missed", "Contract Dispute": "license_complaint_illegal_violation", "Certificate of No Harassment (CONH) Application": "license_complaint_illegal_violation", "Loan Offer": "order_property_inspection_condition", "High Water Pressure (WHP)": "water_basin_litter_missed", "Pedicab Driver": "order_property_inspection_condition", "Installation/Work Quality": "damaged_sign_sidewalk_missing", "Contact Sign Not Posted": "damaged_sign_sidewalk_missing", "Water Meter Stolen/Missing - Other (CLO)": "water_basin_litter_missed", "Plumbing Problem": "water_basin_litter_missed", "BELL/BUZZER/INTERCOM": "damaged_sign_sidewalk_missing", "Accident - Cranes/Derricks/Suspension Scaffold": "order_property_inspection_condition", "Graffiti/Litter on Phone": "order_property_inspection_condition", "Property Value": "order_property_inspection_condition", "Ready NY My Emergency Plan - Russian": "english_emergency_spanish_chinese", "Status of Hearing": "noise_animal_truck_dead", "Letter Grading": "order_property_inspection_condition", "Other (Explain Below)": "damaged_sign_sidewalk_missing", "Ready NY - Flooding": "english_emergency_spanish_chinese", "Certificate of No Harassment (CONH) Exemption": "exemption_commercial_tax_business", "License Violation": "license_complaint_illegal_violation", "14B Derelict Bicycle": "order_property_inspection_condition", "Weather Head": "damaged_sign_sidewalk_missing", "Use of Newly Seeded Lawn": "order_property_inspection_condition", "E14 ASP/Restricted Parking": "license_complaint_illegal_violation", "Clear Water With Other Particles (Use Comments) (QEZ)": "water_basin_litter_missed", "Line/Marking - Faded": "damaged_sign_sidewalk_missing", "Water": "water_basin_litter_missed", "Pet Store - New License": "license_complaint_illegal_violation", "Dead Branches in Tree": "damaged_sign_sidewalk_missing", "Illegal Use Of Hose - Other (CCO)": "license_complaint_illegal_violation", "Milk Not Pasteurized": "odor_food_air_smoke", "Hours of Operation": "order_property_inspection_condition", "DOOR/FRAME": "damaged_sign_sidewalk_missing", "Complaince Inspection": "order_property_inspection_condition", "LOW WATER PRESSURE - WLWP": "water_basin_litter_missed", "Garbage": "order_property_inspection_condition", "Coin or Card Did Not Register": "license_complaint_illegal_violation", "Car/Truck Music": "noise_animal_truck_dead", "NO LIGHTING": "damaged_sign_sidewalk_missing", "LED Lense": "damaged_sign_sidewalk_missing", "House/Property Damaged": "damaged_sign_sidewalk_missing", "Animal Waste": "water_basin_litter_missed", "Lost Property": "order_property_inspection_condition", "Canopy Complaint": "damaged_sign_sidewalk_missing", "Conflict Monitor": "damaged_sign_sidewalk_missing", "Lamppost Knocked Down": "damaged_sign_sidewalk_missing", "Wrong Amount Paid or Withdrawn": "license_complaint_illegal_violation", "DOOR FRAME": "damaged_sign_sidewalk_missing", "Material Stored Improperly": "water_basin_litter_missed", "Iguana": "noise_animal_truck_dead", "Ready NY - Arabic - Full Size": "english_emergency_spanish_chinese", "Heating Problem": "odor_food_air_smoke", "Food Service Establishment License": "license_complaint_illegal_violation", "Illness/Injury": "damaged_sign_sidewalk_missing", "Safety Netting/Guard Rails - Damaged/Inadequate/None (Over 6 Stories/75 Feet)": "damaged_sign_sidewalk_missing", "Derelict Vehicles": "order_property_inspection_condition", "BATHTUB/SHOWER": "water_basin_litter_missed", "Noise: Alarms (NR3)": "noise_animal_truck_dead", "Bus Stop": "order_property_inspection_condition", "Con Edison Referral": "damaged_sign_sidewalk_missing", "Street Light Lamp Missing": "damaged_sign_sidewalk_missing", "Truck Route Violation": "license_complaint_illegal_violation", "Blocking Street": "damaged_sign_sidewalk_missing", "Information on Contracts and Contractors": "license_complaint_illegal_violation", "Status of PV Refund": "exemption_commercial_tax_business", "Sign Defect - Garage": "damaged_sign_sidewalk_missing", "Locksmith Apprentice License": "license_complaint_illegal_violation", "Vehicle Signal": "damaged_sign_sidewalk_missing", "Dead End Signal": "damaged_sign_sidewalk_missing", "High Pressure to Take on Loan/Debt": "water_basin_litter_missed", "Condo Billing Issue": "license_complaint_illegal_violation", "Depression Maintenance": "order_property_inspection_condition", "Existing Building": "damaged_sign_sidewalk_missing", "Flower Planters": "noise_animal_truck_dead", "Secondhand Dealer General License": "license_complaint_illegal_violation", "SMOKE DETECTOR": "odor_food_air_smoke", "Receipt Incomplete/Not Given": "license_complaint_illegal_violation", "Winter Health and Safety Tips Guide": "order_property_inspection_condition", "Concrete In Catch Basin (IEA)": "water_basin_litter_missed", "Misapplied Payment": "license_complaint_illegal_violation", "COOKING GAS": "odor_food_air_smoke", "Foreign Attachment On Wood Pole": "damaged_sign_sidewalk_missing", "Sidewalk Cafe License": "license_complaint_illegal_violation", "null": "order_property_inspection_condition", "STEAM PIPE/RISER": "water_basin_litter_missed", "New Automatic Public Toilet Request": "water_basin_litter_missed", "FLOOR": "damaged_sign_sidewalk_missing", "Non-Compliance w/TTPN 1/00 - Vertical Enlargements": "license_complaint_illegal_violation", "Clear Water With Organisms (Insects, Worms) (QE2)": "water_basin_litter_missed", "Flood Light Lamp Cycling": "damaged_sign_sidewalk_missing", "Swimming Pool - Unmaintained": "water_basin_litter_missed", "Ped Lens": "damaged_sign_sidewalk_missing", "Commercial Green Roof or Solar Panel Exemption": "exemption_commercial_tax_business", "Other School Condition": "order_property_inspection_condition", "News Gathering": "noise_animal_truck_dead", "Ped Visor": "damaged_sign_sidewalk_missing", "Certificate of No Harassment or Exemption - SRO": "license_complaint_illegal_violation", "Permission to Publish Contract": "license_complaint_illegal_violation", "Energy": "damaged_sign_sidewalk_missing", "Safety Inspection-Retaining Walls (May 2005)": "order_property_inspection_condition", "Driver Report": "license_complaint_illegal_violation", "Air: Odor, Sweet From Unknown Source (AZ1)": "odor_food_air_smoke", "3B Sweeping/Inadequate": "order_property_inspection_condition", "Dog Off Leash": "noise_animal_truck_dead", "Debt Collection Agency License": "license_complaint_illegal_violation", "Complaint": "order_property_inspection_condition", "Noise: Jack Hammering (NC2)": "noise_animal_truck_dead", "Assisted Living": "order_property_inspection_condition", "ULURP Project Status Questions": "order_property_inspection_condition", "Catering Establishment License": "license_complaint_illegal_violation", "Voluntary": "order_property_inspection_condition", "Taste/Odor, Sewer (QA5)": "odor_food_air_smoke", "Cable Television": "damaged_sign_sidewalk_missing", "Odor": "odor_food_air_smoke", "Commercial Rent Tax-Other": "exemption_commercial_tax_business", "WIRING": "damaged_sign_sidewalk_missing", "Excessive Water In Basement (WEFB)": "water_basin_litter_missed", "Smoking Ban - Smoking on Construction Site": "license_complaint_illegal_violation", "Commercial Not For Profit Exemption": "exemption_commercial_tax_business", "Wall/Retaining Wall - Bulging/Cracked": "damaged_sign_sidewalk_missing", "Taste": "odor_food_air_smoke", "Clothing/Glasses": "damaged_sign_sidewalk_missing", "Use Outside": "damaged_sign_sidewalk_missing", "Double Parked Blocking Traffic": "damaged_sign_sidewalk_missing", "Veh Signal Head": "damaged_sign_sidewalk_missing", "Pigeon Odor": "odor_food_air_smoke", "Debris - Falling Or In Danger Of Falling": "order_property_inspection_condition", "Branch or Limb Has Fallen Down": "damaged_sign_sidewalk_missing", "Decision and Order": "order_property_inspection_condition", "Unlicensed/Illegal/Improper Work In Progress": "license_complaint_illegal_violation", "Toy Gun Sale": "noise_animal_truck_dead", "Flood Light Lamp Dayburning": "damaged_sign_sidewalk_missing", "Injury or Illness from Tanning": "damaged_sign_sidewalk_missing", "Commercial ICP or ICAP Exemption": "exemption_commercial_tax_business", "Ready NY - Reference Card": "english_emergency_spanish_chinese", "Large Number of Mosquitoes": "noise_animal_truck_dead", "Metal Protruding - Sign Stump": "damaged_sign_sidewalk_missing", "Sidewalk Shed/Pipe Scafford - Inadequate Defective/None": "order_property_inspection_condition", "Amusement Arcade License": "license_complaint_illegal_violation", "Commercial CEP or CRP Exemption": "exemption_commercial_tax_business", "Manhole Cover Missing (Emergency) (SA3)": "order_property_inspection_condition", "Hydrotest": "water_basin_litter_missed", "Bodega/Deli/Supermarket": "odor_food_air_smoke", "Retail Laundry License Application": "license_complaint_illegal_violation", "Sewage Leak": "water_basin_litter_missed", "Electronics Store License": "license_complaint_illegal_violation", "Ready NY - Spanish - Pocket Size": "english_emergency_spanish_chinese", "Wood Pole Damaged": "damaged_sign_sidewalk_missing", "Vehicle": "order_property_inspection_condition", "Waterway-Floatables (IHC)": "water_basin_litter_missed", "Basement": "damaged_sign_sidewalk_missing", "Bill Received in Error": "license_complaint_illegal_violation", "Refund/Credit Info or Status": "license_complaint_illegal_violation", "Plate Noisy/Sunken/Raised (SB5)": "order_property_inspection_condition", "Fixture/Luminaire Damaged": "damaged_sign_sidewalk_missing", "Ready NY - English - Full Size": "english_emergency_spanish_chinese", "Commercial J51 Exemption": "exemption_commercial_tax_business", "Insurance Information Requested": "license_complaint_illegal_violation", "Puddle on Roof": "order_property_inspection_condition", "Exchange/Refund/Return": "exemption_commercial_tax_business", "Performance": "order_property_inspection_condition", "Pet/Animal": "noise_animal_truck_dead", "Noise: Private Carting Noise (NQ1)": "noise_animal_truck_dead", "Fire Alarm Lamp Missing": "damaged_sign_sidewalk_missing", "Tow Truck Driver License": "license_complaint_illegal_violation", "Blocked Hydrant": "water_basin_litter_missed", "EFT or Online Payment Problem": "license_complaint_illegal_violation", "Lead Kit Request (Residential) (L10)": "order_property_inspection_condition", "15R Street Cond/Ref.W Door": "damaged_sign_sidewalk_missing", "Chained": "damaged_sign_sidewalk_missing", "Tobacco Retail Dealer License Application": "license_complaint_illegal_violation", "E15 Illegal Postering": "license_complaint_illegal_violation", "Update Tenant Information": "license_complaint_illegal_violation", "Sports Equipment": "order_property_inspection_condition", "Secondhand Dealer Firearms License": "license_complaint_illegal_violation", "Dirt, Debris, Litter Complaint": "order_property_inspection_condition", "BBQ Outside Authorized Area": "license_complaint_illegal_violation", "Ready NY My Emergency Plan - Polish": "english_emergency_spanish_chinese", "Citywide Procurement": "license_complaint_illegal_violation", "CABINET": "damaged_sign_sidewalk_missing", "Hurricane Preparedness - English": "english_emergency_spanish_chinese", "Sustainability Enforcement Work Order": "license_complaint_illegal_violation", "Bird Bath": "noise_animal_truck_dead", "Individual Process Server License": "license_complaint_illegal_violation", "Graffiti or Vandalism": "damaged_sign_sidewalk_missing", "WiFi/Internet Not Working/Slow": "damaged_sign_sidewalk_missing", "SEP - Professional Certification Compliance Audit": "license_complaint_illegal_violation", "Det-Sens Cabinet": "order_property_inspection_condition", "Disruptive Passenger": "damaged_sign_sidewalk_missing", "Driver Complaint - Non Passenger": "license_complaint_illegal_violation", "Bikes in Buildings": "damaged_sign_sidewalk_missing", "Illegal. Commercial Use In Resident Zone": "license_complaint_illegal_violation", "Electronic Fund Transfer (EFT) Problem": "license_complaint_illegal_violation", "General Complaint": "license_complaint_illegal_violation", "Cigarette Retail Dealer License": "license_complaint_illegal_violation", "Green Roof or Solar Panel Exemption": "exemption_commercial_tax_business", "Not Received - Vending Machine": "license_complaint_illegal_violation", "Billing Name Incorrect": "license_complaint_illegal_violation", "Reflector/Louvre": "damaged_sign_sidewalk_missing", "Birth/Death Certificates": "license_complaint_illegal_violation", "Dust from Construction": "order_property_inspection_condition", "Building Foundation": "damaged_sign_sidewalk_missing", "St Name - Over Intersection": "damaged_sign_sidewalk_missing", "Traffic Signal Light": "damaged_sign_sidewalk_missing", "Grease In Sewer/Catch Basin (IDG)": "water_basin_litter_missed", "Concrete Barrier": "damaged_sign_sidewalk_missing", "Lamppost Damaged": "damaged_sign_sidewalk_missing", "SRO - Illegal Work/No Permit/Change In Occupancy/Use": "license_complaint_illegal_violation", "Street Light Feed": "damaged_sign_sidewalk_missing", "Summer Heat - Russian": "english_emergency_spanish_chinese", "Sewage Odor": "odor_food_air_smoke", "Sign Blocked by Tree": "damaged_sign_sidewalk_missing", "Aided/Injury": "damaged_sign_sidewalk_missing", "Wasting Faucets,Sinks,Flushometer,Urinal,Etc. - Other (CWO)": "water_basin_litter_missed", "Chemical Vapors/Gases/Odors": "odor_food_air_smoke", "Pothole": "order_property_inspection_condition", "Biking/Rollerblading off Path": "damaged_sign_sidewalk_missing", "Unincorporated Business Tax - Refund": "exemption_commercial_tax_business", "ABANDONED APARTMENT UNIT": "order_property_inspection_condition", "On Structure": "damaged_sign_sidewalk_missing", "Property Value Dispute": "order_property_inspection_condition", "Rough, Pitted or Cracked Roads": "order_property_inspection_condition", "Dirty/Graffiti": "order_property_inspection_condition", "Payment Not Posted": "license_complaint_illegal_violation", "Application Appeal": "license_complaint_illegal_violation", "Budget": "order_property_inspection_condition", "Debt Not Owed": "license_complaint_illegal_violation", "Inadequate Support Shoring": "damaged_sign_sidewalk_missing", "Planted Less Than 2 Years Ago": "water_basin_litter_missed", "Ready NY - English - Pocket Size": "english_emergency_spanish_chinese", "1RE Recycling Electronics": "water_basin_litter_missed", "Disabled Device Dealer": "license_complaint_illegal_violation", "Drag Racing": "order_property_inspection_condition", "NYC.gov Web Site": "english_emergency_spanish_chinese", "Ready NY - Chinese Traditional - Pocket Size": "english_emergency_spanish_chinese", "Mssg Sign Multi Lamp": "damaged_sign_sidewalk_missing", "Electrical Enforcement Work Order (DOB)": "license_complaint_illegal_violation", "Advice Request": "order_property_inspection_condition", "Credit Card Stuck in Meter": "license_complaint_illegal_violation", "Unauthorized Tree Removal": "license_complaint_illegal_violation", "Mast Arm": "damaged_sign_sidewalk_missing", "Hydrant Locking Device Request (Use Comments) (WC5)": "water_basin_litter_missed", "Bent/Loose": "damaged_sign_sidewalk_missing", "Laundry Jobber License": "license_complaint_illegal_violation", "Extra Parts": "damaged_sign_sidewalk_missing", "Bracket Arm Loose": "damaged_sign_sidewalk_missing", "Mandatory Tip": "order_property_inspection_condition", "Filing and Technical Issues": "license_complaint_illegal_violation", "Street Light Out": "damaged_sign_sidewalk_missing", "Genealogy Research Application": "order_property_inspection_condition", "Price Not Posted": "license_complaint_illegal_violation", "Non-Public Schools": "exemption_commercial_tax_business", "Education Support, Policy, and Practice": "english_emergency_spanish_chinese", "Snow Emergency": "order_property_inspection_condition", "Apply Payment or Credit": "license_complaint_illegal_violation", "Fixture/Luminaire Hanging": "damaged_sign_sidewalk_missing", "RADIATOR": "order_property_inspection_condition", "Unincorporated Business Tax - Other": "exemption_commercial_tax_business", "Hurricane Preparedness - Chinese": "english_emergency_spanish_chinese", "Adjacent Buildings Not Protected": "damaged_sign_sidewalk_missing", "Water Meter Broken/Leaking - Private Residence (CMR)": "water_basin_litter_missed", "Ready NY - Haitian Creole - Full Size": "english_emergency_spanish_chinese", "Decorative Necklace Lighting": "damaged_sign_sidewalk_missing", "Air: Odor/Fumes, Vehicle Idling (AD3)": "odor_food_air_smoke", "Defacement": "order_property_inspection_condition", "DRY WEATHER DISCHARGE - DWD": "water_basin_litter_missed", "Card - No DOF Confirmation Number Issued": "license_complaint_illegal_violation", "Sewer Break (SBR)": "water_basin_litter_missed", "Air: Odor/Fumes, Dry Cleaners (AD1)": "odor_food_air_smoke", "ER2 Resident Recyc. (Tenant)": "license_complaint_illegal_violation", "Flashing Hazard": "damaged_sign_sidewalk_missing", "EXPY Fixture": "damaged_sign_sidewalk_missing", "Clear Street Light": "damaged_sign_sidewalk_missing", "Multi Agency Joint Inspection": "order_property_inspection_condition", "Tree Trunk Split": "damaged_sign_sidewalk_missing", "Monkey": "noise_animal_truck_dead", "Construction Safety Compliance Action": "order_property_inspection_condition", "Deck Inspection": "order_property_inspection_condition", "SEWAGE": "water_basin_litter_missed", "Plate Condition - Noisy": "noise_animal_truck_dead", "Other (complaint details)": "license_complaint_illegal_violation", "No Bill of Rights": "license_complaint_illegal_violation", "Demolition - Unsafe": "order_property_inspection_condition", "Property Misclassified": "order_property_inspection_condition", "Remove Hydrant Locking Device (WC6)": "water_basin_litter_missed", "To FDNY Approved System": "license_complaint_illegal_violation", "Gender Pricing": "exemption_commercial_tax_business", "Laundry License": "license_complaint_illegal_violation", "Debris - Excessive": "order_property_inspection_condition", "Horse Drawn Carriage Driver License": "license_complaint_illegal_violation", "Unsafe Use of Playground": "order_property_inspection_condition", "Mailed - Not Reflected": "damaged_sign_sidewalk_missing", "City Rebate": "exemption_commercial_tax_business", "ECR Commercial Routing Sticker": "license_complaint_illegal_violation", "Waterway-Color (IHD)": "water_basin_litter_missed", "Other Hazmats": "order_property_inspection_condition", "Plumbing Work - Unlicensed/Illegal/Improper Work In Progress": "license_complaint_illegal_violation", "Illegal Conversion Of Manufacturing/Industrial Space": "license_complaint_illegal_violation", "No Status Call": "damaged_sign_sidewalk_missing", "Sediment": "water_basin_litter_missed", "Glassware Hanging": "damaged_sign_sidewalk_missing", "Landmark Bldg - Illegal Work": "license_complaint_illegal_violation", "Ready NY- Pandemic Flu": "english_emergency_spanish_chinese", "Unsecured Facility": "order_property_inspection_condition", "Trespassing": "order_property_inspection_condition", "Manhole Sunken/Damaged/Raised (SB1)": "water_basin_litter_missed", "Air: Smoke, Chimney or vent (AS1)": "odor_food_air_smoke", "Puddle on Sidewalk": "water_basin_litter_missed", "Finance Business Center - Not Reflected": "license_complaint_illegal_violation", "Dead/Dying Tree": "damaged_sign_sidewalk_missing", "ACRIS Incorrect": "damaged_sign_sidewalk_missing", "Wireless Antenna": "damaged_sign_sidewalk_missing", "Debt Collection Agency": "license_complaint_illegal_violation", "Communications/Intergovernmental": "damaged_sign_sidewalk_missing", "Pesticide": "odor_food_air_smoke", "Overcharge": "order_property_inspection_condition", "Temporary Tattoo License": "license_complaint_illegal_violation", "Noise: Construction Equipment (NC1)": "noise_animal_truck_dead", "Broken Glass": "damaged_sign_sidewalk_missing", "Do Not Block the Box": "damaged_sign_sidewalk_missing", "Nuisance/Truant": "noise_animal_truck_dead", "Ready NY - Spanish - Full Size": "english_emergency_spanish_chinese", "Scale Dealer or Repairer License": "license_complaint_illegal_violation", "Possible Water Main Break (Use Comments) (WA1)": "water_basin_litter_missed", "Hurricane Preparedness - Haitian Creole": "english_emergency_spanish_chinese", "Broken Lock": "damaged_sign_sidewalk_missing", "Noise: Vehicle (NR2)": "noise_animal_truck_dead", "Property Refunds and Credits": "exemption_commercial_tax_business", "Odor In Sewer/Catch Basin (ICB)": "odor_food_air_smoke", "Personal Crime Victim or Good Samaritan Exemption": "exemption_commercial_tax_business", "ER4 City Agency (Inst. Recycling)": "order_property_inspection_condition", "Broken Window": "damaged_sign_sidewalk_missing", "Fire Hydrant Emergency (FHE)": "water_basin_litter_missed", "Food Spoiled": "odor_food_air_smoke", "Rodent Sighting": "noise_animal_truck_dead", "Sandy: Building Destroyed": "damaged_sign_sidewalk_missing", "Taste/Odor, Bitter/Metallic (QA3)": "odor_food_air_smoke", "Damaged or Missing Ad Box": "damaged_sign_sidewalk_missing", "Rent Discrepancy": "license_complaint_illegal_violation", "Facade (LL11/98)- Unsafe Notification": "damaged_sign_sidewalk_missing", "Homestead": "damaged_sign_sidewalk_missing", "Dog": "noise_animal_truck_dead", "Illegal Hotel Rooms In Residential Building": "damaged_sign_sidewalk_missing", "General Vendor Distributor License": "license_complaint_illegal_violation", "Recycling Electronics": "water_basin_litter_missed", "Cash Assistance": "order_property_inspection_condition", "Cable": "damaged_sign_sidewalk_missing", "Snow Removal": "order_property_inspection_condition", "STAIRS": "damaged_sign_sidewalk_missing", "Damaged Leg or Pole Bent": "damaged_sign_sidewalk_missing", "Det-Sens Amplifier": "noise_animal_truck_dead", "Warning Signal Lamp": "damaged_sign_sidewalk_missing", "Food Contaminated": "odor_food_air_smoke", "Photocell (PEC) Missing": "damaged_sign_sidewalk_missing", "Asbestos Complaint (B1)": "license_complaint_illegal_violation", "Structure - Outdoors": "damaged_sign_sidewalk_missing", "Bicycle Chained to Tree": "damaged_sign_sidewalk_missing", "Facility Maintenance": "order_property_inspection_condition", "Trees and Sidewalks Program": "damaged_sign_sidewalk_missing", "Taste/Odor, Chlorine (QA1)": "odor_food_air_smoke", "Material Storage - Unsafe": "order_property_inspection_condition", "Retaining Wall Tracking Complaint": "damaged_sign_sidewalk_missing", "DCP/BSA Compliance Inspection": "license_complaint_illegal_violation", "Property - Other Billing Issue": "license_complaint_illegal_violation", "Sidewalk Blocked": "damaged_sign_sidewalk_missing", "Broken Sidewalk": "damaged_sign_sidewalk_missing", "Unauthorized Bus Layover": "license_complaint_illegal_violation", "Enclosure Cap": "order_property_inspection_condition", "Engine Idling": "noise_animal_truck_dead", "Guide Rail": "damaged_sign_sidewalk_missing", "Waterway-Sewage (IHA)": "water_basin_litter_missed", "Tow Truck Exemption License": "exemption_commercial_tax_business", "Natural Gas In Sewer/Catch Basin (IFB)": "water_basin_litter_missed", "Cell Phone Store": "order_property_inspection_condition", "With License Plate": "order_property_inspection_condition", "Retail Store": "order_property_inspection_condition", "Commercial Other Exemption": "exemption_commercial_tax_business", "Failure to Comply with Vacate Order": "license_complaint_illegal_violation", "Boiler - Defective/Inoperative/No Permit": "odor_food_air_smoke", "Sidewalk Consultation": "damaged_sign_sidewalk_missing", "Roots Damaged": "damaged_sign_sidewalk_missing", "Noise: air condition/ventilation equipment (NV1)": "noise_animal_truck_dead", "Controller": "damaged_sign_sidewalk_missing", "Trunk Damaged": "damaged_sign_sidewalk_missing", "Application Renewal": "license_complaint_illegal_violation", "Labor violation": "license_complaint_illegal_violation", "Plumbing Work - Illegal/No Permit/Standpipe/Sprinkler": "license_complaint_illegal_violation", "Highway Flooding (SH)": "water_basin_litter_missed", "The ABCs of Housing - Spanish": "english_emergency_spanish_chinese", "Unlicensed": "license_complaint_illegal_violation", "Lane Station": "damaged_sign_sidewalk_missing", "Defective Streetlight": "damaged_sign_sidewalk_missing", "Catch Basin Grating Missing (SA4)": "water_basin_litter_missed", "Noise: Loud Music/Daytime (Mark Date And Time) (NN1)": "noise_animal_truck_dead", "Inaccurate Meter": "order_property_inspection_condition", "Branches Damaged": "damaged_sign_sidewalk_missing", "Broken Fence": "damaged_sign_sidewalk_missing", "Sidewalk Caf\u00c3\u00a9": "damaged_sign_sidewalk_missing", "Street Fair Vendor License": "license_complaint_illegal_violation", "List of Outstanding Tickets": "order_property_inspection_condition", "ELECTRIC/GAS RANGE": "odor_food_air_smoke", "Administration": "damaged_sign_sidewalk_missing", "1RG Missed Recycling Paper": "water_basin_litter_missed", "Guard Rail - Bridge": "damaged_sign_sidewalk_missing", "Turn Signal": "damaged_sign_sidewalk_missing", "Rough Pavement": "order_property_inspection_condition", "Best - DM Tracking Complaint": "license_complaint_illegal_violation", "RAIN GARDEN DEBRIS (SRGDBR)": "water_basin_litter_missed", "LIGHTING": "damaged_sign_sidewalk_missing", "Ready NY My Emergency Plan - Traditional Chinese": "english_emergency_spanish_chinese", "Elevator - Dangerous Condition/Shaft Open/Unguarded": "order_property_inspection_condition", "E7 Private Carter Spillage": "water_basin_litter_missed", "Personal DHE Exemption": "exemption_commercial_tax_business", "Oil, Grease In Water (QD1)": "water_basin_litter_missed", "Damaged Toilet/Sink": "water_basin_litter_missed", "Time Switch": "damaged_sign_sidewalk_missing", "NO WATER - WNW": "water_basin_litter_missed", "Dead Animal": "noise_animal_truck_dead", "Cloudy Or Milky Water (QB1)": "water_basin_litter_missed", "8 Request to Clean Vacant Lot": "order_property_inspection_condition", "ER6 Comm. Recyc. (Comm. Tenant)": "license_complaint_illegal_violation", "Electrical - Unlicensed/Illegal/Improper Work In Progress": "license_complaint_illegal_violation", "Accident/Explosion - Boiler": "odor_food_air_smoke"}
    
    service_data = service_data.with_columns(
        pl.col("Descriptor").replace(doc_to_topic_map).alias("DG") # DG Shorthand for descriptor Groups
    )
    
    
    # One Hot Encode Features
    cat_features = ["AG", "Borough", "DG"]
    service_data = service_data.to_dummies(columns=cat_features)
    
    
    # Group by Date and create our Category Feature Vector
    cat_df = service_data.rename({"Created Date": "Datetime"}).group_by("Datetime").agg(
        # Categorical Features Sum
        pl.col('^AG_.*$').sum(),
        pl.col('^Borough_.*$').sum(),
        pl.col('^DG_.*$').sum(),
    ).sort(by="Datetime")
    
    # Concat our category features to our current dataframe
    sd_df = pl.concat([sd_df, cat_df.drop("Datetime")], how="horizontal")
    
    # Now that our dataframe is significantly reduced in size
    # We can finally convert back to a pandas dataframe
    # as pandas is usable across more python packages
    sd_df = sd_df.to_pandas()
    
    # Set index to datetime
    sd_df = sd_df.set_index("Datetime")
    
    # NOTE we added 7 new rows to our weather df 
    # These 7 new rows will essentially be our final pred set
    # The Target for these rows will be null -> indicating it needs to be predicted
    # Add these rows to the service dataframe
    preds_df = pd.DataFrame({'Datetime': pd.date_range(start=sd_df.index[-1], periods=8, freq='D')})[1:]
    sd_df = pd.concat([sd_df, preds_df.set_index("Datetime")], axis=0)

    return sd_df
        

# 1b. Create Dataset (Wrap preprocessing into functions)

In [ ]:
# Build both datasets from file here
from utils import build_service_data
sd_df = build_service_data("data/311-2016-2018.csv")

from utils import build_weather_data
wd_df = build_weather_data("data/weather_NY_2010_2018Nov.csv")

# Lets define our current features
FEATURES = {
    "y": ["Target"],
    "num": ["num_closed_tickets"],
    "cat": ["AG_*", "Borough_*", "DG_*"],
    "time": ["Year", "Month", "Day", "DayOfWeek", "DayOfYear", "is_weekend", "is_holiday", "Season"],
    "weather": list(wd_df.columns)
}

# MERGE
data_merged = pd.concat([sd_df, wd_df], axis=1)
data_merged = build_temporal_features(data_merged, "Datetime")

# data_merged.to_csv("data/data_merged_full.csv")
# data_merged.loc[data_merged.Year <= 2018].to_csv("data/data_merged.csv")

# 2. EDA

Please view graphs using the [gradio application](https://dna-casestudy.com/)<br><br>
For Key Takeaways from this section view final section below

In [ ]:
data_merged = data_merged.set_index("Datetime")

## Univariate

Please view graphs using the [gradio application](https://dna-casestudy.com/)

In [ ]:
# Can view plots using this function
# May need to update jupyter-lab and install plotly to view these functions
# OR use VSCode
from utils import plot_timeseries
data_df = data_merged.loc[data_merged.Year <= 2018]
plot_timeseries(data_df, "MeanTemp", data_name="Weather")

## Bivariate

We will mainly focus on the relationships between Target and Variables, as well as any collinearity.<br>
Please view graphs using the [gradio application](https://dna-casestudy.com/)

In [ ]:
# Can view plots using this function
# May need to update jupyter-lab to view these functions
# OR use VSCode
from utils import plot_bivariate
data_df = data_merged.loc[(data_merged["Year"] >= 2016) & (data_merged["Year"] <= 2018)]
plot_bivariate(data_df, "Target", "MeanTemp", subset="Year")

## Seasonality

We use these main variables to test for seasonality:
* Year
* Season
* Month
* Day of Week
* Weekend
* Holiday
* Rain
* SnowIce

Please view graphs using the [gradio application](https://dna-casestudy.com/)

In [ ]:
from utils import plot_seasonality
data_df = data_merged.loc[(data_merged["Year"] >= 2016) & (data_merged["Year"] <= 2018)]
plot_seasonality(data_merged, "Year", "Target", show_box=True, show_outliers=False)

## Correlation

Please view graphs using the [gradio application](https://dna-casestudy.com/)

In [ ]:
from utils import plot_correlations, plot_all_correlations, plot_autocorr
data_df = data_merged.loc[(data_merged["Year"] >= 2016) & (data_merged["Year"] <= 2018)]

# Example of two plots below, but this can be viewed in the gradio app. Uncomment code sequentially to view
# plot_autocorr(data_df, "Target", np.log)
# plot_correlations(data_df, "Target", "num_closed_tickets", lags=[0,1,2,3,4,5,6,7,8,13,14,15,21], method="pearson")

View Correlations (Can be viewed more easily in [gradio application](https://dna-casestudy.com/))

In [ ]:
plot_all_correlations(data_df, "service", method="pearson")

In [ ]:
plot_all_correlations(data_df, "weather", method="pearson")

## Key Takeaways

* Missing Values
  * Gust if used may need interpolation to fill missing values
* Stationarity:
  * Weather variables exhibit various levels of non-stationarity (mostly based on trend but some constant)
    * Trends are clear for some like Temperature and DewPoint
    * Possible cause of constant non-stationarity are factors such as global warming
  * 311 Calls may exhibit some forms of weekly non-stationarity
    * Potentially weekly and monthly non-stationarity
    * Affected by Holidays and Weekends
    * More robust tests needed
  * Action Item: Test for stationarity and remove
* Bivariate Interactions:
  *  311 Calls have stronger relationships with certain Agency, Borough and Descriptor categories
  *  Holistically, 311 calls exhibit weak linear relationships with weather variables
    *  Broken down by month or season, relationship is strongest in winter months
    *  Month Of January: strongest linear relationship between MinTemp, DewPoint
* Seasonality:
  * Weather variables exhibit a strong Yearly and Seasonal seasonality
  * 311 Service Variables exhibit Weekly Seasonality
  * 311 Variables affected strongly by holidays and weekends (less 311 calls on weekends and holidays)
* Correlation:
  * Heavy Collinearity among weather variables (especially Min, Mean, MaxTemp)
  * Varying degrees of correlation among 311 service covariates with 311 service calls e.g. Target
* Lags & Autocorrelation:
  * 311 Service Calls have highest correlation with 7,14,21 weekly lags
  * 6,8 day lag intervals second strongest relationship. 8 day exhibits some negative correlation
  * 1 day lag exhibits similar correlation with 6,7 day lags

# 3. Feature Engineering

## Feature Selection based on the information gained in EDA
* Weather Covariates:
  * MaxSustainedWind: high correlation with Gust/Windspeed => REMOVE
  * MeanTemp, MaxTemp: High collinearity with MinTemp. MinTemp has highest correlation of 3 => REMOVE
    * Possible Reason: High temps, people stay indoors. A/C doesn't break nowadays. Lower Temps lead to building/tech failure more often
  * Percipitation: Bivariate plot shows weak relationship, outliers no effect on 311 => REMOVE
  * SnowDepth: Low Correlation, High number missing values => REMOVE
  * Rain, SnowIce: Binary variables, plots (look in Seasonality Tab) show weak relationship, SnowIce too heavily imbalanced 99% 0s => REMOVE
* 311 Service Covariates:
  * LOO (Leave One - or many - Out) Encoding:
    * Remove weakest features from our categorical covariates
    * Reduces bias and removes multicollinearity inherent to One-Hot Encoding
    * Candidates For Removal:
      * AG_Health, AG_Other: Lowest Correlation, lowest counts => REMOVE
      * AG_Parks: Lowest Correlation, but low multi-collinearity => KEEP
      * Borough_OTHER: Weakest Correlation, lowest count => REMOVE
      * DG_english_emergency, DG_exemption_commercial: Weakest Correlation, lowest counts => REMOVE
      * DG_odor_food_air_smoke: Lowest Count, but high correlation => KEEP

In [ ]:
data_preprocess = data_merged.loc[(data_merged["Year"] >= 2016)]
FEATURES = {
    "y": ["Target"],
    "past_covariates": [
        "num_closed_tickets",
        # Agency Groups
        'AG_Buildings', 'AG_Environment & Sanitation',
        'AG_Parks', 'AG_Security', 'AG_Transportation',
        # Boroughs
        'Borough_BRONX', 'Borough_BROOKLYN', 'Borough_MANHATTAN',
        'Borough_QUEENS', 'Borough_STATEN ISLAND',
        # Descriptor Groups
        'DG_damaged_sign_sidewalk_missing',
        'DG_license_complaint_illegal_violation',
        'DG_noise_animal_truck_dead',
        'DG_odor_food_air_smoke',
        'DG_order_property_inspection_condition',
        'DG_water_basin_litter_missed'
    ],
    "future_covariates":  [
        'DewPoint',
        'WindSpeed',
        'Gust',
        'MinTemp'
    ],
    "time": [
        "Year", "Month", "Day", "DayOfWeek",
        "DayOfYear", "is_weekend", "is_holiday", "Season"
    ]
}

ALL_FEATS = []
for category in FEATURES:
    ALL_FEATS.extend(FEATURES[category])

data_preprocess = data_preprocess.loc[:,ALL_FEATS].copy()

## Feature Preprocessing

### Impute Missing Values

The only feature with missing values is Gust. We can imput this using a simple imputation algorithm

In [ ]:
print("Features with missing values: ", list(data_preprocess.columns[data_preprocess.isna().sum() > 7]))

In [ ]:
data_preprocess["Gust_lin"] = data_preprocess["Gust"].interpolate(method="linear")
data_preprocess["Gust_spline3"] = data_preprocess["Gust"].interpolate(method="spline", order=3)
data_preprocess["Gust_spline5"] = data_preprocess["Gust"].interpolate(method="spline", order=5)
data_preprocess["Gust_quad"] = data_preprocess["Gust"].interpolate(method="quadratic")

In [ ]:
from utils import plot_gust_interpolation
fig = plot_gust_interpolation(data_preprocess)
# # Uncomment to show Fig
# fig

The graphs above show that the more robust interpolation methods (spline and quadratic) over estimate some points. You can see some values start to approach 0. Linear does the best job at not interpolating values outside of the current range.

In [ ]:
data_preprocess["Gust"] = data_preprocess["Gust"].interpolate(method="linear")

### Remove Stationarity

Stationary test results shown in the [gradio application](https://dna-casestudy.com/)

Use this function to test Stationarity.

In [ ]:
from utils import test_stationary
# for var in ALL_FEATS:
#     print(var)
#     display(test_stationary(data_preprocess, var))

#### Failed Tests: DewPoint & MinTemp

NOTE: Some of the categorical features were ignored to keep complexity as low as possible. <br>
Only real focus is to fix the numerical variables such as weather and target

In [ ]:
var = "MinTemp"
test_stationary(data_preprocess, var)

In [ ]:
data_preprocess["MinTemp_log"] = data_preprocess["MinTemp"].apply(np.log1p)
data_preprocess["MinTemp_log_diff7d"] = data_preprocess["MinTemp_log"] - data_preprocess["MinTemp_log"].shift(7)
test_stationary(data_preprocess, "MinTemp_log_diff7d")

In [ ]:
var = "DewPoint"
test_stationary(data_preprocess, var)

In [ ]:
data_preprocess["DewPoint_diff7d"] = data_preprocess["DewPoint"] - data_preprocess["DewPoint"].shift(7)
test_stationary(data_preprocess, "DewPoint_diff7d")

In [ ]:
# Perform the Transformation
data_preprocess["MinTemp"] = data_preprocess["MinTemp_log_diff7d"]
data_preprocess["DewPoint"] = data_preprocess["DewPoint_diff7d"]

## Feature Engineering

In this section, we use aggregations, lags and differences to compute features.<br>
**NOTE: We could easily incorporate many more variations of these features. To avoid suffering from the curse of dimensionality, we do as little as possible**

### Past Covariates

* Lags: Based on EDA our data has weekly variations, lags based on week intervals
  * Use 7day, 14day, 21day lags
* Rolling: (Shifted 7 Days forward)
  * Mean Through 14 days
* Differencing: (7D difference = 7D lag - 14D lag)
  * 7 Day Difference

In [ ]:
FEATURES["past_covariates_final"] = []
for col in FEATURES["past_covariates"]:
    new_features = data_preprocess[col].to_frame().copy()
    # Lag Features
    new_features[col+"_L7D"] = new_features[col].shift(7)
    new_features[col+"_L14D"] = new_features[col].shift(14)
    new_features[col+"_L21D"] = new_features[col].shift(21)

    # Rolling Features
    # Shift to move the new features into the prediction space (2019-01-01 to 2019-01-07)
    new_features[col+"_RMean14D"] = new_features[col].shift(7).rolling('14D').mean()

    # Differencing Features
    # Shift to move the new features into the prediction space (2019-01-01 to 2019-01-07)
    new_features[col+"_Diff7D"] = (new_features[col].shift(7) - new_features[col].shift(7).shift(7))

    FEATURES["past_covariates_final"].extend([col+"_L7D", col+"_L14D", col+"_L21D", col+"_RMean14D", col+"_Diff7D"])
    new_features = new_features.drop(columns=col)
    data_preprocess = pd.concat([data_preprocess, new_features], axis=1)

assert len(data_preprocess.loc[:, FEATURES["past_covariates_final"]].columns) == len(FEATURES["past_covariates"])*5

### Future Covariates

* Lags: 0D, 1D, 2D, 7D only
* Rolling: Mean and Min of last 14D
* Expanding Window: Max, Min (min-length of 14)
* Differencing already performed to remove trends

In [ ]:
FEATURES["future_covariates_final"] = []
for col in FEATURES["future_covariates"]:
    new_features = data_preprocess[col].to_frame().copy()
    # Lag Features
    new_features[col+"_L0D"] = new_features[col].shift(0)
    new_features[col+"_L1D"] = new_features[col].shift(1)
    new_features[col+"_L2D"] = new_features[col].shift(2)

    # Rolling Features (No shift needed for future vars)
    new_features[col+"_RMean14D"] = new_features[col].rolling('14D').mean()
    new_features[col+"_RMin14D"] = new_features[col].rolling('14D').min()

    # Expanding Window (No shift needed for future vars)
    new_features[col+"_EMean14D"] = new_features[col].expanding(min_periods=14).mean()
    new_features[col+"_EMin14D"] = new_features[col].expanding(min_periods=14).min()
    
    FEATURES["future_covariates_final"].extend([col+"_L0D", col+"_L1D", col+"_L2D", col+"_RMean14D", col+"_RMin14D", col+"_EMean14D", col+"_EMin14D"])
    new_features = new_features.drop(columns=col)
    data_preprocess = pd.concat([data_preprocess, new_features], axis=1)

assert len(data_preprocess.loc[:, FEATURES["future_covariates_final"]].columns) == len(FEATURES["future_covariates"])*7

### Target Variable

* Lags: 1D, 6D, 7D, 8D, 14,
* Differencing: 7D, 14D

In [ ]:
FEATURES["y_features"] = []
col = FEATURES["y"][0]
new_features = data_preprocess[col].to_frame().copy()

# Lag Features
new_features[col+"_L1D"] = new_features[col].shift(1)
new_features[col+"_L6D"] = new_features[col].shift(6)
new_features[col+"_L7D"] = new_features[col].shift(7)
new_features[col+"_L8D"] = new_features[col].shift(8)
new_features[col+"_L14D"] = new_features[col].shift(14)

# Differencing features
new_features[col+"_Diff7D"] = (new_features[col].shift(1) - new_features[col].shift(1).shift(7))
new_features[col+"_Diff14D"] = (new_features[col].shift(1) - new_features[col].shift(1).shift(14))

new_features = new_features.drop(columns=col)
FEATURES["y_features"].extend([col+"_L1D", col+"_L6D", col+"_L7D", col+"_L8D", col+"_L14D", col+"_Diff7D", col+"_Diff14D"])
data_preprocess = pd.concat([data_preprocess, new_features], axis=1)

assert len(data_preprocess.loc[:, FEATURES["y_features"]].columns) == len(FEATURES["y"])*7

# Model

In [ ]:
# Reload features
all_features = ["Target"]
all_features.extend(list(np.append(np.append(FEATURES["y_features"],FEATURES["future_covariates_final"]),FEATURES["past_covariates_final"])))
data_final = data_preprocess.loc[:,all_features]
data_final = build_temporal_features(data_final, "Datetime")
data_final = data_final.set_index("Datetime")

# One hot encode season
data_final[data_final["Season"].str.get_dummies().columns] = data_final["Season"].str.get_dummies()
data_final = data_final.drop(columns="Season")

In [ ]:
# data_final.to_csv("data/data_final.csv")

## Train, Validation, Test splitting

In [ ]:
# Test set
test = data_final[-7:].copy()

# Dataset for training
# Need to store this to compute new features
dataset = data_final[:-7].copy()

# Splitting data for Time-Series, based on time not random samples
# Take 75% of our data for training and the last 25% for validation
split_point = int(len(data_final[:-7])*0.75)
train, val = dataset[:split_point], dataset[split_point:]

In [ ]:
X_train, y_train = train.drop(columns="Target"), train["Target"]
X_val, y_val = val.drop(columns="Target"), val["Target"]
X_test, y_test = test.drop(columns="Target"), test["Target"]

In [ ]:
from utils import plot_train_split

plot_train_split(train, val)

## Model Structure

In favor of using a simple, but fast and efficient model. I choose to use an XGBoost model for regression. Below are the model parameters I will use.

In [ ]:
import torch
from sklearn.metrics import r2_score, mean_absolute_percentage_error
import xgboost as xgb

device = "cuda" if torch.cuda.is_available() else "cpu"

# MAPE is a good metric for forecasting as it allows us to see an average deviation in percentage form
# Goal is to minimize MAPE
# A score of < 0.1 is good
metric = "mape"

# Testing parameters, these showed the best results
# Trick is to make sure we are not overfitting
model = xgb.XGBRegressor(
    n_estimators=500,
    early_stopping_rounds=50,
    objective='reg:squarederror',
    device=device,
    max_depth=3,
    learning_rate=0.01,
    eval_metric="mape",
    reg_lambda=2,
    importance_type="gain",
    random_state=22,
)

## Training

In [ ]:
_ = model.fit(
    X_train, y_train,
    eval_set=[(X_train, y_train), (X_val, y_val)],
    verbose=True
)

# Model Evaluation

### Model Prediction

In [ ]:
from utils import plot_predictions

In [ ]:
# Train scores:
preds_train = model.predict(X_train)
r2 = r2_score(train["Target"], preds_train)
mape = mean_absolute_percentage_error(train["Target"], preds_train)
print(f"Model R2: {r2}")
print(f"Model MAPE: {mape}")

In [ ]:
# Validation scores:
preds_val = model.predict(X_val)
val["Prediction"] = preds_val
r2 = r2_score(val["Target"], val["Prediction"])
mape = mean_absolute_percentage_error(val["Target"], val["Prediction"])
print(f"Model R2: {r2}")
print(f"Model MAPE: {mape}")

fig = plot_predictions(train, val, preds_val)

### Feature Importance

In [ ]:
from utils import plot_final_feature_importance

fig = plot_final_feature_importance(model)
fig

## Final Prediction

In [ ]:
# First we should fit on the full dataset so our model is most trained
final_model = model.fit(
    dataset.drop(columns="Target"), dataset["Target"],
    eval_set=[(dataset.drop(columns="Target"), dataset["Target"])],
    verbose=True
)
# final_model.save_model('models/final_model.json')

In [ ]:
X_test, y_test = test.drop(columns="Target"), test["Target"]

## Recursive Model Prediction

This function is my implementation of a recursive model predictions.<br>
The model makes a prediction, uses that prediction to fill the missing values of the next set of features, then it predicts again.<br>
Process loops until all predictions have been made.

In [ ]:
def predict_recurse(dataset, test, model, features_to_impute=['Target_L1D', 'Target_Diff7D', 'Target_Diff14D'], last_feature='Target_L6D'):
    n_steps = len(test)
    merged_data = pd.concat([dataset[-14:], test], axis=0)
    all_index = merged_data.index
    X_test = test.drop(columns="Target")
    sd = -6 # Starting point for filling next value

    # For each step, get the predictions
    for i in range(n_steps-1):
        pred = final_model.predict(X_test)[i]
        # For the three features needed, compute the new value
        X_test.loc[all_index[sd+i], features_to_impute[0]] = pred
        X_test.loc[all_index[sd+i], features_to_impute[1]] = pred - merged_data.loc[all_index[sd+i-7], features_to_impute[1]]
        X_test.loc[all_index[sd+i], features_to_impute[2]] = pred - merged_data.loc[all_index[sd+i-14], features_to_impute[2]]

        # In the last iteration compute the Lag6D value
        if i == 5:
            X_test.loc[all_index[sd+i], last_feature] = pred - merged_data.loc[all_index[sd+i-6], last_feature]


    final_preds = final_model.predict(X_test)
    return final_preds
            

In [ ]:
next_7_day_prediction = predict_recurse(dataset, test, final_model)

### Plot the final forecast

In [ ]:
fig = plt.subplots(figsize=(15, 5))
data_final.loc[data_final.index[-7:], "Target"]= next_7_day_prediction
ax = data_final.loc[data_final.index[-96:-6], "Target"].plot(label="Real", title="311 Service Volume: 7 Day Prediction")
data_final.loc[data_final.index[-7:], "Target"].plot(label="Forecast", ax=ax)
ax.legend()